In [1]:
import pandas as pd
import numpy as np
import re
from itertools import product, combinations, groupby, permutations, chain, combinations_with_replacement

In [2]:
model_input = "/Users/awaldrop/PycharmProjects/dfs_optimization_tools/data/harmonized_datasets/2019/before_contest/dfk_harm_wk12_2019.csv"

In [3]:
df = pd.read_csv(model_input)
df = df.sort_values(by="position").copy()
df.head(15)

player position team  opp  points_actual  salary  points_projected  \
312  Dolphins         D  MIA  CLE            2.9    2000          5.107000   
135  Steelers         D  PIT  CIN           12.0    4000          9.773429   
148    Browns         D  CLE  MIA            6.7    3800          9.106000   
152     Bears         D  CHI  NYG            8.3    3700          9.193714   
311   Bengals         D  CIN  PIT            3.0    2100          5.565000   
159   Raiders         D  OAK  NYJ            6.0    3600          8.662667   
166   Falcons         D  ATL   TB            4.2    3500          7.608000   
172     Bills         D  BUF  DEN            7.9    3400          8.278000   
185    Saints         D   NO  CAR            9.2    3300          9.332857   
194    Titans         D  TEN  JAX            8.6    3200          7.213714   
202     Lions         D  DET  WAS            5.3    3100          8.916000   
241  Redskins         D  WAS  DET            5.2    3000          6.063667   
188  Patriots         D   NE  DAL           18.5    3300          7.961429   
267    Giants         D  NYG  CHI            6.8    2900          6.714000   
308   Cowboys         D  DAL   NE            7.1    2300          4.966667   

     sdPts_projected  tier  
312         0.365541     4  
135         1.053053     1  
148         1.062528     1  
152         1.346438     1  
311         0.570241     4  
159         1.355047     2  
166         0.638099     2  
172         0.753414     2  
185         1.027862     1  
194         0.771403     2  
202         0.613430     1  
241         1.387349     3  
188         1.079358     2  
267         0.952355     3  
308         0.360278     5

In [4]:
from pulp import *
import math

In [5]:
def generate_player_ids(df):
    return pd.Series(["{0}_{1}_{2}".format(df.position[i], df.team[i], i) for i in range(len(df))])

In [6]:
def get_player_attribute_dict(df, attr):
    return dict(zip(df.player_id, df[attr]))

def get_players_by_position(df):
    return {pos: df[df.position == pos].player_id.tolist() for pos in df.position.unique()}

def get_players_by_team(df):
    return {team: df[df.team == team].player_id.tolist() for team in df.team.unique()}

def get_players_by_game(df):
    df = df.copy()
    def set_game(row):
        return "_".join(sorted([row.team, row.opp]))
    df["game"] = df.apply(set_game, axis=1)
    return {game: df[df.game == game].player_id.tolist() for game in df.game.unique()}

def get_matchups(df):
    matchups = set(["_".join(sorted([team, df[df.team == team].opp.tolist()[0]])) for team in df.team.unique()])
    return [matchup.split("_") for matchup in matchups]

def get_matchup_hash(df):
    return dict(zip(df.team, df.opp))

def get_players_by_team_position(df, pos):
    if not isinstance(pos, list):
        pos = [pos]
    return {team: df[(df.team == team) & (df.position.isin(pos))].player_id.tolist() for team in df.team.unique()}

def get_top_players_by_team_position(df, pos, num=1):
    if not isinstance(pos, list):
        pos = [pos]
    players = {}
    for team in df.team.unique():
        team_players = []
        for p in pos:
            tp = df[(df.team == team) & (df.position == p)].sort_values(by="points_projected").player_id.tolist()
            if tp:
                team_players.append(tp[-1])
        players[team] = team_players
    return players

def get_team_stacks(df, stack_position_dict, get_only_top_players=True):
    players = {}
    for team in df.team.unique():
        team_players = {}
        for stack_pos in stack_position_dict:
            num_to_get = stack_position_dict[stack_pos]
            stack_players = df[(df.team == team) & (df.position == stack_pos)].sort_values(by="points_projected").player_id.tolist()
            if get_only_top_players:
                team_players[stack_pos] = stack_players[-num_to_get:]
            else:
                team_players[stack_pos] = stack_players
        players[team] = team_players
    return players

def get_team_stacks(df, stack_position_dict,  point_diff_for_identical=0):
    players = {}
    for team in df.team.unique():
        team_players = {}
        for stack_pos in stack_position_dict:
            num_to_get = stack_position_dict[stack_pos]
            stack_players = df[(df.team == team) & (df.position == stack_pos)].sort_values(by="points_projected", ascending=False)
            # Add players that are identical to worst player currently in stack
            if len(stack_players) <= num_to_get:
                team_players[stack_pos] = stack_players.player_id[0:num_to_get].tolist()
            else:
                worst_player_in_stack_score = stack_players.points_projected.tolist()[num_to_get-1]
                team_players[stack_pos] = stack_players[stack_players.points_projected >= worst_player_in_stack_score-point_diff_for_identical].player_id.tolist()
        players[team] = team_players
    return players

def get_opp_stacks(df, stack_position_dict, point_diff_for_identical=0):
    team_stacks = get_team_stacks(df, stack_position_dict, point_diff_for_identical)
    for matchup in get_matchups(df):
        home_team = matchup[0]
        away_team = matchup[1]
        home_team_stack = team_stacks[home_team]
        away_team_stack = team_stacks[away_team]
        team_stacks[home_team] = away_team_stack
        team_stacks[away_team] = home_team_stack
    return team_stacks
                                
def get_players_and_positions_by_team(df):
    return {team: get_players_by_position(df[df.team == team]) for team in df.team.unique()}

In [7]:
def smooth_player_scores_by_tier(df):
    for pos in df.position.unique():
        tiers = df[df.position == pos].tier.unique()
        for tier in tiers:
            df.loc[((df.position == pos) & (df.tier == tier)), 'points_projected'] = df[(df.position == pos) & (df.tier == tier)].points_projected.mean()
    return df  

In [8]:
def restrict_positions_from_opposing_teams(prob, df, _vars, exclude_pos):
    for game in get_matchups(df):
        home_team = game[0]
        away_team = game[1]
        players = get_players_and_positions_by_team(df)
        for home_team_pos, away_team_pos in permutations(exclude_pos, 2):
            if home_team not in players or away_team not in players:
                continue
            if home_team_pos not in players[home_team] or away_team_pos not in players[away_team]:
                continue
            home_team_variables = [_vars[player] for player in players[home_team][home_team_pos]]
            away_team_variables = [_vars[player] for player in players[away_team][away_team_pos]]
            for variables in product(home_team_variables, away_team_variables):
                prob += lpSum(variables) <= 1
    return prob

In [9]:
import collections

class InvalidStackError(BaseException):
    pass

class TeamStack:
    def __init__(self, stack_positions, stack_id=""):
        
        if not isinstance(stack_positions, list) or len(stack_positions) < 2:
            raise InvalidStackError("Invalid stack! Stack must be a list with at least 2 positions")
        
        self.id = "_".join(sorted(stack_positions)) if not stack_id else stack_id
        self.pos = [pos for pos in stack_positions if not pos.startswith("-") and not "/" in pos]
        
        # Determine if stack contains players from opposition team
        # E.g. [QB, -WR] means qb must be stacked with the WR he's facing
        self.opp_pos = [pos.replace("-", "") for pos in stack_positions if pos.startswith("-")]
        self.is_opp_stack = len(self.opp_pos) > 0
        self.total_positions = self.pos + self.opp_pos
        
        if len(self.pos) <= 0:
            raise InvalidStackError("{0} only specifies opponent positions! Must include a team to oppose!")

    @property
    def position_counts(self):
        return {pos: len([x for x in self.pos if x == pos]) for pos in self.pos}
    
    @property
    def opp_position_counts(self):
        return {pos: len([x for x in self.opp_pos if x == pos]) for pos in self.opp_pos}
    
    @property
    def total_counts(self):
        return {pos: len([x for x in self.total_positions if x == pos]) for pos in self.total_positions} 
    
    def __str__(self):
        return "Stack: {0}. Pos: {1}. Opp Pos: {2}".format(self.id, 
                                                          ", ".join(self.pos),
                                                          ", ".join(self.opp_pos))
    
class StackSet:
    def __init__(self, stacks, max_team_pos, max_per_team):
        
        self.max_team_pos = max_team_pos
        self.max_per_team = max_per_team 
        
        self.stacks = []
        self.flex_stacks = {}
        for i, stack in enumerate(stacks):
            stack_id = "{0}_{1}".format("_".join(stack), i)            
            # Enumerate sub-stacks if all possible stacks if stack contains flex positions
            if len([pos for pos in stack if "/" in pos]) > 0:
                split_stacks = self.expand_flexible_stack(stack)
                valid_stacks = 0
                for i, split_stack in enumerate(split_stacks):
                    
                    # Skip configurations with only opponent players as we know these are invalid
                    if len([pos for pos in split_stack if "-" in pos]) == len(split_stack):
                        continue
                        
                    # Only add split stack if it's valid. Eliminates permutations that
                    # violate team constraints
                    new_stack = TeamStack(split_stack, "{0}_{1}".format(stack_id,i))
                    try:
                        self._validate_stack(new_stack)
                        if stack_id in self.flex_stacks:
                            self.flex_stacks[stack_id].append(new_stack)
                        else:
                            self.flex_stacks[stack_id] = [new_stack]
                        valid_stacks += 1
                    except InvalidStackError as e:
                        # Don't add stacks that violate team constraints
                        print("Skipping invalid split stack: {0}".format(new_stack))
                        print(e)
                        
                # Raise error if all stacks from split stack were invalid
                if not valid_stacks:
                    raise InvalidStackError("Flex stack yielded 0 valid stacks: {0}".format(stack))

            # Otherwise just add the stack
            else:
                self.stacks.append(TeamStack(stack, stack_id))
                
        # Raise error if validation checking removed all split stacks
        if not self.stacks and not self.flex_stacks:
            raise InvalidStackError("No stack left after removing invalid stacks!")
                
        # Validate stack set
        self._validate_stack_set()
                
    def _validate_stack(self, stack):
        for pos in stack.total_positions:
            # Check position is a valid position
            if pos not in self.max_team_pos:
                raise InvalidStackError("(Stack: {0}) Invalid position: {1}".format(stack.id, pos))
                
            # Check stack doesn't exceed team position limits
            if len([x for x in stack.total_positions if x == pos]) > self.max_team_pos[pos]:
                raise InvalidStackError("(Stack: {0}) Number of {1} in stack exceed positionsl limits!".format(stack.id,
                                                                                                               pos))
        # Check to make sure stack doesn't exceed total team size
        if len(stack.pos) > self.max_per_team:
            raise InvalidStackError("Stack '{0}' is larger than max per single team ({1})!".format(stack.id,
                                                                                                   self.max_per_team))
        if len(stack.opp_pos) > self.max_per_team:
            raise InvalidStackError("Opp Stack '{0}' is larger than max per single team ({1})!".format(stack.id,
                                                                                                       self.max_per_team))
    def _validate_stack_set(self):
        for stack in self.stacks:
            print(stack)
            self._validate_stack(stack)
    
        for stack_id, flex_stacks in self.flex_stacks.items():
            for flex_stack in flex_stacks:
                print(flex_stack)
                self._validate_stack(flex_stack)
            
        # Validate combined stack players < max_team_pos
        for pos in self.max_team_pos:
            # Check all combinations of stack set to make sure no flex stacks violate team constraints
            dup_stacks = [self.flex_stacks[stack_id] for stack_id in self.flex_stacks]
            dup_stacks.append(self.stacks)
            for stack_combo in product(*dup_stacks):
                num_at_pos = sum([stack.total_counts[pos] for stack in list(stack_combo) if pos in stack.total_counts])
                if num_at_pos > self.max_team_pos[pos]:
                    raise InvalidStackError("Number of {0} across stacks exceeds positional limits!".format(pos))
    
    @staticmethod
    def expand_flexible_stack(stack_positions):
        # Get fixed team, opposing team positions
        fixed_pos = [pos for pos in stack_positions if "/" not in pos]
        
        # Get flexible team, opposing team positions
        #free_pos = [pos for pos in stack_positions if "/" in pos and ":" in pos and "-" not in pos]
        #free_opp_pos = [pos for pos in stack_positions if "/" in pos and ":" in pos and "-" in pos]
        free_pos = [pos for pos in stack_positions if "/" in pos and ":" in pos]
        
        # Enumerate possible stacks for team
        stack_combos = []
        for pos in free_pos:
            stack_combos.append(StackSet.expand_flex_pos(pos))
        
        # Enumerate possible stacks for opp team
        #for pos in free_opp_pos:
        #    stack_combos.append(StackSet.expand_flex_pos(pos))
            
        # Enumerate all possible combinations
        #stack_combos = stack_combos[0]
        if fixed_pos:
            stack_combos = [[pos] for pos in fixed_pos] + stack_combos
        stack_combos = [list(stack_combo) for stack_combo in product(*stack_combos)]
        for i in range(len(stack_combos)):
            stack_combos[i] = flatten(stack_combos[i])
        return stack_combos
    
    @staticmethod
    def expand_flex_pos(pos):
        pos_combos = set()
        num_to_choose = int(pos.split(":")[1])
        pos_to_choose = pos.split(":")[0].split("/")
        
        # Add negative sign to all positions if opposing stack
        #if "-" in pos:
        #    pos_to_choose = ["-{0}".format(pos.replace("-","")) for pos in pos_to_choose]
        
        # Dedup positions
        pos_to_choose = set(tuple(pos_to_choose))
        assert len(pos_to_choose) > 1, "Flexible stack {0} contains only one position! Need to specify at least two for flex stack!".format(pos)
        # Return combinations of positions
        for combo in combinations_with_replacement(pos_to_choose, num_to_choose):
            pos_combos.add(combo)
            
        return [list(combo) for combo in pos_combos]
    
def flatten(x):
    if isinstance(x, list):
        return [a for i in x for a in flatten(i)]
    else:
        return [x]
        

In [10]:
def enumerate_stack(df, stack, point_diff_for_identical=0):
    possible_stacks = {}
    stack_players = get_team_stacks(df, stack.position_counts,  point_diff_for_identical)
    
    # Add oppositional stacks if necessary
    if stack.is_opp_stack:        
        opp_stack_players = get_opp_stacks(df, stack.opp_position_counts, point_diff_for_identical)
        for team, players_by_pos in opp_stack_players.items():
            for pos, players in players_by_pos.items():
                stack_players[team]["-{0}".format(pos)] = opp_stack_players[team][pos]
    
    # Get hash indices of positions to include in stack
    pos_to_add = stack.pos + ["-{0}".format(pos) for pos in stack.opp_pos]
    
    # Get all potential stack combinations
    for team, players in stack_players.items():
        all_player_combinations = set()
        players_by_position = [players[pos] for pos in pos_to_add]
        for player_combination in product(*players_by_position):
            # Remove stacks with duplicate players
            if len(set(player_combination)) != len(stack.total_positions):
                continue
            # Sort to prevent duplicate stacks from being added
            player_combination = tuple([player for player in sorted(player_combination)])
            #player_combination = tuple(sorted(player_combination))
            all_player_combinations.add(player_combination)
        possible_stacks[team] = all_player_combinations
    return possible_stacks
    
def enumerate_stacks(df, stacks, point_diff_for_identical=0):
    possible_stacks = {}
    # Enumerate fixed stacks
    for stack in stacks.stacks:
        possible_stacks[stack.id] = enumerate_stack(df, stack, point_diff_for_identical)
    # Enumerate flex stacks
    for stack_id, flex_stack in stacks.flex_stacks.items():
        possible_stacks[stack_id] = {stack.id: enumerate_stack(df, stack, point_diff_for_identical) for stack in flex_stack}
        assert len(possible_stacks[stack_id]) == len(flex_stack)
    return possible_stacks

    
def add_stack(stack, possible_stacks, prob, _vars, team_stack_vars, matchup_hash):
    var_prefix = 'rules_{0}'.format(stack.id)
    stack_variables = []
    for team, player_stacks in possible_stacks.items():
        for player_stack in player_stacks:
            var_name = "{0}_{1}_{2}".format(var_prefix, 
                                                team,
                                                "_".join([player for player in player_stack]))
            var = LpVariable(var_name, cat="Binary")
            stack_variables.append(var)
            team_stack_vars[team].append(var)
            if stack.is_opp_stack:
                team_stack_vars[matchup_hash[team]].append(var)
            prob += lpSum([_vars[player] for player in player_stack]) >= var*len(player_stack)
        
    # Add constraint enforcing only one team can have the stack
    prob += lpSum(stack_variables) >= 1
    

def add_flex_stack(flex_stacks, possible_stacks, prob, _vars, team_stack_vars, matchup_hash):
    #var_prefix = 'rules_{0}'.format(flex_stacks[0].id)
    stack_variables = [] 
    for flex_stack in flex_stacks:
        for team, player_stacks in possible_stacks[flex_stack.id].items():
            for player_stack in player_stacks:
                var_name = "rules_{0}_{1}_{2}".format(flex_stack.id, 
                                                      team,
                                                      "_".join([player for player in player_stack]))
                var = LpVariable(var_name, cat="Binary")
                stack_variables.append(var)
                team_stack_vars[team].append(var)
                if flex_stack.is_opp_stack:
                    team_stack_vars[matchup_hash[team]].append(var)
                prob += lpSum([_vars[player] for player in player_stack]) >= var*len(player_stack)
                
    # Add constraint enforcing only one team can have the stack
    prob += lpSum(stack_variables) >= 1


def add_stacks(prob, df, _vars, stacks, point_diff_for_identical=0):
    # Initialize dict to hold team stack variables
    team_stack_vars = {team: [] for team in df.team.unique()}
    team_stack_var_names = {team: [] for team in df.team.unique()}
    
    # Get list of all possible stack player combinations for each stack
    possible_stacks = enumerate_stacks(df, stacks, point_diff_for_identical)
    matchup_hash = get_matchup_hash(df)
    
    # Add constraints for each team stack
    for stack in stacks.stacks:
        add_stack(stack, possible_stacks[stack.id], prob, _vars, team_stack_vars, matchup_hash)
    
    for stack_id, flex_stack in stacks.flex_stacks.items():
        add_flex_stack(flex_stack, possible_stacks[stack_id], prob, _vars, team_stack_vars, matchup_hash)
    
    # Add constraint that teams can have no more than 1 stack
    for team, team_stack_var in team_stack_vars.items():
        prob += lpSum(team_stack_var) <= 1
    return prob

def add_game_stacks(prob, df, _vars, game_stacks, players_by_pos):
    players_by_game = get_players_by_game(df)
    game_stack_vars = {game: [] for game in players_by_game}
    
    for i, game_stack in enumerate(game_stacks):
        if game_stack <= 1:
            raise IOError("Can't have a game stack less than 1 as that's not a stack!")
        game_vars = []
        for game, players in players_by_game.items():
            var_name = "gamestack_{0}_{1}".format(game, i)
            var = LpVariable(var_name, cat="Binary")
            game_vars.append(var)
            game_stack_vars[game].append(var)
                
            # Add constraint that at least one offensive player must be in game for game variable to be set
            prob += lpSum([_vars[player] for player in players if player not in players_by_pos["D"]]) >= game_stack*var

        # Add constraint that at least one game stack var must be set
        prob += lpSum(game_vars) >= 1     
        
    # Add constraints that 1 game can only satisfy one game stack
    for game, game_stack_vars in game_stack_vars.items():
        prob += lpSum(game_stack_vars) <= 1
    
    return game_stack_vars

def add_qb_game_stack(min_from_qb_game, prob, df, _vars, game_stacks, players_by_pos):
    players_by_game = get_players_by_game(df)    
    game_vars = []
    for game, players in players_by_game.items():
        qbs = [player for player in players if player in players_by_pos["QB"]]
        var_name = "qb_gamestack_{0}_{1}".format(game, "_".join(qbs))
        var = LpVariable(var_name, cat="Binary")
        game_vars.append(var)
        
        # Add constraint that at least one offensive player must be in game for game variable to be set
        prob += lpSum([_vars[qb] for qb in qbs]) == var
        prob += lpSum([_vars[player] for player in players if player not in players_by_pos["D"]]) >= min_from_qb_game*var
        
    # Add constraint that at least one game stack var must be set
    prob += lpSum(game_vars) == 1 
    
def add_team_stacks(prob, df, _vars, team_stacks, players_by_pos):
    players_by_team = get_players_by_team(df)
    team_stack_vars = {team: [] for team in players_by_team}
    
    for i, team_stack in enumerate(team_stacks):
        if team_stack <= 1:
            raise IOError("Can't have a game stack less than 1 as that's not a stack!")
        team_vars = []
        for team, players in players_by_team.items():
            var_name = "teamstack_{0}_{1}_{2}".format(team, team_stack, i)
            var = LpVariable(var_name, cat="Binary")
            team_vars.append(var)
            team_stack_vars[team].append(var)
                
            # Add constraint that at least one offensive player must be in game for game variable to be set
            prob += lpSum([_vars[player] for player in players if player not in players_by_pos["D"]]) >= team_stack*var

        # Add constraint that at least one game stack var must be set
        prob += lpSum(team_vars) >= 1     
        
    # Add constraints that 1 game can only satisfy one game stack
    for team, team_stack_vars in team_stack_vars.items():
        prob += lpSum(team_stack_vars) <= 1
    
    return team_stack_vars


In [11]:
def get_basic_dfs_solver(df, pos_max, pos_min, salary_cap=50000, 
                         roster_size=9, max_per_team=9, min_per_team_in_lineup=1, max_off_players_per_game=9, proj_type="avg", 
                         sd_multiplier=2, opposing_player_exclusions=[], min_projection_cutoff=2,
                         stacks=[],
                         point_diff_for_identical=0,
                         max_offensive_games=9,
                         min_offensive_games=1,
                         max_offensive_teams=9, 
                         min_offensive_teams=1,
                         game_stacks=[],
                         team_stacks=[],
                         min_from_qb_game=0,
                         max_from_d_team=0,
                         min_qb_stack=0,
                         use_actual_points = False,
                         min_home_players=0,
                         exclude_teams=[],
                         min_stud_rbs=0,
                         min_stud_rb_salary=0,
                         min_qb_salary=0,
                         max_te_salary=0,
                         require_home_qb=False,
                         min_opposing_games=0,
                         max_home_players=9,
                         min_studs=0,
                         stud_salary=0,
                         min_wr_rb_salary=0,
                         max_wr_rb_per_team=0,
                         min_per_game_in_lineup=0,
                         no_qb_d_stack=False,
                         max_rb_per_team=0,
                         max_wr_per_team=0, lock_players=[], exclude_players=[]):
    
    if proj_type not in ["avg", "floor", "ceil", "tier_avg"]:
        raise IOError("proj_type must be one of ['avg', 'floor', 'ceil', 'tier_avg']")
    
    # Remove players lower than minimum projection cutof
    df["player_id"] = generate_player_ids(df) 
    df = df[df.points_projected >= min_projection_cutoff].reset_index(drop=True)
    
    if proj_type == 'floor':
        df = df.copy()
        df.points_projected = df.points_projected - (sd_multiplier*df.sdPts_projected)
    elif proj_type == 'ceil':
        df = df.copy()
        df.points_projected = df.points_projected + (sd_multiplier*df.sdPts_projected)
    elif proj_type == 'tier_avg':
        df = df.copy()
        df = smooth_player_scores_by_tier(df)
        
    
    #if min_home_players >= 9:
    #    df = df[df.home_team].reset_index(drop=True)
        
    # Generate variables for each player being in a lineup   
    _vars = {player_id: LpVariable(player_id, cat="Binary") for player_id in df.player_id}
    
    prob = LpProblem("Fantasy", LpMaximize)
    rewards = []
    costs = []
    total_players = []
    team_players = []
    
    # Set up reward
    points_attr = "points_projected" if not use_actual_points else "points_actual"
    proj_points = get_player_attribute_dict(df, points_attr)
    prob += lpSum([proj_points[player] * _vars[player] for player in _vars])
    
    # Add salary constraint
    salaries = get_player_attribute_dict(df, "salary")
    prob += lpSum([salaries[player] * _vars[player] for player in _vars]) <= salary_cap
    
    # Add total player constrains
    prob += lpSum([_vars[player] for player in _vars]) == roster_size
    
    # Add positional constraints
    players_by_pos = get_players_by_position(df)
    for pos, players in players_by_pos.items():
        prob += lpSum(_vars[player] for player in players) <= pos_max[pos]
        prob += lpSum(_vars[player] for player in players) >= pos_min[pos]
        
    # Add team-level constraints
    players_by_team = get_players_by_team(df)
    team_vars = {team: None for team in players_by_team}
    qb_vars = []
    def_vars = []
    for team, players in players_by_team.items():
        # Add constraint for max per team
        prob += lpSum(_vars[player] for player in players if player not in players_by_pos["D"]) <= max_per_team
        
        # Add constraints for max teams that can be in a lineup
        if max_offensive_teams > 0 or min_offensive_teams >0 or min_opposing_games > 0:
            assert max_offensive_teams >= min_offensive_teams
            assert max_offensive_teams <= roster_size
            var_name = "team_offense_{0}".format(team)
            var = LpVariable(var_name, cat="Binary")
            team_vars[team] = var
            for player in players:
                if player not in players_by_pos["D"]:
                    prob += _vars[player] <= var
                #prob += _vars[player] <= var
                    
            # Add constraint that at least one player must be in game for game variable to be set
            prob += lpSum([_vars[player] for player in players if player not in players_by_pos["D"]]) >= var*min_per_team_in_lineup
            
            if team in exclude_teams:
                prob += lpSum([_vars[player] for player in players]) == 0
        
        if min_qb_stack:
            # Add constraint for minimum number of players that must be stacked with QB
            qbs = [player for player in players if player in players_by_pos["QB"]]
            var_name = "qb_teamstack_{0}".format("_".join(qbs))
            var = LpVariable(var_name, cat="Binary")
            off_players = [player for player in players if player not in qbs and player not in players_by_pos["D"]]
            qb_vars.append(var)
            
            # Add constraint that number of QB teammates must be >= min_qb_stack
            prob += lpSum([_vars[qb] for qb in qbs]) == var
            prob += lpSum([_vars[player] for player in off_players]) >= min_qb_stack*var
            
        if max_wr_rb_per_team:
            for pos in ["RB", "WR"]:
                pos_players = [player for player in players if player in players_by_pos[pos]]
                prob += lpSum([_vars[player] for player in pos_players]) <= max_wr_rb_per_team
                
        if max_wr_per_team:
            prob += lpSum([_vars[player] for player in players if player in players_by_pos["WR"]]) <= max_wr_per_team
            
        if max_rb_per_team:
            prob += lpSum([_vars[player] for player in players if player in players_by_pos["RB"]]) <= max_rb_per_team
        
        if no_qb_d_stack:
            qbs = [player for player in players if player in players_by_pos["QB"]]
            dst = [player for player in players if player in players_by_pos["D"]]
            qb_d_players = qbs + dst
            prob += lpSum([_vars[player] for player in qb_d_players]) <= 1
    
    # Add constraint for players that some number of opposing matchups must be included
    if min_opposing_games:
        opposing_player_vars = []
        for game in get_matchups(df):
            var_name = "opposing_players_{0}".format("_".join(game))
            var = LpVariable(var_name, cat="Binary")
            opposing_player_vars.append(var)
            prob += lpSum([team_vars[team] for team in game]) >= var*2 
        prob += lpSum(opposing_player_vars) >= min_opposing_games
            
    # Add constraint that total number of games cannot exceed max number of games
    if max_offensive_teams > 0 or min_offensive_teams >0:
        prob += lpSum(team_vars) <= max_offensive_teams
        prob += lpSum(team_vars) >= min_offensive_teams
        
    # Add max games constraint
    game_vars_dict = {}
    if max_offensive_games > 0 or min_offensive_games > 0 or min_per_game_in_lineup > 0:
        print("We making games!")
        max_offensive_games = min_offensive_games if max_offensive_games == 0 else max_offensive_games
        assert max_offensive_games >= min_offensive_games
        game_vars = []
        for game in get_matchups(df):
            var_name = "game_{0}".format("_".join(game))
            var = LpVariable(var_name, cat="Binary")
            game_vars.append(var)
            game_vars_dict["_".join(sorted(game))] = var
            for team in game:
                prob += team_vars[team] <= var
            prob += lpSum([team_vars[team] for team in game]) >= var
        
        # Add constraint that total number of games cannot exceed max number of games
        prob += lpSum(game_vars) <= max_offensive_games
        prob += lpSum(game_vars) >= min_offensive_games
        
    # Add max per game constraint
    players_by_game = get_players_by_game(df)
    for game, players in players_by_game.items():
        prob += lpSum(_vars[player] for player in players if player not in players_by_pos["D"]) <= max_off_players_per_game
        if min_per_game_in_lineup > 1:
            prob += lpSum(_vars[player] for player in players if player not in players_by_pos["D"]) >= min_per_game_in_lineup*game_vars_dict[game]
        
        if min_from_qb_game:
            qbs = [player for player in players if player in players_by_pos["QB"]]
            for qb in qbs:
                prob += lpSum(_vars[player] for player in players if player not in players_by_pos["D"]) >= _vars[qb]*min_from_qb_game
            
    # Add game stacks. Each game stack enforces at least N players from same game appear in lineup
    # e.g. [4,2] means 4 players must come from same game and at least 2 must come from another game
    if game_stacks:
        assert sum(game_stacks) <= roster_size, "Sum of players in game stacks ({0}) is larger than roster!".format(sum(game_stacks))
        game_stack_vars = add_game_stacks(prob, df, _vars, game_stacks, players_by_pos)
        
    # Add constraints for types of positions that can oppose each other on same team
    for opposing_player_exclusion in opposing_player_exclusions:
        restrict_positions_from_opposing_teams(prob, df, _vars, opposing_player_exclusion)
        
    if stacks:
        stacks = StackSet(stacks, pos_max, max_per_team)
        add_stacks(prob, df, _vars, stacks, point_diff_for_identical)
        
    if team_stacks:
        add_team_stacks(prob, df, _vars, team_stacks, players_by_pos)
    
    if min_home_players:
        home_team_players = df[df.home_team].player_id.tolist()
        away_team_players = df[~df.home_team].player_id.tolist()
        if min_home_players == 9:
            prob += lpSum([_vars[player] for player in away_team_players]) == 0
        else:
            prob += lpSum([_vars[player] for player in home_team_players]) >= min_home_players
            prob += lpSum([_vars[player] for player in home_team_players]) <= max_home_players
        
        
    if min_stud_rbs and min_stud_rb_salary:
        stud_rbs = df[(df.position== "RB") & (df.salary >= min_stud_rb_salary)].player_id.tolist()
        prob += lpSum([_vars[player] for player in stud_rbs]) >= min_stud_rbs
        
    if min_qb_salary:
        qbs = df[(df.position== "QB") & (df.salary < min_qb_salary)].player_id.tolist()
        prob += lpSum([_vars[player] for player in qbs]) == 0
        
    if max_te_salary:
        tes = df[(df.position== "TE") & (df.salary > max_te_salary)].player_id.tolist()
        prob += lpSum([_vars[player] for player in tes]) == 0
        
    if require_home_qb:
        away_qbs = df[(df.position== "QB") & (~df.home_team)].player_id.tolist()
        prob += lpSum([_vars[player] for player in away_qbs]) == 0
    
    if min_studs:
        studs = df[df.salary >= stud_salary].player_id.tolist()
        prob += lpSum([_vars[player] for player in studs]) >= min_studs
    
    if min_wr_rb_salary:
        low_cost_players = df[(df.position.isin(["WR", "RB"])) & (df.salary < min_wr_rb_salary)].player_id.tolist()
        prob += lpSum([_vars[player] for player in low_cost_players]) == 0
        
    if lock_players:
        locks = df[df.player.isin(lock_players)].player_id.tolist()
        prob += lpSum([_vars[player] for player in locks]) == len(locks)
        
    if exclude_players:
        excluders = df[df.player.isin(exclude_players)].player_id.tolist()
        prob += lpSum([_vars[player] for player in excluders]) == 0
    # Add constraints for max number of teams where offensive players can come from
    #if max_offensive_teams:
    #    add_number_of_teams_constraints(prob, df, _vars, max_offensive_teams)
                                                                                    
    return prob, _vars
    

In [12]:
def summary(prob):
    div = '---------------------------------------\n'
    print("Variables:\n")
    score = str(prob.objective)
    constraints = [str(const) for const in prob.constraints.values()]
    for v in prob.variables():
        score = score.replace(v.name, str(v.varValue))
        constraints = [const.replace(v.name, str(v.varValue)) for const in constraints]
        if v.varValue != 0:
            print(v.name, "=", v.varValue)
    print(div)
    print("Constraints:")
    for constraint in constraints:
        constraint_pretty = " + ".join(re.findall("[0-9\.]*\*1.0", constraint))
        if constraint_pretty != "":
            print("{} = {}".format(constraint_pretty, eval(constraint_pretty)))
    print(div)
    print("Score:")
    score_pretty = " + ".join(re.findall("[0-9\.]+\*1.0", score))
    print("{} = {}".format(score_pretty, eval(score)))

In [13]:
def output_performance(prob, df, print_points_actual=False):
    player_names = []
    df["player_id"] = generate_player_ids(df)
    for v in prob.variables():
        if v.varValue != 0:
            player_names.append(v.name)
            
    score_df = df[df.player_id.isin(player_names)]
    assert len(score_df) == 9, "Team doesn't have 9 players so probably a player with a hypen or something"
    if not print_points_actual:
        print("Actual week score: {0}".format(score_df.points_projected.sum()))
    else:
        print("Actual week score: {0}".format(score_df.points_actual.sum()))
    return score_df

In [14]:
pos_max = {
    "QB": 1,
    "RB": 3,
    "WR": 4,
    "TE": 2,
    "D": 1
}

pos_min = {
    "QB": 1,
    "RB": 2,
    "WR": 3,
    "TE": 1,
    "D": 1
}

In [25]:
prob, player_vars = get_basic_dfs_solver(df, pos_max, pos_min, max_per_team=9, proj_type="floor", exclude_players=["Alshon Jeffery"])
prob.solve()
score_df = output_performance(prob, df)
score_df

We making games!
Actual week score: 135.9169428571428


player position team  opp  points_actual  salary  \
202          Lions         D  DET  WAS           5.30    3100   
50     Carson Wentz       QB  PHI  SEA          17.81    5600   
74    Miles Sanders       RB  PHI  SEA          10.58    5000   
27     Le'Veon Bell       RB  NYJ  OAK          15.27    6400   
2      Alvin Kamara       RB   NO  CAR          18.50    8200   
163  Vance McDonald       TE  PIT  CIN           7.58    3500   
24    Calvin Ridley       WR  ATL   TB          14.53    6500   
9        Mike Evans       WR   TB  ATL          21.03    7300   
103    Cole Beasley       WR  BUF  DEN          10.79    4400   

     points_projected  sdPts_projected  tier   player_id  
202          8.916000         0.613430     1   D_DET_202  
50          18.920257         0.551635     3   QB_PHI_50  
74          12.848700         0.941393     5   RB_PHI_74  
27          17.654833         1.258499     3   RB_NYJ_27  
2           23.132339         1.083827     2     RB_NO_2  
163          8.915375         0.671083     3  TE_PIT_163  
24          16.491771         1.055449     3   WR_ATL_24  
9           19.578167         1.739284     2     WR_TB_9  
103          9.459500         0.537797     7  WR_BUF_103

In [24]:
prob, player_vars = get_basic_dfs_solver(df, pos_max, pos_min, max_per_team=9, proj_type="tier_avg", exclude_players=["Alshon Jeffery"])
prob.solve()
score_df = output_performance(prob, df)
score_df

We making games!
Actual week score: 139.20496309523807


player position team  opp  points_actual  salary  \
202          Lions         D  DET  WAS           5.30    3100   
50     Carson Wentz       QB  PHI  SEA          17.81    5600   
74    Miles Sanders       RB  PHI  SEA          10.58    5000   
27     Le'Veon Bell       RB  NYJ  OAK          15.27    6400   
2      Alvin Kamara       RB   NO  CAR          18.50    8200   
169    Jason Witten       TE  DAL   NE           8.91    3500   
9        Mike Evans       WR   TB  ATL          21.03    7300   
63   DeVante Parker       WR  MIA  CLE          12.74    5200   
47      Golden Tate       WR  NYG  CHI          16.05    5700   

     points_projected  sdPts_projected  tier   player_id  
202          8.916000         0.613430     1   D_DET_202  
50          18.920257         0.551635     3   QB_PHI_50  
74          12.848700         0.941393     5   RB_PHI_74  
27          17.654833         1.258499     3   RB_NYJ_27  
2           23.132339         1.083827     2     RB_NO_2  
169          9.294667         2.651952     2  TE_DAL_169  
9           19.578167         1.739284     2     WR_TB_9  
63          14.278417         2.189062     4   WR_MIA_63  
47          14.581583         2.582857     4   WR_NYG_47

In [23]:
prob, player_vars = get_basic_dfs_solver(df, pos_max, pos_min, max_per_team=9, proj_type="avg", exclude_players=["Alshon Jeffery"])
prob.solve()
score_df = output_performance(prob, df)
score_df

We making games!
Actual week score: 139.20496309523807


player position team  opp  points_actual  salary  \
202          Lions         D  DET  WAS           5.30    3100   
50     Carson Wentz       QB  PHI  SEA          17.81    5600   
74    Miles Sanders       RB  PHI  SEA          10.58    5000   
27     Le'Veon Bell       RB  NYJ  OAK          15.27    6400   
2      Alvin Kamara       RB   NO  CAR          18.50    8200   
169    Jason Witten       TE  DAL   NE           8.91    3500   
9        Mike Evans       WR   TB  ATL          21.03    7300   
63   DeVante Parker       WR  MIA  CLE          12.74    5200   
47      Golden Tate       WR  NYG  CHI          16.05    5700   

     points_projected  sdPts_projected  tier   player_id  
202          8.916000         0.613430     1   D_DET_202  
50          18.920257         0.551635     3   QB_PHI_50  
74          12.848700         0.941393     5   RB_PHI_74  
27          17.654833         1.258499     3   RB_NYJ_27  
2           23.132339         1.083827     2     RB_NO_2  
169          9.294667         2.651952     2  TE_DAL_169  
9           19.578167         1.739284     2     WR_TB_9  
63          14.278417         2.189062     4   WR_MIA_63  
47          14.581583         2.582857     4   WR_NYG_47

In [18]:
prob, player_vars = get_basic_dfs_solver(df, pos_max, pos_min, max_per_team=9, proj_type="tier_avg",
                                         stacks=[["QB", "WR"]], point_diff_for_identical=100)
prob.solve()
score_df = output_performance(prob, df)
score_df

We making games!
Stack: QB_WR_0. Pos: QB, WR. Opp Pos: 
Actual week score: 139.02029642857147


player position team  opp  points_actual  salary  \
202          Lions         D  DET  WAS           5.30    3100   
32   Jameis Winston       QB   TB  ATL          22.03    6200   
74    Miles Sanders       RB  PHI  SEA          10.58    5000   
27     Le'Veon Bell       RB  NYJ  OAK          15.27    6400   
2      Alvin Kamara       RB   NO  CAR          18.50    8200   
169    Jason Witten       TE  DAL   NE           8.91    3500   
9        Mike Evans       WR   TB  ATL          21.03    7300   
80   Alshon Jeffery       WR  PHI  SEA          11.69    4900   
63   DeVante Parker       WR  MIA  CLE          12.74    5200   

     points_projected  sdPts_projected  tier   player_id  
202          8.916000         0.613430     1   D_DET_202  
32          20.267257         1.435382     2    QB_TB_32  
74          12.848700         0.941393     5   RB_PHI_74  
27          17.654833         1.258499     3   RB_NYJ_27  
2           23.132339         1.083827     2     RB_NO_2  
169          9.294667         2.651952     2  TE_DAL_169  
9           19.578167         1.739284     2     WR_TB_9  
80          13.049917         2.639944     4   WR_PHI_80  
63          14.278417         2.189062     4   WR_MIA_63

In [22]:
prob, player_vars = get_basic_dfs_solver(df, pos_max, pos_min, max_per_team=9, proj_type="floor",
                                         lock_players=["Christian McCaffrey"],
                                         exclude_players=["Alshon Jeffery"])
prob.solve()
score_df = output_performance(prob, df)
score_df

We making games!
Actual week score: 130.44164999999992


player position team  opp  points_actual  salary  \
312            Dolphins         D  MIA  CLE           2.90    2000   
50          Carson Wentz       QB  PHI  SEA          17.81    5600   
0    Christian McCaffrey       RB  CAR   NO          32.36   10500   
60           James White       RB   NE  DAL          12.93    5300   
2           Alvin Kamara       RB   NO  CAR          18.50    8200   
163       Vance McDonald       TE  PIT  CIN           7.58    3500   
24         Calvin Ridley       WR  ATL   TB          14.53    6500   
151     Demaryius Thomas       WR  NYJ  OAK           8.12    3800   
95        Dede Westbrook       WR  JAX  TEN           9.83    4600   

     points_projected  sdPts_projected  tier   player_id  
312          5.107000         0.365541     4   D_MIA_312  
50          18.920257         0.551635     3   QB_PHI_50  
0           24.470024         1.455251     1    RB_CAR_0  
60          13.560467         0.619908     5    RB_NE_60  
2           23.132339         1.083827     2     RB_NO_2  
163          8.915375         0.671083     3  TE_PIT_163  
24          16.491771         1.055449     3   WR_ATL_24  
151          9.368083         1.511109     7  WR_NYJ_151  
95          10.476333         0.786457     6   WR_JAX_95

In [27]:
prob, player_vars = get_basic_dfs_solver(df, pos_max, pos_min, max_per_team=9, proj_type="avg",
                                         stacks=[["QB", "WR", "TE"]],
                                         exclude_players=["Alshon Jeffery"])
prob.solve()
score_df = output_performance(prob, df)
score_df

We making games!
Stack: QB_WR_TE_0. Pos: QB, WR, TE. Opp Pos: 
Actual week score: 137.3352845238095


player position team  opp  points_actual  salary  \
202          Lions         D  DET  WAS           5.30    3100   
32   Jameis Winston       QB   TB  ATL          22.03    6200   
27     Le'Veon Bell       RB  NYJ  OAK          15.27    6400   
2      Alvin Kamara       RB   NO  CAR          18.50    8200   
169    Jason Witten       TE  DAL   NE           8.91    3500   
157   Cameron Brate       TE   TB  ATL           5.94    3600   
24    Calvin Ridley       WR  ATL   TB          14.53    6500   
9        Mike Evans       WR   TB  ATL          21.03    7300   
63   DeVante Parker       WR  MIA  CLE          12.74    5200   

     points_projected  sdPts_projected  tier   player_id  
202          8.916000         0.613430     1   D_DET_202  
32          20.267257         1.435382     2    QB_TB_32  
27          17.654833         1.258499     3   RB_NYJ_27  
2           23.132339         1.083827     2     RB_NO_2  
169          9.294667         2.651952     2  TE_DAL_169  
157          7.721833         1.720663     4   TE_TB_157  
24          16.491771         1.055449     3   WR_ATL_24  
9           19.578167         1.739284     2     WR_TB_9  
63          14.278417         2.189062     4   WR_MIA_63

In [24]:
prob, player_vars = get_basic_dfs_solver(df, pos_max, pos_min, max_per_team=9, proj_type="avg",
                                         lock_players=["Christian McCaffrey"])
prob.solve()
score_df = output_performance(prob, df)
score_df

We making games!
Actual week score: 145.0158595238096


player position team  opp  points_actual  salary  \
247              Giants         D  NYG  NYJ           7.44    2800   
20            Drew Brees       QB   NO  ATL          18.08    6700   
0    Christian McCaffrey       RB  CAR   GB          32.68   10500   
64      Devin Singletary       RB  BUF  CLE          13.40    5000   
48      David Montgomery       RB  CHI  DET          12.99    5300   
273        Rhett Ellison       TE  NYG  NYJ           3.72    2500   
2         Michael Thomas       WR   NO  ATL          24.45    8300   
138         Ted Ginn Jr.       WR   NO  ATL           7.49    3700   
52              DJ Moore       WR  CAR   GB          13.99    5200   

     points_projected  sdPts_projected  tier   player_id  
247          9.751667         1.725508     2   D_NYG_247  
20          22.379943         1.511406     2    QB_NO_20  
0           25.443554         0.737975     1    RB_CAR_0  
64          14.510167         3.091013     7   RB_BUF_64  
48          15.999405         1.270956     6   RB_CHI_48  
273          6.927500         1.178085     5  TE_NYG_273  
2           25.200208         1.216549     1     WR_NO_2  
138          9.742917         1.183475     6   WR_NO_138  
52          15.060500         2.520428     4   WR_CAR_52

In [32]:
prob, player_vars = get_basic_dfs_solver(df, pos_max, pos_min, max_per_team=9, proj_type="avg",
                                         lock_players=["Saquon Barkley"])
prob.solve()
score_df = output_performance(prob, df)
score_df

We making games!
Actual week score: 147.67708452380955


player position team  opp  points_actual  salary  \
9             Giants         D  NYG  NYJ           7.44    2800   
60      Lamar Jackson       QB  BAL  CIN          27.65    7300   
110  Devin Singletary       RB  BUF  CLE          13.40    5000   
121    Saquon Barkley       RB  NYG  NYJ          19.15    8800   
124  David Montgomery       RB  CHI  DET          12.99    5300   
163     Rhett Ellison       TE  NYG  NYJ           3.72    2500   
195    DeVante Parker       WR  MIA  IND          11.50    4800   
215    Michael Thomas       WR   NO  ATL          24.45    8300   
252          DJ Moore       WR  CAR   GB          13.99    5200   

     points_projected  sdPts_projected  tier   player_id  
9            9.751667         1.725508     2     D_NYG_9  
60          24.602995         1.781700     1   QB_BAL_60  
110         14.510167         3.091013     7  RB_BUF_110  
121         22.202393         1.527519     2  RB_NYG_121  
124         15.999405         1.270956     6  RB_CHI_124  
163          6.927500         1.178085     5  TE_NYG_163  
195         13.422250         2.077255     4  WR_MIA_195  
215         25.200208         1.216549     1   WR_NO_215  
252         15.060500         2.520428     4  WR_CAR_252

## GPP

In [31]:
import math
no_d_vs_off =[["QB", "D"], ["WR", "D"], ["RB", "D"], ["TE", "D"]]
prob, player_vars = get_basic_dfs_solver(df, pos_max, pos_min, proj_type='avg',
                                         stacks=[["QB", "WR", "TE"]],
                                         opposing_player_exclusions=no_d_vs_off,
                                         point_diff_for_identical=100,
                                         use_actual_points=False)

df = df[~df.player.isin(["Pharoh Cooper", "Luke Willson"])].reset_index(drop=True)
num_lineups = 10
max_qb_exposure = 1.0
max_lineups_for_one_qb = int(math.ceil(num_lineups*max_qb_exposure))
qb_exposure = {}

max_points = -1
max_overlap = 5
for i in range(num_lineups):
    print("Lineup {0}".format(i))
    prob.solve()
    score_df = output_performance(prob, df)
    print(score_df)
    lineup = score_df.player_id.tolist()
    if score_df.points_actual.sum() > max_points:
        max_points = score_df.points_actual.sum()
    
    # See if we need to remove QB from consideration
    qb = score_df[score_df.position == "QB"].player_id.tolist()[0]
    if qb in qb_exposure:
        qb_exposure[qb] += 1
    else:
        qb_exposure[qb] = 1
    
    # If QB reaches max exposure remove from future lineups
    if qb_exposure[qb] >= max_lineups_for_one_qb:
        print("Reached lineup exposure max for QB: {0}".format(qb))
        prob += player_vars[qb] == 0
    
    print("Best lineup to point: {0}".format(max_points))
    prob += lpSum([player_vars[player] for player in lineup]) <= max_overlap

print("Max points: {0}".format(max_points))

We making games!
Stack: QB_WR_TE_0. Pos: QB, WR, TE. Opp Pos: 
Lineup 0
Actual week score: 146.44885000000005
               player position team  opp  points_actual  salary  \
9             Giants         D  NYG  NYJ           7.44    2800   
54         Drew Brees       QB   NO  ATL          18.08    6700   
106   Damien Williams       RB   KC  TEN          11.19    4900   
110  Devin Singletary       RB  BUF  CLE          13.40    5000   
124  David Montgomery       RB  CHI  DET          12.99    5300   
192        Jared Cook       TE   NO  ATL           7.30    4100   
196        Mike Evans       WR   TB  ARI          23.40    7600   
215    Michael Thomas       WR   NO  ATL          24.45    8300   
252          DJ Moore       WR  CAR   GB          13.99    5200   

     points_projected  sdPts_projected  tier   player_id  
9            9.751667         1.725508     2     D_NYG_9  
54          22.379943         1.511406     2    QB_NO_54  
106         13.886800         2.708306    

Actual week score: 143.98960833333336
               player position team  opp  points_actual  salary  \
9             Giants         D  NYG  NYJ           7.44    2800   
60      Lamar Jackson       QB  BAL  CIN          27.65    7300   
110  Devin Singletary       RB  BUF  CLE          13.40    5000   
124  David Montgomery       RB  CHI  DET          12.99    5300   
128     David Johnson       RB  ARI   TB          17.36    5700   
177      Mark Andrews       TE  BAL  CIN          13.50    5200   
215    Michael Thomas       WR   NO  ATL          24.45    8300   
252          DJ Moore       WR  CAR   GB          13.99    5200   
281    Marquise Brown       WR  BAL  CIN          13.73    5100   

     points_projected  sdPts_projected  tier   player_id  
9            9.751667         1.725508     2     D_NYG_9  
60          24.602995         1.781700     1   QB_BAL_60  
110         14.510167         3.091013     7  RB_BUF_110  
124         15.999405         1.270956     6  RB_CHI_12

In [30]:
import math
no_d_vs_off =[["QB", "D"], ["WR", "D"], ["RB", "D"], ["TE", "D"]]
prob, player_vars = get_basic_dfs_solver(df, pos_max, pos_min, proj_type='avg',
                                         stacks=[["QB", "WR", "TE"]],
                                         opposing_player_exclusions=no_d_vs_off,
                                         point_diff_for_identical=100,
                                         use_actual_points=False,
                                         lock_players=["Christian McCaffrey"])

df = df[~df.player.isin(["Pharoh Cooper", "Luke Willson"])].reset_index(drop=True)
num_lineups = 10
max_qb_exposure = 1.0
max_lineups_for_one_qb = int(math.ceil(num_lineups*max_qb_exposure))
qb_exposure = {}

max_points = -1
max_overlap = 5
for i in range(num_lineups):
    print("Lineup {0}".format(i))
    prob.solve()
    score_df = output_performance(prob, df)
    print(score_df)
    lineup = score_df.player_id.tolist()
    if score_df.points_actual.sum() > max_points:
        max_points = score_df.points_actual.sum()
    
    # See if we need to remove QB from consideration
    qb = score_df[score_df.position == "QB"].player_id.tolist()[0]
    if qb in qb_exposure:
        qb_exposure[qb] += 1
    else:
        qb_exposure[qb] = 1
    
    # If QB reaches max exposure remove from future lineups
    if qb_exposure[qb] >= max_lineups_for_one_qb:
        print("Reached lineup exposure max for QB: {0}".format(qb))
        prob += player_vars[qb] == 0
    
    print("Best lineup to point: {0}".format(max_points))
    prob += lpSum([player_vars[player] for player in lineup]) <= max_overlap

print("Max points: {0}".format(max_points))

We making games!
Stack: QB_WR_TE_0. Pos: QB, WR, TE. Opp Pos: 
Lineup 0
Actual week score: 142.01474047619052
                  player position team  opp  points_actual  salary  \
9                Giants         D  NYG  NYJ           7.44    2800   
54            Drew Brees       QB   NO  ATL          18.08    6700   
104  Christian McCaffrey       RB  CAR   GB          32.68   10500   
110     Devin Singletary       RB  BUF  CLE          13.40    5000   
163        Rhett Ellison       TE  NYG  NYJ           3.72    2500   
192           Jared Cook       TE   NO  ATL           7.30    4100   
195       DeVante Parker       WR  MIA  IND          11.50    4800   
215       Michael Thomas       WR   NO  ATL          24.45    8300   
252             DJ Moore       WR  CAR   GB          13.99    5200   

     points_projected  sdPts_projected  tier   player_id  
9            9.751667         1.725508     2     D_NYG_9  
54          22.379943         1.511406     2    QB_NO_54  
104         

Actual week score: 140.47331190476203
                  player position team  opp  points_actual  salary  \
16            Cardinals         D  ARI   TB           3.33    2200   
54            Drew Brees       QB   NO  ATL          18.08    6700   
104  Christian McCaffrey       RB  CAR   GB          32.68   10500   
124     David Montgomery       RB  CHI  DET          12.99    5300   
128        David Johnson       RB  ARI   TB          17.36    5700   
192           Jared Cook       TE   NO  ATL           7.30    4100   
202       Adam Humphries       WR  TEN   KC           7.10    3500   
215       Michael Thomas       WR   NO  ATL          24.45    8300   
234         Ted Ginn Jr.       WR   NO  ATL           7.49    3700   

     points_projected  sdPts_projected  tier   player_id  
16           7.335000         2.085791     3    D_ARI_16  
54          22.379943         1.511406     2    QB_NO_54  
104         25.443554         0.737975     1  RB_CAR_104  
124         15.999405    

In [34]:
import math
no_d_vs_off =[["QB", "D"], ["WR", "D"], ["RB", "D"], ["TE", "D"]]
prob, player_vars = get_basic_dfs_solver(df, pos_max, pos_min, proj_type='avg',
                                         stacks=[["QB", "WR", "TE"]],
                                         opposing_player_exclusions=no_d_vs_off,
                                         point_diff_for_identical=100,
                                         use_actual_points=False,
                                         lock_players=["Saquon Barkley"])

df = df[~df.player.isin(["Pharoh Cooper", "Luke Willson"])].reset_index(drop=True)
num_lineups = 10
max_qb_exposure = 1.0
max_lineups_for_one_qb = int(math.ceil(num_lineups*max_qb_exposure))
qb_exposure = {}

max_points = -1
max_overlap = 6
for i in range(num_lineups):
    print("Lineup {0}".format(i))
    prob.solve()
    score_df = output_performance(prob, df)
    print(score_df)
    lineup = score_df.player_id.tolist()
    if score_df.points_actual.sum() > max_points:
        max_points = score_df.points_actual.sum()
    
    # See if we need to remove QB from consideration
    qb = score_df[score_df.position == "QB"].player_id.tolist()[0]
    if qb in qb_exposure:
        qb_exposure[qb] += 1
    else:
        qb_exposure[qb] = 1
    
    # If QB reaches max exposure remove from future lineups
    if qb_exposure[qb] >= max_lineups_for_one_qb:
        print("Reached lineup exposure max for QB: {0}".format(qb))
        prob += player_vars[qb] == 0
    
    print("Best lineup to point: {0}".format(max_points))
    prob += lpSum([player_vars[player] for player in lineup]) <= max_overlap

print("Max points: {0}".format(max_points))

We making games!
Stack: QB_WR_TE_0. Pos: QB, WR, TE. Opp Pos: 
Lineup 0
Actual week score: 144.16615119047628
               player position team  opp  points_actual  salary  \
9             Giants         D  NYG  NYJ           7.44    2800   
54         Drew Brees       QB   NO  ATL          18.08    6700   
110  Devin Singletary       RB  BUF  CLE          13.40    5000   
121    Saquon Barkley       RB  NYG  NYJ          19.15    8800   
124  David Montgomery       RB  CHI  DET          12.99    5300   
192        Jared Cook       TE   NO  ATL           7.30    4100   
215    Michael Thomas       WR   NO  ATL          24.45    8300   
234      Ted Ginn Jr.       WR   NO  ATL           7.49    3700   
252          DJ Moore       WR  CAR   GB          13.99    5200   

     points_projected  sdPts_projected  tier   player_id  
9            9.751667         1.725508     2     D_NYG_9  
54          22.379943         1.511406     2    QB_NO_54  
110         14.510167         3.091013    

Actual week score: 142.69675119047625
               player position team  opp  points_actual  salary  \
9             Giants         D  NYG  NYJ           7.44    2800   
57       Daniel Jones       QB  NYG  NYJ          16.73    5700   
121    Saquon Barkley       RB  NYG  NYJ          19.15    8800   
124  David Montgomery       RB  CHI  DET          12.99    5300   
128     David Johnson       RB  ARI   TB          17.36    5700   
163     Rhett Ellison       TE  NYG  NYJ           3.72    2500   
195    DeVante Parker       WR  MIA  IND          11.50    4800   
215    Michael Thomas       WR   NO  ATL          24.45    8300   
264       Golden Tate       WR  NYG  NYJ          14.36    5900   

     points_projected  sdPts_projected  tier   player_id  
9            9.751667         1.725508     2     D_NYG_9  
57          17.174033         0.556561     5   QB_NYG_57  
121         22.202393         1.527519     2  RB_NYG_121  
124         15.999405         1.270956     6  RB_CHI_12

In [29]:
import math
no_d_vs_off =[["QB", "D"], ["WR", "D"], ["RB", "D"], ["TE", "D"]]
prob, player_vars = get_basic_dfs_solver(df, pos_max, pos_min, proj_type='avg',
                                         stacks=[["QB", "WR", "TE", "-WR"]],
                                         opposing_player_exclusions=no_d_vs_off,
                                         point_diff_for_identical=5,
                                         use_actual_points=False)

df = df[~df.player.isin(["Pharoh Cooper", "Luke Willson"])].reset_index(drop=True)
num_lineups = 10
max_qb_exposure = 1.0
max_lineups_for_one_qb = int(math.ceil(num_lineups*max_qb_exposure))
qb_exposure = {}

max_points = -1
max_overlap = 5
for i in range(num_lineups):
    print("Lineup {0}".format(i))
    prob.solve()
    score_df = output_performance(prob, df)
    print(score_df)
    lineup = score_df.player_id.tolist()
    if score_df.points_actual.sum() > max_points:
        max_points = score_df.points_actual.sum()
    
    # See if we need to remove QB from consideration
    qb = score_df[score_df.position == "QB"].player_id.tolist()[0]
    if qb in qb_exposure:
        qb_exposure[qb] += 1
    else:
        qb_exposure[qb] = 1
    
    # If QB reaches max exposure remove from future lineups
    if qb_exposure[qb] >= max_lineups_for_one_qb:
        print("Reached lineup exposure max for QB: {0}".format(qb))
        prob += player_vars[qb] == 0
    
    print("Best lineup to point: {0}".format(max_points))
    prob += lpSum([player_vars[player] for player in lineup]) <= max_overlap

print("Max points: {0}".format(max_points))

We making games!
Stack: QB_WR_TE_-WR_0. Pos: QB, WR, TE. Opp Pos: WR
Lineup 0
Actual week score: 145.27234166666676
               player position team  opp  points_actual  salary  \
16         Cardinals         D  ARI   TB           3.33    2200   
54         Drew Brees       QB   NO  ATL          18.08    6700   
110  Devin Singletary       RB  BUF  CLE          13.40    5000   
124  David Montgomery       RB  CHI  DET          12.99    5300   
128     David Johnson       RB  ARI   TB          17.36    5700   
192        Jared Cook       TE   NO  ATL           7.30    4100   
197       Julio Jones       WR  ATL   NO          19.66    7500   
215    Michael Thomas       WR   NO  ATL          24.45    8300   
252          DJ Moore       WR  CAR   GB          13.99    5200   

     points_projected  sdPts_projected  tier   player_id  
16           7.335000         2.085791     3    D_ARI_16  
54          22.379943         1.511406     2    QB_NO_54  
110         14.510167         3.0910

Actual week score: 143.19015357142865
              player position team  opp  points_actual  salary  \
9            Giants         D  NYG  NYJ           7.44    2800   
54        Drew Brees       QB   NO  ATL          18.08    6700   
106  Damien Williams       RB   KC  TEN          11.19    4900   
128    David Johnson       RB  ARI   TB          17.36    5700   
192       Jared Cook       TE   NO  ATL           7.30    4100   
195   DeVante Parker       WR  MIA  IND          11.50    4800   
197      Julio Jones       WR  ATL   NO          19.66    7500   
215   Michael Thomas       WR   NO  ATL          24.45    8300   
242   Christian Kirk       WR  ARI   TB          12.73    5200   

     points_projected  sdPts_projected  tier   player_id  
9            9.751667         1.725508     2     D_NYG_9  
54          22.379943         1.511406     2    QB_NO_54  
106         13.886800         2.708306     7   RB_KC_106  
128         16.322667         2.781806     5  RB_ARI_128  
192   

In [34]:
import math
no_d_vs_off =[["QB", "D"], ["WR", "D"], ["RB", "D"], ["TE", "D"]]
prob, player_vars = get_basic_dfs_solver(df, pos_max, pos_min, proj_type='tier_avg',
                                         stacks = [["QB", "WR", "TE", "-WR"], ["RB", "WR", "-WR"]],
                                         opposing_player_exclusions=no_d_vs_off,
                                         point_diff_for_identical=10,
                                         max_offensive_teams=5,
                                         min_offensive_teams=5,
                                         use_actual_points=False)

df = df[~df.player.isin(["Pharoh Cooper", "Luke Willson"])].reset_index(drop=True)
num_lineups = 20
max_qb_exposure = 0.2
max_lineups_for_one_qb = int(math.ceil(num_lineups*max_qb_exposure))
qb_exposure = {}

max_points = -1
max_overlap = 5
for i in range(num_lineups):
    print("Lineup {0}".format(i))
    prob.solve()
    score_df = output_performance(prob, df)
    print(score_df)
    lineup = score_df.player_id.tolist()
    if score_df.points_actual.sum() > max_points:
        max_points = score_df.points_actual.sum()
    
    # See if we need to remove QB from consideration
    qb = score_df[score_df.position == "QB"].player_id.tolist()[0]
    if qb in qb_exposure:
        qb_exposure[qb] += 1
    else:
        qb_exposure[qb] = 1
    
    # If QB reaches max exposure remove from future lineups
    if qb_exposure[qb] >= max_lineups_for_one_qb:
        print("Reached lineup exposure max for QB: {0}".format(qb))
        prob += player_vars[qb] == 0
    
    print("Best lineup to point: {0}".format(max_points))
    prob += lpSum([player_vars[player] for player in lineup]) <= max_overlap

print("Max points: {0}".format(max_points))

Stack: QB_WR_TE_-WR_0. Pos: QB, WR, TE. Opp Pos: WR
Stack: RB_WR_-WR_1. Pos: RB, WR. Opp Pos: WR
Lineup 0
Actual week score: 146.2067261904762
                player position team  opp  points_actual  salary  \
0                Jets         D  NYJ  DAL          10.75    1500   
50           Matt Ryan       QB  ATL  ARI          26.14    6400   
118  Leonard Fournette       RB  JAX   NO          19.30    6700   
135       Le'Veon Bell       RB  NYJ  DAL          17.80    6400   
158      Austin Hooper       TE  ATL  ARI          17.46    5000   
195     Michael Thomas       WR   NO  JAX          24.66    7800   
219   Larry Fitzgerald       WR  ARI  ATL          16.56    6100   
246       Mohamed Sanu       WR  ATL  ARI          12.68    4500   
285       DJ Chark Jr.       WR  JAX   NO          22.30    5500   

     points_projected  sdPts_projected  tier   player_id  
0            6.504800         0.477279     4     D_NYJ_0  
50          21.868021         1.083732     2   QB_ATL_50  

Actual week score: 139.0134511904763
              player position team  opp  points_actual  salary  \
14           Chiefs         D   KC  HOU           6.80    2500   
60      Carson Wentz       QB  PHI  MIN          20.20    6000   
122  Damien Williams       RB   KC  HOU          11.30    5700   
135     Le'Veon Bell       RB  NYJ  DAL          17.80    6400   
156        Zach Ertz       TE  PHI  MIN          13.64    5400   
199     Adam Thielen       WR  MIN  PHI          16.80    6700   
213     Amari Cooper       WR  DAL  NYJ          23.84    7000   
250   Robby Anderson       WR  NYJ  DAL           6.02    4000   
265   Alshon Jeffery       WR  PHI  MIN          11.52    5800   

     points_projected  sdPts_projected  tier   player_id  
14           7.676000         0.600442     4     D_KC_14  
60          17.933148         1.576590     5   QB_PHI_60  
122         15.256667         2.023352     5   RB_KC_122  
135         20.259054         0.592551     2  RB_NYJ_135  
156    

Actual week score: 137.09095476190478
               player position team  opp  points_actual  salary  \
9             Browns         D  CLE  SEA           7.00    2800   
56    Jimmy Garoppolo       QB   SF  LAR          15.60    5700   
132        Nick Chubb       RB  CLE  SEA          20.32    7300   
135      Le'Veon Bell       RB  NYJ  DAL          17.80    6400   
142     George Kittle       TE   SF  LAR          13.58    5200   
213      Amari Cooper       WR  DAL  NYJ          23.84    7000   
215       Cooper Kupp       WR  LAR   SF          25.58    7100   
245  Marquise Goodwin       WR   SF  LAR           8.28    4500   
250    Robby Anderson       WR  NYJ  DAL           6.02    4000   

     points_projected  sdPts_projected  tier   player_id  
9            6.444667         0.874345     4     D_CLE_9  
56          16.143776         1.765654     7    QB_SF_56  
132         18.649625         0.912387     4  RB_CLE_132  
135         20.259054         0.592551     2  RB_NYJ_13

## Post-Week Exploration

In [24]:
model_input = "/Users/awaldrop/PycharmProjects/dfs_optimization_tools/data/harmonized_datasets/2019/dfk_harm_wk9_2019.csv"
df = pd.read_csv(model_input)
df = df.sort_values(by="position").copy()
non_main_slate_teams = ["NYG", "DAL", "NE", "BAL", "ARI", "SF"]
df = df[~df.team.isin(non_main_slate_teams)].reset_index(drop=True)
df.head(15)

player position team  opp  home_team  points_actual  salary  \
0   Steelers        D  PIT  IND       True           19.0    2400   
1   Panthers        D  CAR  TEN       True           11.0    2800   
2      Bills        D  BUF  WAS       True            8.0    3800   
3   Dolphins        D  MIA  NYJ       True            8.0    2700   
4      Colts        D  IND  PIT      False            8.0    2800   
5    Vikings        D  MIN   KC      False            7.0    2700   
6   Chargers        D  LAC   GB       True            7.0    2000   
7    Raiders        D  OAK  DET       True            6.0    2300   
8     Eagles        D  PHI  CHI       True            6.0    3000   
9       Jets        D  NYJ  MIA      False            6.0    3500   
10    Titans        D  TEN  CAR      False            6.0    2600   
11   Jaguars        D  JAX  HOU       True            5.0    2500   
12    Browns        D  CLE  DEN      False            5.0    3100   
13     Bears        D  CHI  PHI      False            4.0    2900   
14   Broncos        D  DEN  CLE       True            3.0    2900   

    points_projected  sdPts_projected  tier  
0           6.678333         0.930514     0  
1           9.655429         1.050975     1  
2           8.471143         1.921047     0  
3           7.182667         1.875734     0  
4           5.901000         0.581403     0  
5           6.273333         0.976681     0  
6           5.433333         1.574076     0  
7           5.441000         1.419253     0  
8           8.049143         0.750893     0  
9           8.736333         1.269677     0  
10          6.653333         0.330817     0  
11          6.960000         1.250786     0  
12          8.246286         1.281440     0  
13          6.335000         1.011032     0  
14          8.289143         0.699869     0

In [25]:
pos_max = {
    "QB": 1,
    "RB": 3,
    "WR": 4,
    "TE": 2,
    "D": 1
}

pos_min = {
    "QB": 1,
    "RB": 2,
    "WR": 3,
    "TE": 1,
    "D": 1
}

In [28]:
import math
no_d_vs_off =[["QB", "D"], ["WR", "D"], ["RB", "D"], ["TE", "D"]]
prob, player_vars = get_basic_dfs_solver(df, pos_max, pos_min, proj_type='tier_avg',
                                         opposing_player_exclusions=no_d_vs_off,
                                         min_from_qb_game=4,
                                         use_actual_points=True)

df = df[~df.player.isin(["Pharoh Cooper", "Luke Willson"])].reset_index(drop=True)
num_lineups = 20
max_qb_exposure = 1.0
max_lineups_for_one_qb = int(math.ceil(num_lineups*max_qb_exposure))
qb_exposure = {}

max_points = -1
max_overlap = 6
for i in range(num_lineups):
    print("Lineup {0}".format(i))
    prob.solve()
    score_df = output_performance(prob, df, print_points_actual=True)
    print(score_df)
    lineup = score_df.player_id.tolist()
    if score_df.points_actual.sum() > max_points:
        max_points = score_df.points_actual.sum()
    
    # See if we need to remove QB from consideration
    qb = score_df[score_df.position == "QB"].player_id.tolist()[0]
    if qb in qb_exposure:
        qb_exposure[qb] += 1
    else:
        qb_exposure[qb] = 1
    
    # If QB reaches max exposure remove from future lineups
    if qb_exposure[qb] >= max_lineups_for_one_qb:
        print("Reached lineup exposure max for QB: {0}".format(qb))
        prob += player_vars[qb] == 0
    
    print("Best lineup to point: {0}".format(max_points))
    prob += lpSum([player_vars[player] for player in lineup]) <= max_overlap

print("Max points: {0}".format(max_points))

We making games!
Lineup 0
Actual week score: 281.02
                  player position team  opp  home_team  points_actual  salary  \
0               Steelers        D  PIT  IND       True          19.00    2400   
22        Russell Wilson       QB  SEA   TB       True          42.22    7100   
70   Christian McCaffrey       RB  CAR  TEN       True          40.60   10000   
89       Damien Williams       RB   KC  MIN       True          23.80    4000   
140      Jacob Hollister       TE  SEA   TB       True          19.70    2900   
141            Noah Fant       TE  DEN  CLE       True          23.50    3000   
207        Tyler Lockett       WR  SEA   TB       True          43.20    7500   
208           Mike Evans       WR   TB  SEA      False          39.00    7200   
209         D.K. Metcalf       WR  SEA   TB       True          30.00    5700   

     points_projected  sdPts_projected  tier   player_id  
0            6.678333         0.930514     0     D_PIT_0  
22          23.9102

Actual week score: 275.92
               player position team  opp  home_team  points_actual  salary  \
0            Steelers        D  PIT  IND       True          19.00    2400   
22     Russell Wilson       QB  SEA   TB       True          42.22    7100   
88   Devin Singletary       RB  BUF  WAS       True          23.00    4700   
93        Josh Jacobs       RB  OAK  DET       True          27.00    6500   
119         Zach Ertz       TE  PHI  CHI       True          28.30    4700   
207     Tyler Lockett       WR  SEA   TB       True          43.20    7500   
208        Mike Evans       WR   TB  SEA      False          39.00    7200   
209      D.K. Metcalf       WR  SEA   TB       True          30.00    5700   
213  Preston Williams       WR  MIA  NYJ       True          24.20    4200   

     points_projected  sdPts_projected  tier   player_id  
0            6.678333         0.930514     0     D_PIT_0  
22          23.910286         1.394769     1   QB_SEA_22  
88           9.6

Actual week score: 272.72
               player position team  opp  home_team  points_actual  salary  \
0            Steelers        D  PIT  IND       True          19.00    2400   
22     Russell Wilson       QB  SEA   TB       True          42.22    7100   
87   David Montgomery       RB  CHI  PHI      False          22.60    5200   
90      Derrick Henry       RB  TEN  CAR      False          24.90    5700   
119         Zach Ertz       TE  PHI  CHI       True          28.30    4700   
141         Noah Fant       TE  DEN  CLE       True          23.50    3000   
207     Tyler Lockett       WR  SEA   TB       True          43.20    7500   
208        Mike Evans       WR   TB  SEA      False          39.00    7200   
209      D.K. Metcalf       WR  SEA   TB       True          30.00    5700   

     points_projected  sdPts_projected  tier   player_id  
0            6.678333         0.930514     0     D_PIT_0  
22          23.910286         1.394769     1   QB_SEA_22  
87          13.1

Actual week score: 270.02
                  player position team  opp  home_team  points_actual  salary  \
20                Texans        D  HOU  JAX      False          19.00    2800   
22        Russell Wilson       QB  SEA   TB       True          42.22    7100   
70   Christian McCaffrey       RB  CAR  TEN       True          40.60   10000   
89       Damien Williams       RB   KC  MIN       True          23.80    4000   
119            Zach Ertz       TE  PHI  CHI       True          28.30    4700   
140      Jacob Hollister       TE  SEA   TB       True          19.70    2900   
207        Tyler Lockett       WR  SEA   TB       True          43.20    7500   
208           Mike Evans       WR   TB  SEA      False          39.00    7200   
224     Breshad Perriman       WR   TB  SEA      False          14.20    3000   

     points_projected  sdPts_projected  tier   player_id  
20           6.075000         0.826635     0    D_HOU_20  
22          23.910286         1.394769     1 

In [81]:
import math
no_d_vs_off =[["QB", "D"], ["WR", "D"], ["RB", "D"], ["TE", "D"]]
prob, player_vars = get_basic_dfs_solver(df, pos_max, pos_min, proj_type='avg',
                                         opposing_player_exclusions=no_d_vs_off,
                                         stacks=[["QB", "WR", "TE"]],
                                         max_offensive_teams=5,
                                         min_offensive_teams=4,
                                         max_per_team=4,
                                         use_actual_points=False)

df = df[~df.player.isin(["Pharoh Cooper", "Luke Willson"])].reset_index(drop=True)
num_lineups = 200
max_qb_exposure = 1.0
max_lineups_for_one_qb = int(math.ceil(num_lineups*max_qb_exposure))
qb_exposure = {}

max_points = -1
max_overlap = 3
for i in range(num_lineups):
    print("Lineup {0}".format(i))
    prob.solve()
    score_df = output_performance(prob, df, print_points_actual=True)
    print(score_df)
    lineup = score_df.player_id.tolist()
    if score_df.points_actual.sum() > max_points:
        max_points = score_df.points_actual.sum()
    
    # See if we need to remove QB from consideration
    qb = score_df[score_df.position == "QB"].player_id.tolist()[0]
    if qb in qb_exposure:
        qb_exposure[qb] += 1
    else:
        qb_exposure[qb] = 1
    
    # If QB reaches max exposure remove from future lineups
    if qb_exposure[qb] >= max_lineups_for_one_qb:
        print("Reached lineup exposure max for QB: {0}".format(qb))
        prob += player_vars[qb] == 0
    
    print("Best lineup to point: {0}".format(max_points))
    prob += lpSum([player_vars[player] for player in lineup]) <= max_overlap

print("Max points: {0}".format(max_points))

Stack: QB_WR_TE_0. Pos: QB, WR, TE. Opp Pos: 
Lineup 0
Actual week score: 171.54
                player position team  opp  home_team  points_actual  salary  \
17                Jets        D  NYJ  DAL       True           1.00  1500.0   
22           Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
58        Kenyan Drake       RB  MIA  WAS       True          13.00  4400.0   
62        Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
70   Leonard Fournette       RB  JAX   NO       True          17.80  6700.0   
123      Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
197     Robby Anderson       WR  NYJ  DAL       True          26.50  4000.0   
200        Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
205    DeAndre Hopkins       WR  HOU   KC      False          16.50  7400.0   

     points_projected  sdPts_projected  tier   player_id  
17           6.504800         0.477279     4    D_NYJ_17  
22        

Actual week score: 125.3
                player position team  opp  home_team  points_actual  salary  \
4             Redskins        D  WAS  MIA      False           10.0  3200.0   
24      Deshaun Watson       QB  HOU   KC      False           31.4  6700.0   
62        Le'Veon Bell       RB  NYJ  DAL       True           12.3  6400.0   
70   Leonard Fournette       RB  JAX   NO       True           17.8  6700.0   
71     Phillip Lindsay       RB  DEN  TEN       True           15.5  5300.0   
119       Jordan Akins       TE  HOU   KC      False            6.9  3200.0   
183       Robert Woods       WR  LAR   SF       True            7.6  5600.0   
185         D.J. Chark       WR  JAX   NO       True            7.3  5500.0   
205    DeAndre Hopkins       WR  HOU   KC      False           16.5  7400.0   

     points_projected  sdPts_projected  tier   player_id  
4            9.298667         1.180995     3     D_WAS_4  
24          21.593686         0.510101     2   QB_HOU_24  
62     

Actual week score: 146.62
                 player position team  opp  home_team  points_actual  salary  \
11               Chiefs        D   KC  HOU       True           5.00  2500.0   
30   Patrick Mahomes II       QB   KC  HOU       True          20.82  7500.0   
58         Kenyan Drake       RB  MIA  WAS       True          13.00  4400.0   
62         Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
124       George Kittle       TE   SF  LAR      False          21.30  5200.0   
132        Travis Kelce       TE   KC  HOU       True           9.80  7000.0   
197      Robby Anderson       WR  NYJ  DAL       True          26.50  4000.0   
198         Tyreek Hill       WR   KC  HOU       True          25.00  6900.0   
209    Larry Fitzgerald       WR  ARI  ATL       True          12.90  6100.0   

     points_projected  sdPts_projected  tier   player_id  
11           7.676000         0.600442     4     D_KC_11  
30          22.202200         1.551496     1    QB_KC_3

Actual week score: 134.0
               player position team  opp  home_team  points_actual  salary  \
11             Chiefs        D   KC  HOU       True            5.0  2500.0   
26     Russell Wilson       QB  SEA  CLE      False           28.9  6600.0   
64       Chris Carson       RB  SEA  CLE      False           28.9  6000.0   
71    Phillip Lindsay       RB  DEN  TEN       True           15.5  5300.0   
123     Austin Hooper       TE  ATL  ARI      False           28.7  5000.0   
146       Will Dissly       TE  SEA  CLE      False            0.0  4900.0   
209  Larry Fitzgerald       WR  ARI  ATL       True           12.9  6100.0   
210     Tyler Lockett       WR  SEA  CLE      False           12.8  6400.0   
216      Amari Cooper       WR  DAL  NYJ      False            1.3  7000.0   

     points_projected  sdPts_projected  tier   player_id  
11           7.676000         0.600442     4     D_KC_11  
26          20.593821         0.712899     3   QB_SEA_26  
64          16.20

Actual week score: 132.14
             player position team  opp  home_team  points_actual  salary  \
11           Chiefs        D   KC  HOU       True           5.00  2500.0   
27     Carson Wentz       QB  PHI  MIN      False          24.54  6000.0   
61       Nick Chubb       RB  CLE  SEA       True          32.90  7300.0   
85        Joe Mixon       RB  CIN  BAL      False           5.90  5500.0   
133       Zach Ertz       TE  PHI  MIN      False           8.40  5400.0   
197  Robby Anderson       WR  NYJ  DAL       True          26.50  4000.0   
199  Alshon Jeffery       WR  PHI  MIN      False          23.60  5800.0   
216    Amari Cooper       WR  DAL  NYJ      False           1.30  7000.0   
240      Tyler Boyd       WR  CIN  BAL      False           4.00  6300.0   

     points_projected  sdPts_projected  tier   player_id  
11           7.676000         0.600442     4     D_KC_11  
27          17.933148         1.576590     5   QB_PHI_27  
61          18.649625         0.9123

...

Actual week score: 97.82
                 player position team  opp  home_team  points_actual  salary  \
16               Eagles        D  PHI  MIN      False           1.00  3000.0   
30   Patrick Mahomes II       QB   KC  HOU       True          20.82  7500.0   
96        Malcolm Brown       RB  LAR   SF       True           4.00  4300.0   
100           Ito Smith       RB  ATL  ARI      False           0.60  4300.0   
132        Travis Kelce       TE   KC  HOU       True           9.80  7000.0   
172        D.K. Metcalf       WR  SEA  CLE      False          11.30  4700.0   
191       Brandin Cooks       WR  LAR   SF       True           6.20  5400.0   
198         Tyreek Hill       WR   KC  HOU       True          25.00  6900.0   
211   Odell Beckham Jr.       WR  CLE  SEA       True          19.10  6800.0   

     points_projected  sdPts_projected  tier   player_id  
16           6.194667         0.444545     5    D_PHI_16  
30          22.202200         1.551496     1    QB_KC_30

Actual week score: 147.0
               player position team  opp  home_team  points_actual  salary  \
2              Saints        D   NO  JAX      False           11.0  3200.0   
24     Deshaun Watson       QB  HOU   KC      False           31.4  6700.0   
59       Duke Johnson       RB  HOU   KC      False           13.4  4100.0   
74      Tevin Coleman       RB   SF  LAR      False           14.1  4400.0   
119      Jordan Akins       TE  HOU   KC      False            6.9  3200.0   
191     Brandin Cooks       WR  LAR   SF       True            6.2  5400.0   
195      Stefon Diggs       WR  MIN  PHI       True           46.5  5900.0   
205   DeAndre Hopkins       WR  HOU   KC      False           16.5  7400.0   
217  Emmanuel Sanders       WR  DEN  TEN       True            1.0  4800.0   

     points_projected  sdPts_projected  tier   player_id  
2            7.347714         1.458719     4      D_NO_2  
24          21.593686         0.510101     2   QB_HOU_24  
59           9.51

Actual week score: 140.54000000000002
              player position team  opp  home_team  points_actual  salary  \
1            Broncos        D  DEN  TEN       True          23.00  3100.0   
32       Case Keenum       QB  WAS  MIA      False          15.64  5000.0   
82     Jordan Howard       RB  PHI  MIN      False           4.90  4900.0   
90       Matt Breida       RB   SF  LAR      False          10.30  5100.0   
112  Jeremy Sprinkle       TE  WAS  MIA      False           4.40  2600.0   
125     Mark Andrews       TE  BAL  CIN       True          14.90  4800.0   
196   Terry McLaurin       WR  WAS  MIA      False          29.00  6000.0   
199   Alshon Jeffery       WR  PHI  MIN      False          23.60  5800.0   
207    Calvin Ridley       WR  ATL  ARI      False          14.80  5700.0   

     points_projected  sdPts_projected  tier   player_id  
1            7.690000         1.399451     4     D_DEN_1  
32          15.305700         1.853184     7   QB_WAS_32  
82          10

Actual week score: 99.9
            player position team  opp  home_team  points_actual  salary  \
2           Saints        D   NO  JAX      False           11.0  3200.0   
33     Andy Dalton       QB  CIN  BAL      False           14.6  5400.0   
59    Duke Johnson       RB  HOU   KC      False           13.4  4100.0   
67     Carlos Hyde       RB  HOU   KC      False           22.0  4400.0   
122   Tyler Eifert       TE  CIN  BAL      False            3.3  3500.0   
146    Will Dissly       TE  SEA  CLE      False            0.0  4900.0   
188  Jarvis Landry       WR  CLE  SEA       True            6.6  5200.0   
198    Tyreek Hill       WR   KC  HOU       True           25.0  6900.0   
240     Tyler Boyd       WR  CIN  BAL      False            4.0  6300.0   

     points_projected  sdPts_projected  tier   player_id  
2            7.347714         1.458719     4      D_NO_2  
33          16.575429         1.069878     7   QB_CIN_33  
59           9.517833         0.543083     8   R

Actual week score: 131.14000000000001
                player position team  opp  home_team  points_actual  salary  \
14              Browns        D  CLE  SEA       True           4.00  2800.0   
44       Lamar Jackson       QB  BAL  CIN       True          33.64  6900.0   
46       Royce Freeman       RB  DEN  TEN       True          12.60  4500.0   
87        LeSean McCoy       RB   KC  HOU       True           6.40  5600.0   
125       Mark Andrews       TE  BAL  CIN       True          14.90  4800.0   
179     Dede Westbrook       WR  JAX   NO       True           8.30  5100.0   
195       Stefon Diggs       WR  MIN  PHI       True          46.50  5900.0   
225  Demarcus Robinson       WR   KC  HOU       True           0.00  5900.0   
235       Willie Snead       WR  BAL  CIN       True           4.80  5500.0   

     points_projected  sdPts_projected  tier   player_id  
14           6.444667         0.874345     4    D_CLE_14  
44          23.693690         1.568820     1   QB_BAL

In [84]:
import math
no_d_vs_off =[["QB", "D"], ["WR", "D"], ["RB", "D"], ["TE", "D"]]
prob, player_vars = get_basic_dfs_solver(df, pos_max, pos_min, proj_type='tier_avg',
                                         opposing_player_exclusions=no_d_vs_off,
                                         stacks=[["QB", "WR", "TE/RB:1"]],
                                         max_offensive_teams=5,
                                         min_offensive_teams=4,
                                         max_per_team=4,
                                         use_actual_points=False)

df = df[~df.player.isin(["Pharoh Cooper", "Luke Willson"])].reset_index(drop=True)
num_lineups = 200
max_qb_exposure = 1.0
max_lineups_for_one_qb = int(math.ceil(num_lineups*max_qb_exposure))
qb_exposure = {}

max_points = -1
max_overlap = 4
for i in range(num_lineups):
    print("Lineup {0}".format(i))
    prob.solve()
    score_df = output_performance(prob, df, print_points_actual=True)
    print(score_df)
    lineup = score_df.player_id.tolist()
    if score_df.points_actual.sum() > max_points:
        max_points = score_df.points_actual.sum()
    
    # See if we need to remove QB from consideration
    qb = score_df[score_df.position == "QB"].player_id.tolist()[0]
    if qb in qb_exposure:
        qb_exposure[qb] += 1
    else:
        qb_exposure[qb] = 1
    
    # If QB reaches max exposure remove from future lineups
    if qb_exposure[qb] >= max_lineups_for_one_qb:
        print("Reached lineup exposure max for QB: {0}".format(qb))
        prob += player_vars[qb] == 0
    
    print("Best lineup to point: {0}".format(max_points))
    prob += lpSum([player_vars[player] for player in lineup]) <= max_overlap

print("Max points: {0}".format(max_points))

Stack: QB_WR_TE/RB:1_0_0. Pos: QB, WR, RB. Opp Pos: 
Stack: QB_WR_TE/RB:1_0_1. Pos: QB, WR, TE. Opp Pos: 
Lineup 0
Actual week score: 139.53999999999996
              player position team  opp  home_team  points_actual  salary  \
17              Jets        D  NYJ  DAL       True           1.00  1500.0   
22         Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
58      Kenyan Drake       RB  MIA  WAS       True          13.00  4400.0   
62      Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
71   Phillip Lindsay       RB  DEN  TEN       True          15.50  5300.0   
123    Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
183     Robert Woods       WR  LAR   SF       True           7.60  5600.0   
200      Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
213      Cooper Kupp       WR  LAR   SF       True           5.70  7100.0   

     points_projected  sdPts_projected  tier   player_id  
17           6.50

Actual week score: 139.10000000000002
               player position team  opp  home_team  points_actual  salary  \
11             Chiefs        D   KC  HOU       True            5.0  2500.0   
43       Kyler Murray       QB  ARI  ATL       True           31.8  6500.0   
58       Kenyan Drake       RB  MIA  WAS       True           13.0  4400.0   
62       Le'Veon Bell       RB  NYJ  DAL       True           12.3  6400.0   
65      David Johnson       RB  ARI  ATL       True           28.2  7600.0   
123     Austin Hooper       TE  ATL  ARI      False           28.7  5000.0   
193      Mohamed Sanu       WR  ATL  ARI      False            5.9  4500.0   
209  Larry Fitzgerald       WR  ARI  ATL       True           12.9  6100.0   
216      Amari Cooper       WR  DAL  NYJ      False            1.3  7000.0   

     points_projected  sdPts_projected  tier   player_id  
11           7.676000         0.600442     4     D_KC_11  
43          21.183843         1.592853     2   QB_ARI_43  
58  

Actual week score: 91.58
                player position team  opp  home_team  points_actual  salary  \
11              Chiefs        D   KC  HOU       True           5.00  2500.0   
31        Dak Prescott       QB  DAL  NYJ      False          18.18  6200.0   
58        Kenyan Drake       RB  MIA  WAS       True          13.00  4400.0   
62        Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
70   Leonard Fournette       RB  JAX   NO       True          17.80  6700.0   
130       Jason Witten       TE  DAL  NYJ      False          10.70  3900.0   
183       Robert Woods       WR  LAR   SF       True           7.60  5600.0   
213        Cooper Kupp       WR  LAR   SF       True           5.70  7100.0   
216       Amari Cooper       WR  DAL  NYJ      False           1.30  7000.0   

     points_projected  sdPts_projected  tier   player_id  
11           7.676000         0.600442     4     D_KC_11  
31          20.460943         0.933020     3   QB_DAL_31  
58     

Actual week score: 157.54
              player position team  opp  home_team  points_actual  salary  \
17              Jets        D  NYJ  DAL       True           1.00  1500.0   
22         Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
62      Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
66   Devonta Freeman       RB  ATL  ARI      False          26.80  5800.0   
90       Matt Breida       RB   SF  LAR      False          10.30  5100.0   
133        Zach Ertz       TE  PHI  MIN      False           8.40  5400.0   
197   Robby Anderson       WR  NYJ  DAL       True          26.50  4000.0   
200      Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
205  DeAndre Hopkins       WR  HOU   KC      False          16.50  7400.0   

     points_projected  sdPts_projected  tier   player_id  
17           6.504800         0.477279     4    D_NYJ_17  
22          21.868021         1.083732     2   QB_ATL_22  
62          20.259054     

Actual week score: 148.84
                player position team  opp  home_team  points_actual  salary  \
11              Chiefs        D   KC  HOU       True           5.00  2500.0   
22           Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
58        Kenyan Drake       RB  MIA  WAS       True          13.00  4400.0   
70   Leonard Fournette       RB  JAX   NO       True          17.80  6700.0   
123      Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
133          Zach Ertz       TE  PHI  MIN      False           8.40  5400.0   
185         D.J. Chark       WR  JAX   NO       True           7.30  5500.0   
200        Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
209   Larry Fitzgerald       WR  ARI  ATL       True          12.90  6100.0   

     points_projected  sdPts_projected  tier   player_id  
11           7.676000         0.600442     4     D_KC_11  
22          21.868021         1.083732     2   QB_ATL_22  
58    

...

Actual week score: 151.62
                player position team  opp  home_team  points_actual  salary  \
4             Redskins        D  WAS  MIA      False          10.00  3200.0   
28         Sam Darnold       QB  NYJ  DAL       True          23.62  5100.0   
61          Nick Chubb       RB  CLE  SEA       True          32.90  7300.0   
62        Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
70   Leonard Fournette       RB  JAX   NO       True          17.80  6700.0   
133          Zach Ertz       TE  PHI  MIN      False           8.40  5400.0   
185         D.J. Chark       WR  JAX   NO       True           7.30  5500.0   
197     Robby Anderson       WR  NYJ  DAL       True          26.50  4000.0   
210      Tyler Lockett       WR  SEA  CLE      False          12.80  6400.0   

     points_projected  sdPts_projected  tier   player_id  
4            9.298667         1.180995     3     D_WAS_4  
28          13.281367         2.502780     9   QB_NYJ_28  
61    

Actual week score: 115.82000000000001
              player position team  opp  home_team  points_actual  salary  \
19         Cardinals        D  ARI  ATL       True           1.00  1900.0   
28       Sam Darnold       QB  NYJ  DAL       True          23.62  5100.0   
62      Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
64      Chris Carson       RB  SEA  CLE      False          28.90  6000.0   
146      Will Dissly       TE  SEA  CLE      False           0.00  4900.0   
197   Robby Anderson       WR  NYJ  DAL       True          26.50  4000.0   
205  DeAndre Hopkins       WR  HOU   KC      False          16.50  7400.0   
213      Cooper Kupp       WR  LAR   SF       True           5.70  7100.0   
216     Amari Cooper       WR  DAL  NYJ      False           1.30  7000.0   

     points_projected  sdPts_projected  tier   player_id  
19           5.030000         1.515305     5    D_ARI_19  
28          13.281367         2.502780     9   QB_NYJ_28  
62          20

Actual week score: 149.34000000000003
              player position team  opp  home_team  points_actual  salary  \
15            Titans        D  TEN  DEN      False           4.00  2900.0   
22         Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
58      Kenyan Drake       RB  MIA  WAS       True          13.00  4400.0   
60       Dalvin Cook       RB  MIN  PHI       True          13.40  8400.0   
123    Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
193     Mohamed Sanu       WR  ATL  ARI      False           5.90  4500.0   
200      Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
206  Jamison Crowder       WR  NYJ  DAL       True          15.80  4000.0   
210    Tyler Lockett       WR  SEA  CLE      False          12.80  6400.0   

     points_projected  sdPts_projected  tier   player_id  
15           7.489429         1.032126     4    D_TEN_15  
22          21.868021         1.083732     2   QB_ATL_22  
58          14

Actual week score: 121.1
               player position team  opp  home_team  points_actual  salary  \
0             Falcons        D  ATL  ARI      False           -1.0  2300.0   
24     Deshaun Watson       QB  HOU   KC      False           31.4  6700.0   
67        Carlos Hyde       RB  HOU   KC      False           22.0  4400.0   
72        Mark Ingram       RB  BAL  CIN       True           15.4  6600.0   
89    Damien Williams       RB   KC  HOU       True            9.0  5700.0   
125      Mark Andrews       TE  BAL  CIN       True           14.9  4800.0   
194  Courtland Sutton       WR  DEN  TEN       True           11.6  5000.0   
205   DeAndre Hopkins       WR  HOU   KC      False           16.5  7400.0   
216      Amari Cooper       WR  DAL  NYJ      False            1.3  7000.0   

     points_projected  sdPts_projected  tier   player_id  
0            6.911600         1.018358     4     D_ATL_0  
24          21.593686         0.510101     2   QB_HOU_24  
67          11.51

Actual week score: 147.03999999999996
            player position team  opp  home_team  points_actual  salary  \
4         Redskins        D  WAS  MIA      False          10.00  3200.0   
22       Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
67     Carlos Hyde       RB  HOU   KC      False          22.00  4400.0   
90     Matt Breida       RB   SF  LAR      False          10.30  5100.0   
123  Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
133      Zach Ertz       TE  PHI  MIN      False           8.40  5400.0   
191  Brandin Cooks       WR  LAR   SF       True           6.20  5400.0   
200    Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
213    Cooper Kupp       WR  LAR   SF       True           5.70  7100.0   

     points_projected  sdPts_projected  tier   player_id  
4            9.298667         1.180995     3     D_WAS_4  
22          21.868021         1.083732     2   QB_ATL_22  
67          11.511762         1.47

In [85]:
import math
no_d_vs_off =[["QB", "D"], ["WR", "D"], ["RB", "D"], ["TE", "D"]]
prob, player_vars = get_basic_dfs_solver(df, pos_max, pos_min, proj_type='tier_avg',
                                         opposing_player_exclusions=no_d_vs_off,
                                         stacks=[["QB", "WR", "TE"]],
                                         max_offensive_teams=5,
                                         min_offensive_teams=4,
                                         max_per_team=4,
                                         use_actual_points=False)

df = df[~df.player.isin(["Pharoh Cooper", "Luke Willson"])].reset_index(drop=True)
num_lineups = 200
max_qb_exposure = 1.0
max_lineups_for_one_qb = int(math.ceil(num_lineups*max_qb_exposure))
qb_exposure = {}

max_points = -1
max_overlap = 4
for i in range(num_lineups):
    print("Lineup {0}".format(i))
    prob.solve()
    score_df = output_performance(prob, df, print_points_actual=True)
    print(score_df)
    lineup = score_df.player_id.tolist()
    if score_df.points_actual.sum() > max_points:
        max_points = score_df.points_actual.sum()
    
    # See if we need to remove QB from consideration
    qb = score_df[score_df.position == "QB"].player_id.tolist()[0]
    if qb in qb_exposure:
        qb_exposure[qb] += 1
    else:
        qb_exposure[qb] = 1
    
    # If QB reaches max exposure remove from future lineups
    if qb_exposure[qb] >= max_lineups_for_one_qb:
        print("Reached lineup exposure max for QB: {0}".format(qb))
        prob += player_vars[qb] == 0
    
    print("Best lineup to point: {0}".format(max_points))
    prob += lpSum([player_vars[player] for player in lineup]) <= max_overlap

print("Max points: {0}".format(max_points))

Stack: QB_WR_TE_0. Pos: QB, WR, TE. Opp Pos: 
Lineup 0
Actual week score: 139.53999999999996
              player position team  opp  home_team  points_actual  salary  \
17              Jets        D  NYJ  DAL       True           1.00  1500.0   
22         Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
58      Kenyan Drake       RB  MIA  WAS       True          13.00  4400.0   
62      Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
71   Phillip Lindsay       RB  DEN  TEN       True          15.50  5300.0   
123    Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
183     Robert Woods       WR  LAR   SF       True           7.60  5600.0   
200      Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
213      Cooper Kupp       WR  LAR   SF       True           5.70  7100.0   

     points_projected  sdPts_projected  tier   player_id  
17           6.504800         0.477279     4    D_NYJ_17  
22          21.868

Actual week score: 92.62
               player position team  opp  home_team  points_actual  salary  \
17               Jets        D  NYJ  DAL       True           1.00  1500.0   
40         Jared Goff       QB  LAR   SF       True           2.12  6100.0   
61         Nick Chubb       RB  CLE  SEA       True          32.90  7300.0   
62       Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
135    Gerald Everett       TE  LAR   SF       True           2.90  3600.0   
183      Robert Woods       WR  LAR   SF       True           7.60  5600.0   
194  Courtland Sutton       WR  DEN  TEN       True          11.60  5000.0   
205   DeAndre Hopkins       WR  HOU   KC      False          16.50  7400.0   
213       Cooper Kupp       WR  LAR   SF       True           5.70  7100.0   

     points_projected  sdPts_projected  tier   player_id  
17           6.504800         0.477279     4    D_NYJ_17  
40          19.365736         1.232886     4   QB_LAR_40  
61          18.64

Actual week score: 112.3
                player position team  opp  home_team  points_actual  salary  \
0              Falcons        D  ATL  ARI      False           -1.0  2300.0   
24      Deshaun Watson       QB  HOU   KC      False           31.4  6700.0   
62        Le'Veon Bell       RB  NYJ  DAL       True           12.3  6400.0   
70   Leonard Fournette       RB  JAX   NO       True           17.8  6700.0   
71     Phillip Lindsay       RB  DEN  TEN       True           15.5  5300.0   
119       Jordan Akins       TE  HOU   KC      False            6.9  3200.0   
194   Courtland Sutton       WR  DEN  TEN       True           11.6  5000.0   
205    DeAndre Hopkins       WR  HOU   KC      False           16.5  7400.0   
216       Amari Cooper       WR  DAL  NYJ      False            1.3  7000.0   

     points_projected  sdPts_projected  tier   player_id  
0            6.911600         1.018358     4     D_ATL_0  
24          21.593686         0.510101     2   QB_HOU_24  
62     

Actual week score: 151.54000000000002
               player position team  opp  home_team  points_actual  salary  \
4            Redskins        D  WAS  MIA      False          10.00  3200.0   
27       Carson Wentz       QB  PHI  MIN      False          24.54  6000.0   
62       Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
71    Phillip Lindsay       RB  DEN  TEN       True          15.50  5300.0   
123     Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
133         Zach Ertz       TE  PHI  MIN      False           8.40  5400.0   
194  Courtland Sutton       WR  DEN  TEN       True          11.60  5000.0   
199    Alshon Jeffery       WR  PHI  MIN      False          23.60  5800.0   
204    Michael Thomas       WR   NO  JAX      False          16.90  7800.0   

     points_projected  sdPts_projected  tier   player_id  
4            9.298667         1.180995     3     D_WAS_4  
27          17.933148         1.576590     5   QB_PHI_27  
62  

Actual week score: 145.50000000000003
               player position team  opp  home_team  points_actual  salary  \
17               Jets        D  NYJ  DAL       True            1.0  1500.0   
24     Deshaun Watson       QB  HOU   KC      False           31.4  6700.0   
62       Le'Veon Bell       RB  NYJ  DAL       True           12.3  6400.0   
65      David Johnson       RB  ARI  ATL       True           28.2  7600.0   
119      Jordan Akins       TE  HOU   KC      False            6.9  3200.0   
123     Austin Hooper       TE  ATL  ARI      False           28.7  5000.0   
183      Robert Woods       WR  LAR   SF       True            7.6  5600.0   
205   DeAndre Hopkins       WR  HOU   KC      False           16.5  7400.0   
209  Larry Fitzgerald       WR  ARI  ATL       True           12.9  6100.0   

     points_projected  sdPts_projected  tier   player_id  
17           6.504800         0.477279     4    D_NYJ_17  
24          21.593686         0.510101     2   QB_HOU_24  
62  

...

Actual week score: 161.54000000000002
                player position team  opp  home_team  points_actual  salary  \
4             Redskins        D  WAS  MIA      False          10.00  3200.0   
27        Carson Wentz       QB  PHI  MIN      False          24.54  6000.0   
64        Chris Carson       RB  SEA  CLE      False          28.90  6000.0   
70   Leonard Fournette       RB  JAX   NO       True          17.80  6700.0   
133          Zach Ertz       TE  PHI  MIN      False           8.40  5400.0   
146        Will Dissly       TE  SEA  CLE      False           0.00  4900.0   
197     Robby Anderson       WR  NYJ  DAL       True          26.50  4000.0   
199     Alshon Jeffery       WR  PHI  MIN      False          23.60  5800.0   
200        Julio Jones       WR  ATL  ARI      False          21.80  8000.0   

     points_projected  sdPts_projected  tier   player_id  
4            9.298667         1.180995     3     D_WAS_4  
27          17.933148         1.576590     5   QB_PHI

Actual week score: 105.92000000000002
                player position team  opp  home_team  points_actual  salary  \
11              Chiefs        D   KC  HOU       True           5.00  2500.0   
38     Gardner Minshew       QB  JAX   NO       True           5.62  5000.0   
58        Kenyan Drake       RB  MIA  WAS       True          13.00  4400.0   
65       David Johnson       RB  ARI  ATL       True          28.20  7600.0   
70   Leonard Fournette       RB  JAX   NO       True          17.80  6700.0   
157        Geoff Swaim       TE  JAX   NO       True           1.50  2900.0   
185         D.J. Chark       WR  JAX   NO       True           7.30  5500.0   
200        Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
213        Cooper Kupp       WR  LAR   SF       True           5.70  7100.0   

     points_projected  sdPts_projected  tier   player_id  
11           7.676000         0.600442     4     D_KC_11  
38          17.176630         1.793378     6   QB_JAX

Actual week score: 90.32
             player position team  opp  home_team  points_actual  salary  \
7           Vikings        D  MIN  PHI       True           9.00  2600.0   
40       Jared Goff       QB  LAR   SF       True           2.12  6100.0   
61       Nick Chubb       RB  CLE  SEA       True          32.90  7300.0   
85        Joe Mixon       RB  CIN  BAL      False           5.90  5500.0   
135  Gerald Everett       TE  LAR   SF       True           2.90  3600.0   
197  Robby Anderson       WR  NYJ  DAL       True          26.50  4000.0   
213     Cooper Kupp       WR  LAR   SF       True           5.70  7100.0   
216    Amari Cooper       WR  DAL  NYJ      False           1.30  7000.0   
240      Tyler Boyd       WR  CIN  BAL      False           4.00  6300.0   

     points_projected  sdPts_projected  tier   player_id  
7            7.025143         0.727103     4     D_MIN_7  
40          19.365736         1.232886     4   QB_LAR_40  
61          18.649625         0.91238

Actual week score: 101.88000000000001
               player position team  opp  home_team  points_actual  salary  \
4            Redskins        D  WAS  MIA      False          10.00  3200.0   
31       Dak Prescott       QB  DAL  NYJ      False          18.18  6200.0   
64       Chris Carson       RB  SEA  CLE      False          28.90  6000.0   
75       Alvin Kamara       RB   NO  JAX      False          13.60  8000.0   
130      Jason Witten       TE  DAL  NYJ      False          10.70  3900.0   
146       Will Dissly       TE  SEA  CLE      False           0.00  4900.0   
183      Robert Woods       WR  LAR   SF       True           7.60  5600.0   
194  Courtland Sutton       WR  DEN  TEN       True          11.60  5000.0   
216      Amari Cooper       WR  DAL  NYJ      False           1.30  7000.0   

     points_projected  sdPts_projected  tier   player_id  
4            9.298667         1.180995     3     D_WAS_4  
31          20.460943         0.933020     3   QB_DAL_31  
64  

Actual week score: 155.82000000000002
              player position team  opp  home_team  points_actual  salary  \
11            Chiefs        D   KC  HOU       True           5.00  2500.0   
25      Kirk Cousins       QB  MIN  PHI       True          31.32  5200.0   
62      Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
71   Phillip Lindsay       RB  DEN  TEN       True          15.50  5300.0   
116     Kyle Rudolph       TE  MIN  PHI       True           6.60  3000.0   
123    Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
200      Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
203     Adam Thielen       WR  MIN  PHI       True          17.70  6700.0   
204   Michael Thomas       WR   NO  JAX      False          16.90  7800.0   

     points_projected  sdPts_projected  tier   player_id  
11           7.676000         0.600442     4     D_KC_11  
25          16.821000         1.250591     6   QB_MIN_25  
62          20

In [92]:
pos_max = {
    "QB": 1,
    "RB": 2,
    "WR": 4,
    "TE": 1,
    "D": 1
}

pos_min = {
    "QB": 1,
    "RB": 2,
    "WR": 3,
    "TE": 1,
    "D": 1
}

no_d_vs_off =[["QB", "D"], ["WR", "D"], ["RB", "D"], ["TE", "D"]]
prob, player_vars = get_basic_dfs_solver(df, pos_max, pos_min, proj_type='avg',
                                         opposing_player_exclusions=no_d_vs_off,
                                         stacks=[["QB", "WR", "TE"]],
                                         game_stacks=[4,2],
                                         use_actual_points=False)

df = df[~df.player.isin(["Pharoh Cooper", "Luke Willson"])].reset_index(drop=True)
num_lineups = 200
max_qb_exposure = 1.0
max_lineups_for_one_qb = int(math.ceil(num_lineups*max_qb_exposure))
qb_exposure = {}

max_points = -1
max_overlap = 5
for i in range(num_lineups):
    print("Lineup {0}".format(i))
    prob.solve()
    score_df = output_performance(prob, df, print_points_actual=True)
    print(score_df)
    lineup = score_df.player_id.tolist()
    if score_df.points_actual.sum() > max_points:
        max_points = score_df.points_actual.sum()
    
    # See if we need to remove QB from consideration
    qb = score_df[score_df.position == "QB"].player_id.tolist()[0]
    if qb in qb_exposure:
        qb_exposure[qb] += 1
    else:
        qb_exposure[qb] = 1
    
    # If QB reaches max exposure remove from future lineups
    if qb_exposure[qb] >= max_lineups_for_one_qb:
        print("Reached lineup exposure max for QB: {0}".format(qb))
        prob += player_vars[qb] == 0
    
    print("Best lineup to point: {0}".format(max_points))
    prob += lpSum([player_vars[player] for player in lineup]) <= max_overlap

print("Max points: {0}".format(max_points))

Stack: QB_WR_TE_0. Pos: QB, WR, TE. Opp Pos: 
Lineup 0
Actual week score: 159.83999999999997
               player position team  opp  home_team  points_actual  salary  \
11             Chiefs        D   KC  HOU       True           5.00  2500.0   
22          Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
58       Kenyan Drake       RB  MIA  WAS       True          13.00  4400.0   
62       Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
123     Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
197    Robby Anderson       WR  NYJ  DAL       True          26.50  4000.0   
200       Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
209  Larry Fitzgerald       WR  ARI  ATL       True          12.90  6100.0   
213       Cooper Kupp       WR  LAR   SF       True           5.70  7100.0   

     points_projected  sdPts_projected  tier   player_id  
11           7.676000         0.600442     4     D_KC_11  
22      

Actual week score: 73.22
                player position team  opp  home_team  points_actual  salary  \
17                Jets        D  NYJ  DAL       True           1.00  1500.0   
40          Jared Goff       QB  LAR   SF       True           2.12  6100.0   
62        Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
70   Leonard Fournette       RB  JAX   NO       True          17.80  6700.0   
135     Gerald Everett       TE  LAR   SF       True           2.90  3600.0   
183       Robert Woods       WR  LAR   SF       True           7.60  5600.0   
185         D.J. Chark       WR  JAX   NO       True           7.30  5500.0   
205    DeAndre Hopkins       WR  HOU   KC      False          16.50  7400.0   
213        Cooper Kupp       WR  LAR   SF       True           5.70  7100.0   

     points_projected  sdPts_projected  tier   player_id  
17           6.504800         0.477279     4    D_NYJ_17  
40          19.365736         1.232886     4   QB_LAR_40  
62     

Actual week score: 56.42
              player position team  opp  home_team  points_actual  salary  \
11            Chiefs        D   KC  HOU       True           5.00  2500.0   
40        Jared Goff       QB  LAR   SF       True           2.12  6100.0   
62      Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
71   Phillip Lindsay       RB  DEN  TEN       True          15.50  5300.0   
135   Gerald Everett       TE  LAR   SF       True           2.90  3600.0   
183     Robert Woods       WR  LAR   SF       True           7.60  5600.0   
213      Cooper Kupp       WR  LAR   SF       True           5.70  7100.0   
216     Amari Cooper       WR  DAL  NYJ      False           1.30  7000.0   
240       Tyler Boyd       WR  CIN  BAL      False           4.00  6300.0   

     points_projected  sdPts_projected  tier   player_id  
11           7.676000         0.600442     4     D_KC_11  
40          19.365736         1.232886     4   QB_LAR_40  
62          20.259054      

Actual week score: 131.84
              player position team  opp  home_team  points_actual  salary  \
0            Falcons        D  ATL  ARI      False          -1.00  2300.0   
22         Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
58      Kenyan Drake       RB  MIA  WAS       True          13.00  4400.0   
89   Damien Williams       RB   KC  HOU       True           9.00  5700.0   
123    Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
193     Mohamed Sanu       WR  ATL  ARI      False           5.90  4500.0   
200      Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
205  DeAndre Hopkins       WR  HOU   KC      False          16.50  7400.0   
240       Tyler Boyd       WR  CIN  BAL      False           4.00  6300.0   

     points_projected  sdPts_projected  tier   player_id  
0            6.911600         1.018358     4     D_ATL_0  
22          21.868021         1.083732     2   QB_ATL_22  
58          14.752067     

Actual week score: 103.67999999999999
               player position team  opp  home_team  points_actual  salary  \
4            Redskins        D  WAS  MIA      False          10.00  3200.0   
31       Dak Prescott       QB  DAL  NYJ      False          18.18  6200.0   
62       Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
71    Phillip Lindsay       RB  DEN  TEN       True          15.50  5300.0   
130      Jason Witten       TE  DAL  NYJ      False          10.70  3900.0   
183      Robert Woods       WR  LAR   SF       True           7.60  5600.0   
194  Courtland Sutton       WR  DEN  TEN       True          11.60  5000.0   
205   DeAndre Hopkins       WR  HOU   KC      False          16.50  7400.0   
216      Amari Cooper       WR  DAL  NYJ      False           1.30  7000.0   

     points_projected  sdPts_projected  tier   player_id  
4            9.298667         1.180995     3     D_WAS_4  
31          20.460943         0.933020     3   QB_DAL_31  
62  

...

Actual week score: 101.3
              player position team  opp  home_team  points_actual  salary  \
0            Falcons        D  ATL  ARI      False           -1.0  2300.0   
24    Deshaun Watson       QB  HOU   KC      False           31.4  6700.0   
58      Kenyan Drake       RB  MIA  WAS       True           13.0  4400.0   
89   Damien Williams       RB   KC  HOU       True            9.0  5700.0   
119     Jordan Akins       TE  HOU   KC      False            6.9  3200.0   
185       D.J. Chark       WR  JAX   NO       True            7.3  5500.0   
204   Michael Thomas       WR   NO  JAX      False           16.9  7800.0   
205  DeAndre Hopkins       WR  HOU   KC      False           16.5  7400.0   
216     Amari Cooper       WR  DAL  NYJ      False            1.3  7000.0   

     points_projected  sdPts_projected  tier   player_id  
0            6.911600         1.018358     4     D_ATL_0  
24          21.593686         0.510101     2   QB_HOU_24  
58          14.752067      

Actual week score: 70.72
                player position team  opp  home_team  points_actual  salary  \
15              Titans        D  TEN  DEN      False           4.00  2900.0   
40          Jared Goff       QB  LAR   SF       True           2.12  6100.0   
62        Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
70   Leonard Fournette       RB  JAX   NO       True          17.80  6700.0   
135     Gerald Everett       TE  LAR   SF       True           2.90  3600.0   
177     Michael Gallup       WR  DAL  NYJ      False           8.80  5600.0   
206    Jamison Crowder       WR  NYJ  DAL       True          15.80  4000.0   
213        Cooper Kupp       WR  LAR   SF       True           5.70  7100.0   
216       Amari Cooper       WR  DAL  NYJ      False           1.30  7000.0   

     points_projected  sdPts_projected  tier   player_id  
15           7.489429         1.032126     4    D_TEN_15  
40          19.365736         1.232886     4   QB_LAR_40  
62     

Actual week score: 130.04
              player position team  opp  home_team  points_actual  salary  \
4           Redskins        D  WAS  MIA      False          10.00  3200.0   
27      Carson Wentz       QB  PHI  MIN      False          24.54  6000.0   
69     Miles Sanders       RB  PHI  MIN      False          18.20  4200.0   
71   Phillip Lindsay       RB  DEN  TEN       True          15.50  5300.0   
133        Zach Ertz       TE  PHI  MIN      False           8.40  5400.0   
183     Robert Woods       WR  LAR   SF       True           7.60  5600.0   
199   Alshon Jeffery       WR  PHI  MIN      False          23.60  5800.0   
205  DeAndre Hopkins       WR  HOU   KC      False          16.50  7400.0   
213      Cooper Kupp       WR  LAR   SF       True           5.70  7100.0   

     points_projected  sdPts_projected  tier   player_id  
4            9.298667         1.180995     3     D_WAS_4  
27          17.933148         1.576590     5   QB_PHI_27  
69          10.587167     

Actual week score: 166.04
              player position team  opp  home_team  points_actual  salary  \
17              Jets        D  NYJ  DAL       True           1.00  1500.0   
22         Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
66   Devonta Freeman       RB  ATL  ARI      False          26.80  5800.0   
71   Phillip Lindsay       RB  DEN  TEN       True          15.50  5300.0   
123    Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
185       D.J. Chark       WR  JAX   NO       True           7.30  5500.0   
200      Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
204   Michael Thomas       WR   NO  JAX      False          16.90  7800.0   
208       Auden Tate       WR  CIN  BAL      False          14.10  4500.0   

     points_projected  sdPts_projected  tier   player_id  
17           6.504800         0.477279     4    D_NYJ_17  
22          21.868021         1.083732     2   QB_ATL_22  
66          14.427700     

Actual week score: 123.44000000000001
                player position team  opp  home_team  points_actual  salary  \
11              Chiefs        D   KC  HOU       True           5.00  2500.0   
27        Carson Wentz       QB  PHI  MIN      False          24.54  6000.0   
60         Dalvin Cook       RB  MIN  PHI       True          13.40  8400.0   
70   Leonard Fournette       RB  JAX   NO       True          17.80  6700.0   
133          Zach Ertz       TE  PHI  MIN      False           8.40  5400.0   
183       Robert Woods       WR  LAR   SF       True           7.60  5600.0   
185         D.J. Chark       WR  JAX   NO       True           7.30  5500.0   
199     Alshon Jeffery       WR  PHI  MIN      False          23.60  5800.0   
206    Jamison Crowder       WR  NYJ  DAL       True          15.80  4000.0   

     points_projected  sdPts_projected  tier   player_id  
11           7.676000         0.600442     4     D_KC_11  
27          17.933148         1.576590     5   QB_PHI

In [93]:
pos_max = {
    "QB": 1,
    "RB": 2,
    "WR": 4,
    "TE": 1,
    "D": 1
}

pos_min = {
    "QB": 1,
    "RB": 2,
    "WR": 4,
    "TE": 1,
    "D": 1
}

no_d_vs_off =[["QB", "D"], ["WR", "D"], ["RB", "D"], ["TE", "D"]]
prob, player_vars = get_basic_dfs_solver(df, pos_max, pos_min, proj_type='avg',
                                         opposing_player_exclusions=no_d_vs_off,
                                         stacks=[["QB", "WR", "TE"]],
                                         game_stacks=[4,2],
                                         use_actual_points=False,
                                         exclude_teams=["MIA"])

df = df[~df.player.isin(["Pharoh Cooper", "Luke Willson"])].reset_index(drop=True)
num_lineups = 200
max_qb_exposure = 1.0
max_lineups_for_one_qb = int(math.ceil(num_lineups*max_qb_exposure))
qb_exposure = {}

max_points = -1
max_overlap = 5
for i in range(num_lineups):
    print("Lineup {0}".format(i))
    prob.solve()
    score_df = output_performance(prob, df, print_points_actual=True)
    print(score_df)
    lineup = score_df.player_id.tolist()
    if score_df.points_actual.sum() > max_points:
        max_points = score_df.points_actual.sum()
    
    # See if we need to remove QB from consideration
    qb = score_df[score_df.position == "QB"].player_id.tolist()[0]
    if qb in qb_exposure:
        qb_exposure[qb] += 1
    else:
        qb_exposure[qb] = 1
    
    # If QB reaches max exposure remove from future lineups
    if qb_exposure[qb] >= max_lineups_for_one_qb:
        print("Reached lineup exposure max for QB: {0}".format(qb))
        prob += player_vars[qb] == 0
    
    print("Best lineup to point: {0}".format(max_points))
    prob += lpSum([player_vars[player] for player in lineup]) <= max_overlap

print("Max points: {0}".format(max_points))

Stack: QB_WR_TE_0. Pos: QB, WR, TE. Opp Pos: 
Lineup 0
Actual week score: 162.54
                player position team  opp  home_team  points_actual  salary  \
17                Jets        D  NYJ  DAL       True           1.00  1500.0   
22           Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
62        Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
70   Leonard Fournette       RB  JAX   NO       True          17.80  6700.0   
123      Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
183       Robert Woods       WR  LAR   SF       True           7.60  5600.0   
197     Robby Anderson       WR  NYJ  DAL       True          26.50  4000.0   
200        Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
209   Larry Fitzgerald       WR  ARI  ATL       True          12.90  6100.0   

     points_projected  sdPts_projected  tier   player_id  
17           6.504800         0.477279     4    D_NYJ_17  
22        

Actual week score: 146.14
              player position team  opp  home_team  points_actual  salary  \
17              Jets        D  NYJ  DAL       True           1.00  1500.0   
22         Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
62      Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
67       Carlos Hyde       RB  HOU   KC      False          22.00  4400.0   
123    Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
193     Mohamed Sanu       WR  ATL  ARI      False           5.90  4500.0   
200      Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
205  DeAndre Hopkins       WR  HOU   KC      False          16.50  7400.0   
240       Tyler Boyd       WR  CIN  BAL      False           4.00  6300.0   

     points_projected  sdPts_projected  tier   player_id  
17           6.504800         0.477279     4    D_NYJ_17  
22          21.868021         1.083732     2   QB_ATL_22  
62          20.259054     

Actual week score: 142.83999999999997
               player position team  opp  home_team  points_actual  salary  \
17               Jets        D  NYJ  DAL       True           1.00  1500.0   
22          Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
62       Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
66    Devonta Freeman       RB  ATL  ARI      False          26.80  5800.0   
123     Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
194  Courtland Sutton       WR  DEN  TEN       True          11.60  5000.0   
200       Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
213       Cooper Kupp       WR  LAR   SF       True           5.70  7100.0   
217  Emmanuel Sanders       WR  DEN  TEN       True           1.00  4800.0   

     points_projected  sdPts_projected  tier   player_id  
17           6.504800         0.477279     4    D_NYJ_17  
22          21.868021         1.083732     2   QB_ATL_22  
62  

Actual week score: 94.4
              player position team  opp  home_team  points_actual  salary  \
17              Jets        D  NYJ  DAL       True            1.0  1500.0   
24    Deshaun Watson       QB  HOU   KC      False           31.4  6700.0   
62      Le'Veon Bell       RB  NYJ  DAL       True           12.3  6400.0   
89   Damien Williams       RB   KC  HOU       True            9.0  5700.0   
119     Jordan Akins       TE  HOU   KC      False            6.9  3200.0   
183     Robert Woods       WR  LAR   SF       True            7.6  5600.0   
205  DeAndre Hopkins       WR  HOU   KC      False           16.5  7400.0   
213      Cooper Kupp       WR  LAR   SF       True            5.7  7100.0   
240       Tyler Boyd       WR  CIN  BAL      False            4.0  6300.0   

     points_projected  sdPts_projected  tier   player_id  
17           6.504800         0.477279     4    D_NYJ_17  
24          21.593686         0.510101     2   QB_HOU_24  
62          20.259054       

Actual week score: 160.94
            player position team  opp  home_team  points_actual  salary  \
5          Bengals        D  CIN  BAL      False           9.00  1700.0   
22       Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
62    Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
64    Chris Carson       RB  SEA  CLE      False          28.90  6000.0   
123  Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
183   Robert Woods       WR  LAR   SF       True           7.60  5600.0   
193   Mohamed Sanu       WR  ATL  ARI      False           5.90  4500.0   
200    Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
210  Tyler Lockett       WR  SEA  CLE      False          12.80  6400.0   

     points_projected  sdPts_projected  tier   player_id  
5            4.689000         1.476738     6     D_CIN_5  
22          21.868021         1.083732     2   QB_ATL_22  
62          20.259054         0.592551     2  

...

Actual week score: 91.02
              player position team  opp  home_team  points_actual  salary  \
0            Falcons        D  ATL  ARI      False          -1.00  2300.0   
40        Jared Goff       QB  LAR   SF       True           2.12  6100.0   
64      Chris Carson       RB  SEA  CLE      False          28.90  6000.0   
71   Phillip Lindsay       RB  DEN  TEN       True          15.50  5300.0   
135   Gerald Everett       TE  LAR   SF       True           2.90  3600.0   
183     Robert Woods       WR  LAR   SF       True           7.60  5600.0   
205  DeAndre Hopkins       WR  HOU   KC      False          16.50  7400.0   
210    Tyler Lockett       WR  SEA  CLE      False          12.80  6400.0   
213      Cooper Kupp       WR  LAR   SF       True           5.70  7100.0   

     points_projected  sdPts_projected  tier   player_id  
0            6.911600         1.018358     4     D_ATL_0  
40          19.365736         1.232886     4   QB_LAR_40  
64          16.201905      

Actual week score: 70.72
             player position team  opp  home_team  points_actual  salary  \
15           Titans        D  TEN  DEN      False           4.00  2900.0   
40       Jared Goff       QB  LAR   SF       True           2.12  6100.0   
62     Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
64     Chris Carson       RB  SEA  CLE      False          28.90  6000.0   
135  Gerald Everett       TE  LAR   SF       True           2.90  3600.0   
185      D.J. Chark       WR  JAX   NO       True           7.30  5500.0   
191   Brandin Cooks       WR  LAR   SF       True           6.20  5400.0   
213     Cooper Kupp       WR  LAR   SF       True           5.70  7100.0   
216    Amari Cooper       WR  DAL  NYJ      False           1.30  7000.0   

     points_projected  sdPts_projected  tier   player_id  
15           7.489429         1.032126     4    D_TEN_15  
40          19.365736         1.232886     4   QB_LAR_40  
62          20.259054         0.59255

Actual week score: 138.74
              player position team  opp  home_team  points_actual  salary  \
0            Falcons        D  ATL  ARI      False          -1.00  2300.0   
22         Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
62      Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
66   Devonta Freeman       RB  ATL  ARI      False          26.80  5800.0   
123    Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
179   Dede Westbrook       WR  JAX   NO       True           8.30  5100.0   
189      Corey Davis       WR  TEN  DEN      False           6.60  4000.0   
200      Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
216     Amari Cooper       WR  DAL  NYJ      False           1.30  7000.0   

     points_projected  sdPts_projected  tier   player_id  
0            6.911600         1.018358     4     D_ATL_0  
22          21.868021         1.083732     2   QB_ATL_22  
62          20.259054     

Actual week score: 97.47999999999999
             player position team  opp  home_team  points_actual  salary  \
11           Chiefs        D   KC  HOU       True           5.00  2500.0   
31     Dak Prescott       QB  DAL  NYJ      False          18.18  6200.0   
62     Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
64     Chris Carson       RB  SEA  CLE      False          28.90  6000.0   
130    Jason Witten       TE  DAL  NYJ      False          10.70  3900.0   
177  Michael Gallup       WR  DAL  NYJ      False           8.80  5600.0   
188   Jarvis Landry       WR  CLE  SEA       True           6.60  5200.0   
213     Cooper Kupp       WR  LAR   SF       True           5.70  7100.0   
216    Amari Cooper       WR  DAL  NYJ      False           1.30  7000.0   

     points_projected  sdPts_projected  tier   player_id  
11           7.676000         0.600442     4     D_KC_11  
31          20.460943         0.933020     3   QB_DAL_31  
62          20.259054    

Actual week score: 146.24
               player position team  opp  home_team  points_actual  salary  \
14             Browns        D  CLE  SEA       True           4.00  2800.0   
22          Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
71    Phillip Lindsay       RB  DEN  TEN       True          15.50  5300.0   
89    Damien Williams       RB   KC  HOU       True           9.00  5700.0   
123     Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
177    Michael Gallup       WR  DAL  NYJ      False           8.80  5600.0   
194  Courtland Sutton       WR  DEN  TEN       True          11.60  5000.0   
200       Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
209  Larry Fitzgerald       WR  ARI  ATL       True          12.90  6100.0   

     points_projected  sdPts_projected  tier   player_id  
14           6.444667         0.874345     4    D_CLE_14  
22          21.868021         1.083732     2   QB_ATL_22  
71          15.1

In [94]:
pos_max = {
    "QB": 1,
    "RB": 2,
    "WR": 4,
    "TE": 1,
    "D": 1
}

pos_min = {
    "QB": 1,
    "RB": 2,
    "WR": 4,
    "TE": 1,
    "D": 1
}

no_d_vs_off =[["QB", "D"], ["WR", "D"], ["RB", "D"], ["TE", "D"]]
prob, player_vars = get_basic_dfs_solver(df, pos_max, pos_min, proj_type='avg',
                                         opposing_player_exclusions=no_d_vs_off,
                                         stacks=[["QB", "WR", "TE"]],
                                         game_stacks=[4,2],
                                         use_actual_points=False,
                                         exclude_teams=["MIA"])

df = df[~df.player.isin(["Pharoh Cooper", "Luke Willson"])].reset_index(drop=True)
num_lineups = 200
max_qb_exposure = 1.0
max_lineups_for_one_qb = int(math.ceil(num_lineups*max_qb_exposure))
qb_exposure = {}

max_points = -1
max_overlap = 4
for i in range(num_lineups):
    print("Lineup {0}".format(i))
    prob.solve()
    score_df = output_performance(prob, df, print_points_actual=True)
    print(score_df)
    lineup = score_df.player_id.tolist()
    if score_df.points_actual.sum() > max_points:
        max_points = score_df.points_actual.sum()
    
    # See if we need to remove QB from consideration
    qb = score_df[score_df.position == "QB"].player_id.tolist()[0]
    if qb in qb_exposure:
        qb_exposure[qb] += 1
    else:
        qb_exposure[qb] = 1
    
    # If QB reaches max exposure remove from future lineups
    if qb_exposure[qb] >= max_lineups_for_one_qb:
        print("Reached lineup exposure max for QB: {0}".format(qb))
        prob += player_vars[qb] == 0
    
    print("Best lineup to point: {0}".format(max_points))
    prob += lpSum([player_vars[player] for player in lineup]) <= max_overlap

print("Max points: {0}".format(max_points))

Stack: QB_WR_TE_0. Pos: QB, WR, TE. Opp Pos: 
Lineup 0
Actual week score: 162.54
                player position team  opp  home_team  points_actual  salary  \
17                Jets        D  NYJ  DAL       True           1.00  1500.0   
22           Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
62        Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
70   Leonard Fournette       RB  JAX   NO       True          17.80  6700.0   
123      Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
183       Robert Woods       WR  LAR   SF       True           7.60  5600.0   
197     Robby Anderson       WR  NYJ  DAL       True          26.50  4000.0   
200        Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
209   Larry Fitzgerald       WR  ARI  ATL       True          12.90  6100.0   

     points_projected  sdPts_projected  tier   player_id  
17           6.504800         0.477279     4    D_NYJ_17  
22        

Actual week score: 155.64
              player position team  opp  home_team  points_actual  salary  \
11            Chiefs        D   KC  HOU       True           5.00  2500.0   
22         Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
62      Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
66   Devonta Freeman       RB  ATL  ARI      False          26.80  5800.0   
123    Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
185       D.J. Chark       WR  JAX   NO       True           7.30  5500.0   
200      Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
206  Jamison Crowder       WR  NYJ  DAL       True          15.80  4000.0   
240       Tyler Boyd       WR  CIN  BAL      False           4.00  6300.0   

     points_projected  sdPts_projected  tier   player_id  
11           7.676000         0.600442     4     D_KC_11  
22          21.868021         1.083732     2   QB_ATL_22  
62          20.259054     

Actual week score: 75.32
                player position team  opp  home_team  points_actual  salary  \
7              Vikings        D  MIN  PHI       True           9.00  2600.0   
38     Gardner Minshew       QB  JAX   NO       True           5.62  5000.0   
62        Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
70   Leonard Fournette       RB  JAX   NO       True          17.80  6700.0   
157        Geoff Swaim       TE  JAX   NO       True           1.50  2900.0   
185         D.J. Chark       WR  JAX   NO       True           7.30  5500.0   
205    DeAndre Hopkins       WR  HOU   KC      False          16.50  7400.0   
216       Amari Cooper       WR  DAL  NYJ      False           1.30  7000.0   
240         Tyler Boyd       WR  CIN  BAL      False           4.00  6300.0   

     points_projected  sdPts_projected  tier   player_id  
7            7.025143         0.727103     4     D_MIN_7  
38          17.176630         1.793378     6   QB_JAX_38  
62     

Actual week score: 165.84000000000003
               player position team  opp  home_team  points_actual  salary  \
8             Jaguars        D  JAX   NO       True           7.00  2200.0   
22          Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
64       Chris Carson       RB  SEA  CLE      False          28.90  6000.0   
71    Phillip Lindsay       RB  DEN  TEN       True          15.50  5300.0   
123     Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
200       Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
206   Jamison Crowder       WR  NYJ  DAL       True          15.80  4000.0   
209  Larry Fitzgerald       WR  ARI  ATL       True          12.90  6100.0   
216      Amari Cooper       WR  DAL  NYJ      False           1.30  7000.0   

     points_projected  sdPts_projected  tier   player_id  
8            5.919143         0.778975     5     D_JAX_8  
22          21.868021         1.083732     2   QB_ATL_22  
64  

Actual week score: 117.2
              player position team  opp  home_team  points_actual  salary  \
17              Jets        D  NYJ  DAL       True            1.0  1500.0   
24    Deshaun Watson       QB  HOU   KC      False           31.4  6700.0   
62      Le'Veon Bell       RB  NYJ  DAL       True           12.3  6400.0   
71   Phillip Lindsay       RB  DEN  TEN       True           15.5  5300.0   
119     Jordan Akins       TE  HOU   KC      False            6.9  3200.0   
176      Will Fuller       WR  HOU   KC      False            9.4  6000.0   
185       D.J. Chark       WR  JAX   NO       True            7.3  5500.0   
204   Michael Thomas       WR   NO  JAX      False           16.9  7800.0   
205  DeAndre Hopkins       WR  HOU   KC      False           16.5  7400.0   

     points_projected  sdPts_projected  tier   player_id  
17           6.504800         0.477279     4    D_NYJ_17  
24          21.593686         0.510101     2   QB_HOU_24  
62          20.259054      

...

Actual week score: 98.61999999999999
              player position team  opp  home_team  points_actual  salary  \
5            Bengals        D  CIN  BAL      False           9.00  1700.0   
40        Jared Goff       QB  LAR   SF       True           2.12  6100.0   
61        Nick Chubb       RB  CLE  SEA       True          32.90  7300.0   
67       Carlos Hyde       RB  HOU   KC      False          22.00  4400.0   
135   Gerald Everett       TE  LAR   SF       True           2.90  3600.0   
191    Brandin Cooks       WR  LAR   SF       True           6.20  5400.0   
205  DeAndre Hopkins       WR  HOU   KC      False          16.50  7400.0   
213      Cooper Kupp       WR  LAR   SF       True           5.70  7100.0   
216     Amari Cooper       WR  DAL  NYJ      False           1.30  7000.0   

     points_projected  sdPts_projected  tier   player_id  
5            4.689000         1.476738     6     D_CIN_5  
40          19.365736         1.232886     4   QB_LAR_40  
61          18.

Actual week score: 162.34
               player position team  opp  home_team  points_actual  salary  \
7             Vikings        D  MIN  PHI       True           9.00  2600.0   
22          Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
59       Duke Johnson       RB  HOU   KC      False          13.40  4100.0   
72        Mark Ingram       RB  BAL  CIN       True          15.40  6600.0   
123     Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
173    Adam Humphries       WR  TEN  DEN      False          10.70  3800.0   
200       Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
205   DeAndre Hopkins       WR  HOU   KC      False          16.50  7400.0   
209  Larry Fitzgerald       WR  ARI  ATL       True          12.90  6100.0   

     points_projected  sdPts_projected  tier   player_id  
7            7.025143         0.727103     4     D_MIN_7  
22          21.868021         1.083732     2   QB_ATL_22  
59           9.5

Actual week score: 88.52
                player position team  opp  home_team  points_actual  salary  \
1              Broncos        D  DEN  TEN       True          23.00  3100.0   
40          Jared Goff       QB  LAR   SF       True           2.12  6100.0   
70   Leonard Fournette       RB  JAX   NO       True          17.80  6700.0   
74       Tevin Coleman       RB   SF  LAR      False          14.10  4400.0   
135     Gerald Everett       TE  LAR   SF       True           2.90  3600.0   
177     Michael Gallup       WR  DAL  NYJ      False           8.80  5600.0   
210      Tyler Lockett       WR  SEA  CLE      False          12.80  6400.0   
213        Cooper Kupp       WR  LAR   SF       True           5.70  7100.0   
216       Amari Cooper       WR  DAL  NYJ      False           1.30  7000.0   

     points_projected  sdPts_projected  tier   player_id  
1            7.690000         1.399451     4     D_DEN_1  
40          19.365736         1.232886     4   QB_LAR_40  
70     

Actual week score: 106.7
              player position team  opp  home_team  points_actual  salary  \
15            Titans        D  TEN  DEN      False            4.0  2900.0   
24    Deshaun Watson       QB  HOU   KC      False           31.4  6700.0   
59      Duke Johnson       RB  HOU   KC      False           13.4  4100.0   
60       Dalvin Cook       RB  MIN  PHI       True           13.4  8400.0   
119     Jordan Akins       TE  HOU   KC      False            6.9  3200.0   
205  DeAndre Hopkins       WR  HOU   KC      False           16.5  7400.0   
206  Jamison Crowder       WR  NYJ  DAL       True           15.8  4000.0   
216     Amari Cooper       WR  DAL  NYJ      False            1.3  7000.0   
240       Tyler Boyd       WR  CIN  BAL      False            4.0  6300.0   

     points_projected  sdPts_projected  tier   player_id  
15           7.489429         1.032126     4    D_TEN_15  
24          21.593686         0.510101     2   QB_HOU_24  
59           9.517833      

Actual week score: 122.0
               player position team  opp  home_team  points_actual  salary  \
5             Bengals        D  CIN  BAL      False            9.0  1700.0   
43       Kyler Murray       QB  ARI  ATL       True           31.8  6500.0   
60        Dalvin Cook       RB  MIN  PHI       True           13.4  8400.0   
61         Nick Chubb       RB  CLE  SEA       True           32.9  7300.0   
148      Charles Clay       TE  ARI  ATL       True            2.8  2700.0   
183      Robert Woods       WR  LAR   SF       True            7.6  5600.0   
193      Mohamed Sanu       WR  ATL  ARI      False            5.9  4500.0   
209  Larry Fitzgerald       WR  ARI  ATL       True           12.9  6100.0   
213       Cooper Kupp       WR  LAR   SF       True            5.7  7100.0   

     points_projected  sdPts_projected  tier   player_id  
5            4.689000         1.476738     6     D_CIN_5  
43          21.183843         1.592853     2   QB_ARI_43  
60          21.29

In [98]:
pos_max = {
    "QB": 1,
    "RB": 2,
    "WR": 4,
    "TE": 1,
    "D": 1
}

pos_min = {
    "QB": 1,
    "RB": 2,
    "WR": 4,
    "TE": 1,
    "D": 1
}

no_d_vs_off =[["QB", "D"], ["WR", "D"], ["RB", "D"], ["TE", "D"]]
prob, player_vars = get_basic_dfs_solver(df, pos_max, pos_min, proj_type='avg',
                                         opposing_player_exclusions=no_d_vs_off,
                                         stacks=[["QB", "WR", "TE"], ["WR", "-WR"]],
                                         use_actual_points=False)

df = df[~df.player.isin(["Pharoh Cooper", "Luke Willson"])].reset_index(drop=True)
num_lineups = 200
max_qb_exposure = 1.0
max_lineups_for_one_qb = int(math.ceil(num_lineups*max_qb_exposure))
qb_exposure = {}

max_points = -1
max_overlap = 5
for i in range(num_lineups):
    print("Lineup {0}".format(i))
    prob.solve()
    score_df = output_performance(prob, df, print_points_actual=True)
    print(score_df)
    lineup = score_df.player_id.tolist()
    if score_df.points_actual.sum() > max_points:
        max_points = score_df.points_actual.sum()
    
    # See if we need to remove QB from consideration
    qb = score_df[score_df.position == "QB"].player_id.tolist()[0]
    if qb in qb_exposure:
        qb_exposure[qb] += 1
    else:
        qb_exposure[qb] = 1
    
    # If QB reaches max exposure remove from future lineups
    if qb_exposure[qb] >= max_lineups_for_one_qb:
        print("Reached lineup exposure max for QB: {0}".format(qb))
        prob += player_vars[qb] == 0
    
    print("Best lineup to point: {0}".format(max_points))
    prob += lpSum([player_vars[player] for player in lineup]) <= max_overlap

print("Max points: {0}".format(max_points))

Stack: QB_WR_TE_0. Pos: QB, WR, TE. Opp Pos: 
Stack: WR_-WR_1. Pos: WR. Opp Pos: WR
Lineup 0
Actual week score: 146.54000000000002
             player position team  opp  home_team  points_actual  salary  \
11           Chiefs        D   KC  HOU       True           5.00  2500.0   
22        Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
58     Kenyan Drake       RB  MIA  WAS       True          13.00  4400.0   
62     Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
123   Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
197  Robby Anderson       WR  NYJ  DAL       True          26.50  4000.0   
200     Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
216    Amari Cooper       WR  DAL  NYJ      False           1.30  7000.0   
240      Tyler Boyd       WR  CIN  BAL      False           4.00  6300.0   

     points_projected  sdPts_projected  tier   player_id  
11           7.676000         0.600442     4     

Actual week score: 131.74
                player position team  opp  home_team  points_actual  salary  \
4             Redskins        D  WAS  MIA      False          10.00  3200.0   
27        Carson Wentz       QB  PHI  MIN      False          24.54  6000.0   
62        Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
70   Leonard Fournette       RB  JAX   NO       True          17.80  6700.0   
133          Zach Ertz       TE  PHI  MIN      False           8.40  5400.0   
185         D.J. Chark       WR  JAX   NO       True           7.30  5500.0   
197     Robby Anderson       WR  NYJ  DAL       True          26.50  4000.0   
199     Alshon Jeffery       WR  PHI  MIN      False          23.60  5800.0   
216       Amari Cooper       WR  DAL  NYJ      False           1.30  7000.0   

     points_projected  sdPts_projected  tier   player_id  
4            9.298667         1.180995     3     D_WAS_4  
27          17.933148         1.576590     5   QB_PHI_27  
62    

Actual week score: 155.24
             player position team  opp  home_team  points_actual  salary  \
0           Falcons        D  ATL  ARI      False          -1.00  2300.0   
22        Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
58     Kenyan Drake       RB  MIA  WAS       True          13.00  4400.0   
62     Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
123   Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
196  Terry McLaurin       WR  WAS  MIA      False          29.00  6000.0   
200     Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
201  DeVante Parker       WR  MIA  WAS       True          11.80  4200.0   
213     Cooper Kupp       WR  LAR   SF       True           5.70  7100.0   

     points_projected  sdPts_projected  tier   player_id  
0            6.911600         1.018358     4     D_ATL_0  
22          21.868021         1.083732     2   QB_ATL_22  
58          14.752067         1.3776

Actual week score: 161.54
              player position team  opp  home_team  points_actual  salary  \
11            Chiefs        D   KC  HOU       True           5.00  2500.0   
22         Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
71   Phillip Lindsay       RB  DEN  TEN       True          15.50  5300.0   
85         Joe Mixon       RB  CIN  BAL      False           5.90  5500.0   
123    Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
185       D.J. Chark       WR  JAX   NO       True           7.30  5500.0   
197   Robby Anderson       WR  NYJ  DAL       True          26.50  4000.0   
200      Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
204   Michael Thomas       WR   NO  JAX      False          16.90  7800.0   

     points_projected  sdPts_projected  tier   player_id  
11           7.676000         0.600442     4     D_KC_11  
22          21.868021         1.083732     2   QB_ATL_22  
71          15.188600     

Actual week score: 160.93999999999997
                player position team  opp  home_team  points_actual  salary  \
17                Jets        D  NYJ  DAL       True           1.00  1500.0   
22           Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
62        Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
71     Phillip Lindsay       RB  DEN  TEN       True          15.50  5300.0   
123      Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
200        Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
206    Jamison Crowder       WR  NYJ  DAL       True          15.80  4000.0   
210      Tyler Lockett       WR  SEA  CLE      False          12.80  6400.0   
211  Odell Beckham Jr.       WR  CLE  SEA       True          19.10  6800.0   

     points_projected  sdPts_projected  tier   player_id  
17           6.504800         0.477279     4    D_NYJ_17  
22          21.868021         1.083732     2   QB_ATL

...

Actual week score: 121.94
              player position team  opp  home_team  points_actual  salary  \
4           Redskins        D  WAS  MIA      False          10.00  3200.0   
27      Carson Wentz       QB  PHI  MIN      False          24.54  6000.0   
69     Miles Sanders       RB  PHI  MIN      False          18.20  4200.0   
89   Damien Williams       RB   KC  HOU       True           9.00  5700.0   
133        Zach Ertz       TE  PHI  MIN      False           8.40  5400.0   
185       D.J. Chark       WR  JAX   NO       True           7.30  5500.0   
199   Alshon Jeffery       WR  PHI  MIN      False          23.60  5800.0   
204   Michael Thomas       WR   NO  JAX      False          16.90  7800.0   
240       Tyler Boyd       WR  CIN  BAL      False           4.00  6300.0   

     points_projected  sdPts_projected  tier   player_id  
4            9.298667         1.180995     3     D_WAS_4  
27          17.933148         1.576590     5   QB_PHI_27  
69          10.587167     

Actual week score: 127.3
                player position team  opp  home_team  points_actual  salary  \
8              Jaguars        D  JAX   NO       True            7.0  2200.0   
26      Russell Wilson       QB  SEA  CLE      False           28.9  6600.0   
70   Leonard Fournette       RB  JAX   NO       True           17.8  6700.0   
90         Matt Breida       RB   SF  LAR      False           10.3  5100.0   
146        Will Dissly       TE  SEA  CLE      False            0.0  4900.0   
200        Julio Jones       WR  ATL  ARI      False           21.8  8000.0   
206    Jamison Crowder       WR  NYJ  DAL       True           15.8  4000.0   
209   Larry Fitzgerald       WR  ARI  ATL       True           12.9  6100.0   
210      Tyler Lockett       WR  SEA  CLE      False           12.8  6400.0   

     points_projected  sdPts_projected  tier   player_id  
8            5.919143         0.778975     5     D_JAX_8  
26          20.593821         0.712899     3   QB_SEA_26  
70     

Actual week score: 120.60000000000001
                player position team  opp  home_team  points_actual  salary  \
5              Bengals        D  CIN  BAL      False            9.0  1700.0   
26      Russell Wilson       QB  SEA  CLE      False           28.9  6600.0   
65       David Johnson       RB  ARI  ATL       True           28.2  7600.0   
70   Leonard Fournette       RB  JAX   NO       True           17.8  6700.0   
146        Will Dissly       TE  SEA  CLE      False            0.0  4900.0   
189        Corey Davis       WR  TEN  DEN      False            6.6  4000.0   
194   Courtland Sutton       WR  DEN  TEN       True           11.6  5000.0   
210      Tyler Lockett       WR  SEA  CLE      False           12.8  6400.0   
213        Cooper Kupp       WR  LAR   SF       True            5.7  7100.0   

     points_projected  sdPts_projected  tier   player_id  
5            4.689000         1.476738     6     D_CIN_5  
26          20.593821         0.712899     3   QB_SEA

Actual week score: 103.32
               player position team  opp  home_team  points_actual  salary  \
4            Redskins        D  WAS  MIA      False          10.00  3200.0   
34    Jimmy Garoppolo       QB   SF  LAR      False          14.12  5700.0   
71    Phillip Lindsay       RB  DEN  TEN       True          15.50  5300.0   
89    Damien Williams       RB   KC  HOU       True           9.00  5700.0   
124     George Kittle       TE   SF  LAR      False          21.30  5200.0   
185        D.J. Chark       WR  JAX   NO       True           7.30  5500.0   
204    Michael Thomas       WR   NO  JAX      False          16.90  7800.0   
213       Cooper Kupp       WR  LAR   SF       True           5.70  7100.0   
242  Marquise Goodwin       WR   SF  LAR      False           3.50  4500.0   

     points_projected  sdPts_projected  tier   player_id  
4            9.298667         1.180995     3     D_WAS_4  
34          16.143776         1.765654     7    QB_SF_34  
71          15.1

Actual week score: 111.4
               player position team  opp  home_team  points_actual  salary  \
17               Jets        D  NYJ  DAL       True            1.0  1500.0   
26     Russell Wilson       QB  SEA  CLE      False           28.9  6600.0   
61         Nick Chubb       RB  CLE  SEA       True           32.9  7300.0   
75       Alvin Kamara       RB   NO  JAX      False           13.6  8000.0   
146       Will Dissly       TE  SEA  CLE      False            0.0  4900.0   
189       Corey Davis       WR  TEN  DEN      False            6.6  4000.0   
194  Courtland Sutton       WR  DEN  TEN       True           11.6  5000.0   
210     Tyler Lockett       WR  SEA  CLE      False           12.8  6400.0   
240        Tyler Boyd       WR  CIN  BAL      False            4.0  6300.0   

     points_projected  sdPts_projected  tier   player_id  
17           6.504800         0.477279     4    D_NYJ_17  
26          20.593821         0.712899     3   QB_SEA_26  
61          18.64

In [99]:
pos_max = {
    "QB": 1,
    "RB": 2,
    "WR": 4,
    "TE": 1,
    "D": 1
}

pos_min = {
    "QB": 1,
    "RB": 2,
    "WR": 4,
    "TE": 1,
    "D": 1
}

no_d_vs_off =[["QB", "D"], ["WR", "D"], ["RB", "D"], ["TE", "D"]]
prob, player_vars = get_basic_dfs_solver(df, pos_max, pos_min, proj_type='avg',
                                         opposing_player_exclusions=no_d_vs_off,
                                         stacks=[["QB", "WR", "TE"], ["WR", "-WR"]],
                                         use_actual_points=False,
                                         min_home_players=5)

df = df[~df.player.isin(["Pharoh Cooper", "Luke Willson"])].reset_index(drop=True)
num_lineups = 200
max_qb_exposure = 1.0
max_lineups_for_one_qb = int(math.ceil(num_lineups*max_qb_exposure))
qb_exposure = {}

max_points = -1
max_overlap = 5
for i in range(num_lineups):
    print("Lineup {0}".format(i))
    prob.solve()
    score_df = output_performance(prob, df, print_points_actual=True)
    print(score_df)
    lineup = score_df.player_id.tolist()
    if score_df.points_actual.sum() > max_points:
        max_points = score_df.points_actual.sum()
    
    # See if we need to remove QB from consideration
    qb = score_df[score_df.position == "QB"].player_id.tolist()[0]
    if qb in qb_exposure:
        qb_exposure[qb] += 1
    else:
        qb_exposure[qb] = 1
    
    # If QB reaches max exposure remove from future lineups
    if qb_exposure[qb] >= max_lineups_for_one_qb:
        print("Reached lineup exposure max for QB: {0}".format(qb))
        prob += player_vars[qb] == 0
    
    print("Best lineup to point: {0}".format(max_points))
    prob += lpSum([player_vars[player] for player in lineup]) <= max_overlap

print("Max points: {0}".format(max_points))

Stack: QB_WR_TE_0. Pos: QB, WR, TE. Opp Pos: 
Stack: WR_-WR_1. Pos: WR. Opp Pos: WR
Lineup 0
Actual week score: 155.44
               player position team  opp  home_team  points_actual  salary  \
11             Chiefs        D   KC  HOU       True           5.00  2500.0   
22          Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
58       Kenyan Drake       RB  MIA  WAS       True          13.00  4400.0   
62       Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
123     Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
197    Robby Anderson       WR  NYJ  DAL       True          26.50  4000.0   
200       Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
209  Larry Fitzgerald       WR  ARI  ATL       True          12.90  6100.0   
216      Amari Cooper       WR  DAL  NYJ      False           1.30  7000.0   

     points_projected  sdPts_projected  tier   player_id  
11           7.676000         0.600442   

Actual week score: 166.14
                player position team  opp  home_team  points_actual  salary  \
7              Vikings        D  MIN  PHI       True           9.00  2600.0   
22           Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
70   Leonard Fournette       RB  JAX   NO       True          17.80  6700.0   
71     Phillip Lindsay       RB  DEN  TEN       True          15.50  5300.0   
123      Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
194   Courtland Sutton       WR  DEN  TEN       True          11.60  5000.0   
197     Robby Anderson       WR  NYJ  DAL       True          26.50  4000.0   
200        Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
216       Amari Cooper       WR  DAL  NYJ      False           1.30  7000.0   

     points_projected  sdPts_projected  tier   player_id  
7            7.025143         0.727103     4     D_MIN_7  
22          21.868021         1.083732     2   QB_ATL_22  
70    

Actual week score: 136.64000000000001
             player position team  opp  home_team  points_actual  salary  \
1           Broncos        D  DEN  TEN       True          23.00  3100.0   
27     Carson Wentz       QB  PHI  MIN      False          24.54  6000.0   
58     Kenyan Drake       RB  MIA  WAS       True          13.00  4400.0   
62     Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
133       Zach Ertz       TE  PHI  MIN      False           8.40  5400.0   
183    Robert Woods       WR  LAR   SF       True           7.60  5600.0   
185      D.J. Chark       WR  JAX   NO       True           7.30  5500.0   
199  Alshon Jeffery       WR  PHI  MIN      False          23.60  5800.0   
204  Michael Thomas       WR   NO  JAX      False          16.90  7800.0   

     points_projected  sdPts_projected  tier   player_id  
1            7.690000         1.399451     4     D_DEN_1  
27          17.933148         1.576590     5   QB_PHI_27  
58          14.752067   

Actual week score: 158.73999999999998
                player position team  opp  home_team  points_actual  salary  \
17                Jets        D  NYJ  DAL       True           1.00  1500.0   
22           Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
58        Kenyan Drake       RB  MIA  WAS       True          13.00  4400.0   
71     Phillip Lindsay       RB  DEN  TEN       True          15.50  5300.0   
123      Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
200        Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
209   Larry Fitzgerald       WR  ARI  ATL       True          12.90  6100.0   
210      Tyler Lockett       WR  SEA  CLE      False          12.80  6400.0   
211  Odell Beckham Jr.       WR  CLE  SEA       True          19.10  6800.0   

     points_projected  sdPts_projected  tier   player_id  
17           6.504800         0.477279     4    D_NYJ_17  
22          21.868021         1.083732     2   QB_ATL

Actual week score: 94.42
              player position team  opp  home_team  points_actual  salary  \
4           Redskins        D  WAS  MIA      False          10.00  3200.0   
38   Gardner Minshew       QB  JAX   NO       True           5.62  5000.0   
60       Dalvin Cook       RB  MIN  PHI       True          13.40  8400.0   
62      Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
157      Geoff Swaim       TE  JAX   NO       True           1.50  2900.0   
185       D.J. Chark       WR  JAX   NO       True           7.30  5500.0   
197   Robby Anderson       WR  NYJ  DAL       True          26.50  4000.0   
205  DeAndre Hopkins       WR  HOU   KC      False          16.50  7400.0   
216     Amari Cooper       WR  DAL  NYJ      False           1.30  7000.0   

     points_projected  sdPts_projected  tier   player_id  
4            9.298667         1.180995     3     D_WAS_4  
38          17.176630         1.793378     6   QB_JAX_38  
60          21.296375      

...

Actual week score: 156.34
              player position team  opp  home_team  points_actual  salary  \
14            Browns        D  CLE  SEA       True           4.00  2800.0   
27      Carson Wentz       QB  PHI  MIN      False          24.54  6000.0   
62      Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
71   Phillip Lindsay       RB  DEN  TEN       True          15.50  5300.0   
133        Zach Ertz       TE  PHI  MIN      False           8.40  5400.0   
197   Robby Anderson       WR  NYJ  DAL       True          26.50  4000.0   
198      Tyreek Hill       WR   KC  HOU       True          25.00  6900.0   
199   Alshon Jeffery       WR  PHI  MIN      False          23.60  5800.0   
205  DeAndre Hopkins       WR  HOU   KC      False          16.50  7400.0   

     points_projected  sdPts_projected  tier   player_id  
14           6.444667         0.874345     4    D_CLE_14  
27          17.933148         1.576590     5   QB_PHI_27  
62          20.259054     

Actual week score: 118.72000000000001
                player position team  opp  home_team  points_actual  salary  \
15              Titans        D  TEN  DEN      False           4.00  2900.0   
40          Jared Goff       QB  LAR   SF       True           2.12  6100.0   
64        Chris Carson       RB  SEA  CLE      False          28.90  6000.0   
70   Leonard Fournette       RB  JAX   NO       True          17.80  6700.0   
135     Gerald Everett       TE  LAR   SF       True           2.90  3600.0   
196     Terry McLaurin       WR  WAS  MIA      False          29.00  6000.0   
201     DeVante Parker       WR  MIA  WAS       True          11.80  4200.0   
205    DeAndre Hopkins       WR  HOU   KC      False          16.50  7400.0   
213        Cooper Kupp       WR  LAR   SF       True           5.70  7100.0   

     points_projected  sdPts_projected  tier   player_id  
15           7.489429         1.032126     4    D_TEN_15  
40          19.365736         1.232886     4   QB_LAR

Actual week score: 141.12
                player position team  opp  home_team  points_actual  salary  \
17                Jets        D  NYJ  DAL       True           1.00  1500.0   
25        Kirk Cousins       QB  MIN  PHI       True          31.32  5200.0   
70   Leonard Fournette       RB  JAX   NO       True          17.80  6700.0   
71     Phillip Lindsay       RB  DEN  TEN       True          15.50  5300.0   
116       Kyle Rudolph       TE  MIN  PHI       True           6.60  3000.0   
200        Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
203       Adam Thielen       WR  MIN  PHI       True          17.70  6700.0   
205    DeAndre Hopkins       WR  HOU   KC      False          16.50  7400.0   
209   Larry Fitzgerald       WR  ARI  ATL       True          12.90  6100.0   

     points_projected  sdPts_projected  tier   player_id  
17           6.504800         0.477279     4    D_NYJ_17  
25          16.821000         1.250591     6   QB_MIN_25  
70    

Actual week score: 116.61999999999999
               player position team  opp  home_team  points_actual  salary  \
11             Chiefs        D   KC  HOU       True           5.00  2500.0   
34    Jimmy Garoppolo       QB   SF  LAR      False          14.12  5700.0   
58       Kenyan Drake       RB  MIA  WAS       True          13.00  4400.0   
60        Dalvin Cook       RB  MIN  PHI       True          13.40  8400.0   
124     George Kittle       TE   SF  LAR      False          21.30  5200.0   
194  Courtland Sutton       WR  DEN  TEN       True          11.60  5000.0   
200       Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
209  Larry Fitzgerald       WR  ARI  ATL       True          12.90  6100.0   
242  Marquise Goodwin       WR   SF  LAR      False           3.50  4500.0   

     points_projected  sdPts_projected  tier   player_id  
11           7.676000         0.600442     4     D_KC_11  
34          16.143776         1.765654     7    QB_SF_34  
58  

Actual week score: 139.58
                player position team  opp  home_team  points_actual  salary  \
11              Chiefs        D   KC  HOU       True           5.00  2500.0   
31        Dak Prescott       QB  DAL  NYJ      False          18.18  6200.0   
61          Nick Chubb       RB  CLE  SEA       True          32.90  7300.0   
70   Leonard Fournette       RB  JAX   NO       True          17.80  6700.0   
130       Jason Witten       TE  DAL  NYJ      False          10.70  3900.0   
196     Terry McLaurin       WR  WAS  MIA      False          29.00  6000.0   
201     DeVante Parker       WR  MIA  WAS       True          11.80  4200.0   
209   Larry Fitzgerald       WR  ARI  ATL       True          12.90  6100.0   
216       Amari Cooper       WR  DAL  NYJ      False           1.30  7000.0   

     points_projected  sdPts_projected  tier   player_id  
11           7.676000         0.600442     4     D_KC_11  
31          20.460943         0.933020     3   QB_DAL_31  
61    

In [104]:
pos_max = {
    "QB": 1,
    "RB": 2,
    "WR": 4,
    "TE": 1,
    "D": 1
}

pos_min = {
    "QB": 1,
    "RB": 2,
    "WR": 4,
    "TE": 1,
    "D": 1
}

no_d_vs_off =[["QB", "D"], ["WR", "D"], ["RB", "D"], ["TE", "D"]]
prob, player_vars = get_basic_dfs_solver(df, pos_max, pos_min, proj_type='avg',
                                         opposing_player_exclusions=no_d_vs_off,
                                         stacks=[["QB", "WR", "TE"], ["WR", "-WR"]],
                                         use_actual_points=True,
                                         min_home_players=5)

df = df[~df.player.isin(["Pharoh Cooper", "Luke Willson"])].reset_index(drop=True)
num_lineups = 5
max_qb_exposure = 1.0
max_lineups_for_one_qb = int(math.ceil(num_lineups*max_qb_exposure))
qb_exposure = {}

max_points = -1
max_overlap = 4
for i in range(num_lineups):
    print("Lineup {0}".format(i))
    prob.solve()
    score_df = output_performance(prob, df, print_points_actual=True)
    print(score_df)
    lineup = score_df.player_id.tolist()
    if score_df.points_actual.sum() > max_points:
        max_points = score_df.points_actual.sum()
    
    # See if we need to remove QB from consideration
    qb = score_df[score_df.position == "QB"].player_id.tolist()[0]
    if qb in qb_exposure:
        qb_exposure[qb] += 1
    else:
        qb_exposure[qb] = 1
    
    # If QB reaches max exposure remove from future lineups
    if qb_exposure[qb] >= max_lineups_for_one_qb:
        print("Reached lineup exposure max for QB: {0}".format(qb))
        prob += player_vars[qb] == 0
    
    print("Best lineup to point: {0}".format(max_points))
    prob += lpSum([player_vars[player] for player in lineup]) <= max_overlap

print("Max points: {0}".format(max_points))

Stack: QB_WR_TE_0. Pos: QB, WR, TE. Opp Pos: 
Stack: WR_-WR_1. Pos: WR. Opp Pos: WR
Lineup 0
Actual week score: 240.14000000000001
             player position team  opp  home_team  points_actual  salary  \
1           Broncos        D  DEN  TEN       True          23.00  3100.0   
22        Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
47      Mark Walton       RB  MIA  WAS       True          12.50  3000.0   
61       Nick Chubb       RB  CLE  SEA       True          32.90  7300.0   
123   Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
195    Stefon Diggs       WR  MIN  PHI       True          46.50  5900.0   
196  Terry McLaurin       WR  WAS  MIA      False          29.00  6000.0   
200     Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
201  DeVante Parker       WR  MIA  WAS       True          11.80  4200.0   

     points_projected  sdPts_projected  tier   player_id  
1            7.690000         1.399451     4     

In [117]:
pos_max = {
    "QB": 1,
    "RB": 2,
    "WR": 4,
    "TE": 1,
    "D": 1
}

pos_min = {
    "QB": 1,
    "RB": 2,
    "WR": 4,
    "TE": 1,
    "D": 1
}

no_d_vs_off =[["QB", "D"], ["WR", "D"], ["RB", "D"], ["TE", "D"]]
prob, player_vars = get_basic_dfs_solver(df, pos_max, pos_min, proj_type='avg',
                                         opposing_player_exclusions=no_d_vs_off,
                                         stacks=[["QB", "WR", "TE"]],
                                         use_actual_points=False,
                                         min_home_players=6,
                                         min_stud_rbs=1,
                                         min_stud_rb_salary=7000)

df = df[~df.player.isin(["Pharoh Cooper", "Luke Willson"])].reset_index(drop=True)
num_lineups = 300
max_qb_exposure = 1.0
max_lineups_for_one_qb = int(math.ceil(num_lineups*max_qb_exposure))
qb_exposure = {}

max_points = -1
max_overlap = 4
for i in range(num_lineups):
    print("Lineup {0}".format(i))
    prob.solve()
    score_df = output_performance(prob, df, print_points_actual=True)
    print(score_df)
    lineup = score_df.player_id.tolist()
    if score_df.points_actual.sum() > max_points:
        max_points = score_df.points_actual.sum()
    
    # See if we need to remove QB from consideration
    qb = score_df[score_df.position == "QB"].player_id.tolist()[0]
    if qb in qb_exposure:
        qb_exposure[qb] += 1
    else:
        qb_exposure[qb] = 1
    
    # If QB reaches max exposure remove from future lineups
    if qb_exposure[qb] >= max_lineups_for_one_qb:
        print("Reached lineup exposure max for QB: {0}".format(qb))
        prob += player_vars[qb] == 0
    
    print("Best lineup to point: {0}".format(max_points))
    prob += lpSum([player_vars[player] for player in lineup]) <= max_overlap

print("Max points: {0}".format(max_points))

Stack: QB_WR_TE_0. Pos: QB, WR, TE. Opp Pos: 
Lineup 0
Actual week score: 167.34
             player position team  opp  home_team  points_actual  salary  \
17             Jets        D  NYJ  DAL       True           1.00  1500.0   
22        Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
62     Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
65    David Johnson       RB  ARI  ATL       True          28.20  7600.0   
123   Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
183    Robert Woods       WR  LAR   SF       True           7.60  5600.0   
185      D.J. Chark       WR  JAX   NO       True           7.30  5500.0   
197  Robby Anderson       WR  NYJ  DAL       True          26.50  4000.0   
200     Julio Jones       WR  ATL  ARI      False          21.80  8000.0   

     points_projected  sdPts_projected  tier   player_id  
17           6.504800         0.477279     4    D_NYJ_17  
22          21.868021         1.083732  

Actual week score: 174.54000000000002
                player position team  opp  home_team  points_actual  salary  \
11              Chiefs        D   KC  HOU       True           5.00  2500.0   
22           Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
60         Dalvin Cook       RB  MIN  PHI       True          13.40  8400.0   
70   Leonard Fournette       RB  JAX   NO       True          17.80  6700.0   
123      Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
194   Courtland Sutton       WR  DEN  TEN       True          11.60  5000.0   
197     Robby Anderson       WR  NYJ  DAL       True          26.50  4000.0   
200        Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
206    Jamison Crowder       WR  NYJ  DAL       True          15.80  4000.0   

     points_projected  sdPts_projected  tier   player_id  
11           7.676000         0.600442     4     D_KC_11  
22          21.868021         1.083732     2   QB_ATL

Actual week score: 90.32000000000001
               player position team  opp  home_team  points_actual  salary  \
17               Jets        D  NYJ  DAL       True           1.00  1500.0   
40         Jared Goff       QB  LAR   SF       True           2.12  6100.0   
58       Kenyan Drake       RB  MIA  WAS       True          13.00  4400.0   
65      David Johnson       RB  ARI  ATL       True          28.20  7600.0   
135    Gerald Everett       TE  LAR   SF       True           2.90  3600.0   
183      Robert Woods       WR  LAR   SF       True           7.60  5600.0   
204    Michael Thomas       WR   NO  JAX      False          16.90  7800.0   
209  Larry Fitzgerald       WR  ARI  ATL       True          12.90  6100.0   
213       Cooper Kupp       WR  LAR   SF       True           5.70  7100.0   

     points_projected  sdPts_projected  tier   player_id  
17           6.504800         0.477279     4    D_NYJ_17  
40          19.365736         1.232886     4   QB_LAR_40  
58   

Actual week score: 148.1
               player position team  opp  home_team  points_actual  salary  \
7             Vikings        D  MIN  PHI       True            9.0  2600.0   
24     Deshaun Watson       QB  HOU   KC      False           31.4  6700.0   
62       Le'Veon Bell       RB  NYJ  DAL       True           12.3  6400.0   
65      David Johnson       RB  ARI  ATL       True           28.2  7600.0   
119      Jordan Akins       TE  HOU   KC      False            6.9  3200.0   
194  Courtland Sutton       WR  DEN  TEN       True           11.6  5000.0   
197    Robby Anderson       WR  NYJ  DAL       True           26.5  4000.0   
205   DeAndre Hopkins       WR  HOU   KC      False           16.5  7400.0   
213       Cooper Kupp       WR  LAR   SF       True            5.7  7100.0   

     points_projected  sdPts_projected  tier   player_id  
7            7.025143         0.727103     4     D_MIN_7  
24          21.593686         0.510101     2   QB_HOU_24  
62          20.25

Actual week score: 85.22
              player position team  opp  home_team  points_actual  salary  \
4           Redskins        D  WAS  MIA      False          10.00  3200.0   
40        Jared Goff       QB  LAR   SF       True           2.12  6100.0   
71   Phillip Lindsay       RB  DEN  TEN       True          15.50  5300.0   
75      Alvin Kamara       RB   NO  JAX      False          13.60  8000.0   
135   Gerald Everett       TE  LAR   SF       True           2.90  3600.0   
183     Robert Woods       WR  LAR   SF       True           7.60  5600.0   
197   Robby Anderson       WR  NYJ  DAL       True          26.50  4000.0   
213      Cooper Kupp       WR  LAR   SF       True           5.70  7100.0   
216     Amari Cooper       WR  DAL  NYJ      False           1.30  7000.0   

     points_projected  sdPts_projected  tier   player_id  
4            9.298667         1.180995     3     D_WAS_4  
40          19.365736         1.232886     4   QB_LAR_40  
71          15.188600      

...

Actual week score: 131.12
                 player position team  opp  home_team  points_actual  salary  \
0               Falcons        D  ATL  ARI      False          -1.00  2300.0   
30   Patrick Mahomes II       QB   KC  HOU       True          20.82  7500.0   
63      Ezekiel Elliott       RB  DAL  NYJ      False          29.20  8500.0   
93       Chris Thompson       RB  WAS  MIA      False           4.00  5000.0   
132        Travis Kelce       TE   KC  HOU       True           9.80  7000.0   
197      Robby Anderson       WR  NYJ  DAL       True          26.50  4000.0   
198         Tyreek Hill       WR   KC  HOU       True          25.00  6900.0   
206     Jamison Crowder       WR  NYJ  DAL       True          15.80  4000.0   
217    Emmanuel Sanders       WR  DEN  TEN       True           1.00  4800.0   

     points_projected  sdPts_projected  tier   player_id  
0            6.911600         1.018358     4     D_ATL_0  
30          22.202200         1.551496     1    QB_KC_3

Actual week score: 108.52
                 player position team  opp  home_team  points_actual  salary  \
17                 Jets        D  NYJ  DAL       True           1.00  1500.0   
30   Patrick Mahomes II       QB   KC  HOU       True          20.82  7500.0   
70    Leonard Fournette       RB  JAX   NO       True          17.80  6700.0   
75         Alvin Kamara       RB   NO  JAX      False          13.60  8000.0   
132        Travis Kelce       TE   KC  HOU       True           9.80  7000.0   
193        Mohamed Sanu       WR  ATL  ARI      False           5.90  4500.0   
198         Tyreek Hill       WR   KC  HOU       True          25.00  6900.0   
201      DeVante Parker       WR  MIA  WAS       True          11.80  4200.0   
244          Trey Quinn       WR  WAS  MIA      False           2.80  3700.0   

     points_projected  sdPts_projected  tier   player_id  
17           6.504800         0.477279     4    D_NYJ_17  
30          22.202200         1.551496     1    QB_KC_3

Actual week score: 137.86
                player position team  opp  home_team  points_actual  salary  \
7              Vikings        D  MIN  PHI       True           9.00  2600.0   
29      Baker Mayfield       QB  CLE  SEA       True          22.46  5500.0   
65       David Johnson       RB  ARI  ATL       True          28.20  7600.0   
70   Leonard Fournette       RB  JAX   NO       True          17.80  6700.0   
126  Ricky Seals-Jones       TE  CLE  SEA       True          13.70  3300.0   
193       Mohamed Sanu       WR  ATL  ARI      False           5.90  4500.0   
203       Adam Thielen       WR  MIN  PHI       True          17.70  6700.0   
211  Odell Beckham Jr.       WR  CLE  SEA       True          19.10  6800.0   
240         Tyler Boyd       WR  CIN  BAL      False           4.00  6300.0   

     points_projected  sdPts_projected  tier   player_id  
7            7.025143         0.727103     4     D_MIN_7  
29          14.926505         2.509434     7   QB_CLE_29  
65    

Actual week score: 157.26
                player position team  opp  home_team  points_actual  salary  \
1              Broncos        D  DEN  TEN       True          23.00  3100.0   
29      Baker Mayfield       QB  CLE  SEA       True          22.46  5500.0   
71     Phillip Lindsay       RB  DEN  TEN       True          15.50  5300.0   
75        Alvin Kamara       RB   NO  JAX      False          13.60  8000.0   
126  Ricky Seals-Jones       TE  CLE  SEA       True          13.70  3300.0   
197     Robby Anderson       WR  NYJ  DAL       True          26.50  4000.0   
203       Adam Thielen       WR  MIN  PHI       True          17.70  6700.0   
211  Odell Beckham Jr.       WR  CLE  SEA       True          19.10  6800.0   
213        Cooper Kupp       WR  LAR   SF       True           5.70  7100.0   

     points_projected  sdPts_projected  tier   player_id  
1            7.690000         1.399451     4     D_DEN_1  
29          14.926505         2.509434     7   QB_CLE_29  
71    

Actual week score: 121.62
               player position team  opp  home_team  points_actual  salary  \
11             Chiefs        D   KC  HOU       True           5.00  2500.0   
40         Jared Goff       QB  LAR   SF       True           2.12  6100.0   
65      David Johnson       RB  ARI  ATL       True          28.20  7600.0   
72        Mark Ingram       RB  BAL  CIN       True          15.40  6600.0   
135    Gerald Everett       TE  LAR   SF       True           2.90  3600.0   
195      Stefon Diggs       WR  MIN  PHI       True          46.50  5900.0   
207     Calvin Ridley       WR  ATL  ARI      False          14.80  5700.0   
213       Cooper Kupp       WR  LAR   SF       True           5.70  7100.0   
217  Emmanuel Sanders       WR  DEN  TEN       True           1.00  4800.0   

     points_projected  sdPts_projected  tier   player_id  
11           7.676000         0.600442     4     D_KC_11  
40          19.365736         1.232886     4   QB_LAR_40  
65          19.0

In [125]:
pos_max = {
    "QB": 1,
    "RB": 2,
    "WR": 4,
    "TE": 1,
    "D": 1
}

pos_min = {
    "QB": 1,
    "RB": 2,
    "WR": 4,
    "TE": 1,
    "D": 1
}

no_d_vs_off =[["QB", "D"], ["WR", "D"], ["RB", "D"], ["TE", "D"]]
prob, player_vars = get_basic_dfs_solver(df, pos_max, pos_min, proj_type='avg',
                                         opposing_player_exclusions=no_d_vs_off,
                                         stacks=[["QB", "WR", "TE"], ["WR", "-WR"]],
                                         use_actual_points=False,
                                         min_home_players=5,
                                         min_stud_rbs=1,
                                         min_stud_rb_salary=7000,
                                         point_diff_for_identical=10)

df = df[~df.player.isin(["Pharoh Cooper", "Luke Willson"])].reset_index(drop=True)
num_lineups = 300
max_qb_exposure = 1.0
max_lineups_for_one_qb = int(math.ceil(num_lineups*max_qb_exposure))
qb_exposure = {}

max_points = -1
max_overlap = 4
for i in range(num_lineups):
    print("Lineup {0}".format(i))
    prob.solve()
    score_df = output_performance(prob, df, print_points_actual=True)
    print(score_df)
    lineup = score_df.player_id.tolist()
    if score_df.points_actual.sum() > max_points:
        max_points = score_df.points_actual.sum()
    
    # See if we need to remove QB from consideration
    qb = score_df[score_df.position == "QB"].player_id.tolist()[0]
    if qb in qb_exposure:
        qb_exposure[qb] += 1
    else:
        qb_exposure[qb] = 1
    
    # If QB reaches max exposure remove from future lineups
    if qb_exposure[qb] >= max_lineups_for_one_qb:
        print("Reached lineup exposure max for QB: {0}".format(qb))
        prob += player_vars[qb] == 0
    
    print("Best lineup to point: {0}".format(max_points))
    prob += lpSum([player_vars[player] for player in lineup]) <= max_overlap

print("Max points: {0}".format(max_points))

Stack: QB_WR_TE_0. Pos: QB, WR, TE. Opp Pos: 
Stack: WR_-WR_1. Pos: WR. Opp Pos: WR
Lineup 0
Actual week score: 134.64
             player position team  opp  home_team  points_actual  salary  \
11           Chiefs        D   KC  HOU       True           5.00  2500.0   
22        Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
60      Dalvin Cook       RB  MIN  PHI       True          13.40  8400.0   
62     Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
123   Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
183    Robert Woods       WR  LAR   SF       True           7.60  5600.0   
193    Mohamed Sanu       WR  ATL  ARI      False           5.90  4500.0   
197  Robby Anderson       WR  NYJ  DAL       True          26.50  4000.0   
216    Amari Cooper       WR  DAL  NYJ      False           1.30  7000.0   

     points_projected  sdPts_projected  tier   player_id  
11           7.676000         0.600442     4     D_KC_11  
22

Actual week score: 60.220000000000006
               player position team  opp  home_team  points_actual  salary  \
17               Jets        D  NYJ  DAL       True           1.00  1500.0   
40         Jared Goff       QB  LAR   SF       True           2.12  6100.0   
60        Dalvin Cook       RB  MIN  PHI       True          13.40  8400.0   
62       Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
135    Gerald Everett       TE  LAR   SF       True           2.90  3600.0   
193      Mohamed Sanu       WR  ATL  ARI      False           5.90  4500.0   
209  Larry Fitzgerald       WR  ARI  ATL       True          12.90  6100.0   
213       Cooper Kupp       WR  LAR   SF       True           5.70  7100.0   
240        Tyler Boyd       WR  CIN  BAL      False           4.00  6300.0   

     points_projected  sdPts_projected  tier   player_id  
17           6.504800         0.477279     4    D_NYJ_17  
40          19.365736         1.232886     4   QB_LAR_40  
60  

Actual week score: 116.83999999999999
               player position team  opp  home_team  points_actual  salary  \
17               Jets        D  NYJ  DAL       True           1.00  1500.0   
44      Lamar Jackson       QB  BAL  CIN       True          33.64  6900.0   
62       Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
75       Alvin Kamara       RB   NO  JAX      False          13.60  8000.0   
125      Mark Andrews       TE  BAL  CIN       True          14.90  4800.0   
185        D.J. Chark       WR  JAX   NO       True           7.30  5500.0   
204    Michael Thomas       WR   NO  JAX      False          16.90  7800.0   
209  Larry Fitzgerald       WR  ARI  ATL       True          12.90  6100.0   
238      Seth Roberts       WR  BAL  CIN       True           4.30  3000.0   

     points_projected  sdPts_projected  tier   player_id  
17           6.504800         0.477279     4    D_NYJ_17  
44          23.693690         1.568820     1   QB_BAL_44  
62  

Actual week score: 74.62
                player position team  opp  home_team  points_actual  salary  \
0              Falcons        D  ATL  ARI      False          -1.00  2300.0   
40          Jared Goff       QB  LAR   SF       True           2.12  6100.0   
60         Dalvin Cook       RB  MIN  PHI       True          13.40  8400.0   
70   Leonard Fournette       RB  JAX   NO       True          17.80  6700.0   
135     Gerald Everett       TE  LAR   SF       True           2.90  3600.0   
183       Robert Woods       WR  LAR   SF       True           7.60  5600.0   
197     Robby Anderson       WR  NYJ  DAL       True          26.50  4000.0   
216       Amari Cooper       WR  DAL  NYJ      False           1.30  7000.0   
240         Tyler Boyd       WR  CIN  BAL      False           4.00  6300.0   

     points_projected  sdPts_projected  tier   player_id  
0            6.911600         1.018358     4     D_ATL_0  
40          19.365736         1.232886     4   QB_LAR_40  
60     

Actual week score: 83.72
              player position team  opp  home_team  points_actual  salary  \
4           Redskins        D  WAS  MIA      False          10.00  3200.0   
38   Gardner Minshew       QB  JAX   NO       True           5.62  5000.0   
60       Dalvin Cook       RB  MIN  PHI       True          13.40  8400.0   
62      Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
157      Geoff Swaim       TE  JAX   NO       True           1.50  2900.0   
185       D.J. Chark       WR  JAX   NO       True           7.30  5500.0   
205  DeAndre Hopkins       WR  HOU   KC      False          16.50  7400.0   
206  Jamison Crowder       WR  NYJ  DAL       True          15.80  4000.0   
216     Amari Cooper       WR  DAL  NYJ      False           1.30  7000.0   

     points_projected  sdPts_projected  tier   player_id  
4            9.298667         1.180995     3     D_WAS_4  
38          17.176630         1.793378     6   QB_JAX_38  
60          21.296375      

...

Actual week score: 106.94
             player position team  opp  home_team  points_actual  salary  \
0           Falcons        D  ATL  ARI      False          -1.00  2300.0   
44    Lamar Jackson       QB  BAL  CIN       True          33.64  6900.0   
58     Kenyan Drake       RB  MIA  WAS       True          13.00  4400.0   
60      Dalvin Cook       RB  MIN  PHI       True          13.40  8400.0   
125    Mark Andrews       TE  BAL  CIN       True          14.90  4800.0   
185      D.J. Chark       WR  JAX   NO       True           7.30  5500.0   
204  Michael Thomas       WR   NO  JAX      False          16.90  7800.0   
233    Miles Boykin       WR  BAL  CIN       True           4.80  3500.0   
240      Tyler Boyd       WR  CIN  BAL      False           4.00  6300.0   

     points_projected  sdPts_projected  tier   player_id  
0            6.911600         1.018358     4     D_ATL_0  
44          23.693690         1.568820     1   QB_BAL_44  
58          14.752067         1.3776

Actual week score: 105.08
                player position team  opp  home_team  points_actual  salary  \
11              Chiefs        D   KC  HOU       True           5.00  2500.0   
31        Dak Prescott       QB  DAL  NYJ      False          18.18  6200.0   
65       David Johnson       RB  ARI  ATL       True          28.20  7600.0   
70   Leonard Fournette       RB  JAX   NO       True          17.80  6700.0   
130       Jason Witten       TE  DAL  NYJ      False          10.70  3900.0   
189        Corey Davis       WR  TEN  DEN      False           6.60  4000.0   
194   Courtland Sutton       WR  DEN  TEN       True          11.60  5000.0   
213        Cooper Kupp       WR  LAR   SF       True           5.70  7100.0   
216       Amari Cooper       WR  DAL  NYJ      False           1.30  7000.0   

     points_projected  sdPts_projected  tier   player_id  
11           7.676000         0.600442     4     D_KC_11  
31          20.460943         0.933020     3   QB_DAL_31  
65    

Actual week score: 105.99999999999999
               player position team  opp  home_team  points_actual  salary  \
17               Jets        D  NYJ  DAL       True            1.0  1500.0   
26     Russell Wilson       QB  SEA  CLE      False           28.9  6600.0   
60        Dalvin Cook       RB  MIN  PHI       True           13.4  8400.0   
71    Phillip Lindsay       RB  DEN  TEN       True           15.5  5300.0   
146       Will Dissly       TE  SEA  CLE      False            0.0  4900.0   
175  Demaryius Thomas       WR  NYJ  DAL       True           10.2  3300.0   
185        D.J. Chark       WR  JAX   NO       True            7.3  5500.0   
204    Michael Thomas       WR   NO  JAX      False           16.9  7800.0   
210     Tyler Lockett       WR  SEA  CLE      False           12.8  6400.0   

     points_projected  sdPts_projected  tier   player_id  
17           6.504800         0.477279     4    D_NYJ_17  
26          20.593821         0.712899     3   QB_SEA_26  
60  

Actual week score: 118.83999999999999
                player position team  opp  home_team  points_actual  salary  \
19           Cardinals        D  ARI  ATL       True           1.00  1900.0   
44       Lamar Jackson       QB  BAL  CIN       True          33.64  6900.0   
70   Leonard Fournette       RB  JAX   NO       True          17.80  6700.0   
75        Alvin Kamara       RB   NO  JAX      False          13.60  8000.0   
125       Mark Andrews       TE  BAL  CIN       True          14.90  4800.0   
205    DeAndre Hopkins       WR  HOU   KC      False          16.50  7400.0   
206    Jamison Crowder       WR  NYJ  DAL       True          15.80  4000.0   
216       Amari Cooper       WR  DAL  NYJ      False           1.30  7000.0   
238       Seth Roberts       WR  BAL  CIN       True           4.30  3000.0   

     points_projected  sdPts_projected  tier   player_id  
19           5.030000         1.515305     5    D_ARI_19  
44          23.693690         1.568820     1   QB_BAL

KeyboardInterrupt: 

In [154]:
pos_max = {
    "QB": 1,
    "RB": 2,
    "WR": 4,
    "TE": 1,
    "D": 1
}

pos_min = {
    "QB": 1,
    "RB": 2,
    "WR": 4,
    "TE": 1,
    "D": 1
}

no_d_vs_off =[["QB", "D"], ["WR", "D"], ["RB", "D"], ["TE", "D"]]
prob, player_vars = get_basic_dfs_solver(df, pos_max, pos_min, proj_type='avg',
                                         opposing_player_exclusions=no_d_vs_off,
                                         stacks=[["QB", "WR", "TE"]],
                                         use_actual_points=False,
                                         point_diff_for_identical=10,
                                         min_home_players=5, 
                                         max_offensive_teams=5,
                                         max_per_team=4)

df = df[~df.player.isin(["Pharoh Cooper", "Luke Willson"])].reset_index(drop=True)
num_lineups = 200
max_qb_exposure = 1.0
max_lineups_for_one_qb = int(math.ceil(num_lineups*max_qb_exposure))
qb_exposure = {}

max_points = -1
max_overlap = 4
for i in range(num_lineups):
    print("Lineup {0}".format(i))
    prob.solve()
    score_df = output_performance(prob, df, print_points_actual=True)
    print(score_df)
    lineup = score_df.player_id.tolist()
    if score_df.points_actual.sum() > max_points:
        max_points = score_df.points_actual.sum()
    
    # See if we need to remove QB from consideration
    qb = score_df[score_df.position == "QB"].player_id.tolist()[0]
    if qb in qb_exposure:
        qb_exposure[qb] += 1
    else:
        qb_exposure[qb] = 1
    
    # If QB reaches max exposure remove from future lineups
    if qb_exposure[qb] >= max_lineups_for_one_qb:
        print("Reached lineup exposure max for QB: {0}".format(qb))
        prob += player_vars[qb] == 0
    
    print("Best lineup to point: {0}".format(max_points))
    prob += lpSum([player_vars[player] for player in lineup]) <= max_overlap

print("Max points: {0}".format(max_points))

Stack: QB_WR_TE_0. Pos: QB, WR, TE. Opp Pos: 
Lineup 0
Actual week score: 131.34
            player position team  opp  home_team  points_actual  salary  \
17            Jets        D  NYJ  DAL       True           1.00  1500.0   
22       Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
58    Kenyan Drake       RB  MIA  WAS       True          13.00  4400.0   
62    Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
123  Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
183   Robert Woods       WR  LAR   SF       True           7.60  5600.0   
185     D.J. Chark       WR  JAX   NO       True           7.30  5500.0   
200    Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
213    Cooper Kupp       WR  LAR   SF       True           5.70  7100.0   

     points_projected  sdPts_projected  tier   player_id  
17           6.504800         0.477279     4    D_NYJ_17  
22          21.868021         1.083732     2   QB_

Actual week score: 110.24000000000001
                player position team  opp  home_team  points_actual  salary  \
4             Redskins        D  WAS  MIA      False          10.00  3200.0   
44       Lamar Jackson       QB  BAL  CIN       True          33.64  6900.0   
62        Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
70   Leonard Fournette       RB  JAX   NO       True          17.80  6700.0   
125       Mark Andrews       TE  BAL  CIN       True          14.90  4800.0   
183       Robert Woods       WR  LAR   SF       True           7.60  5600.0   
213        Cooper Kupp       WR  LAR   SF       True           5.70  7100.0   
238       Seth Roberts       WR  BAL  CIN       True           4.30  3000.0   
240         Tyler Boyd       WR  CIN  BAL      False           4.00  6300.0   

     points_projected  sdPts_projected  tier   player_id  
4            9.298667         1.180995     3     D_WAS_4  
44          23.693690         1.568820     1   QB_BAL

Actual week score: 93.08
                player position team  opp  home_team  points_actual  salary  \
11              Chiefs        D   KC  HOU       True           5.00  2500.0   
31        Dak Prescott       QB  DAL  NYJ      False          18.18  6200.0   
62        Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
70   Leonard Fournette       RB  JAX   NO       True          17.80  6700.0   
130       Jason Witten       TE  DAL  NYJ      False          10.70  3900.0   
183       Robert Woods       WR  LAR   SF       True           7.60  5600.0   
185         D.J. Chark       WR  JAX   NO       True           7.30  5500.0   
209   Larry Fitzgerald       WR  ARI  ATL       True          12.90  6100.0   
216       Amari Cooper       WR  DAL  NYJ      False           1.30  7000.0   

     points_projected  sdPts_projected  tier   player_id  
11           7.676000         0.600442     4     D_KC_11  
31          20.460943         0.933020     3   QB_DAL_31  
62     

Actual week score: 108.39999999999999
                player position team  opp  home_team  points_actual  salary  \
17                Jets        D  NYJ  DAL       True            1.0  1500.0   
43        Kyler Murray       QB  ARI  ATL       True           31.8  6500.0   
62        Le'Veon Bell       RB  NYJ  DAL       True           12.3  6400.0   
70   Leonard Fournette       RB  JAX   NO       True           17.8  6700.0   
148       Charles Clay       TE  ARI  ATL       True            2.8  2700.0   
183       Robert Woods       WR  LAR   SF       True            7.6  5600.0   
205    DeAndre Hopkins       WR  HOU   KC      False           16.5  7400.0   
209   Larry Fitzgerald       WR  ARI  ATL       True           12.9  6100.0   
213        Cooper Kupp       WR  LAR   SF       True            5.7  7100.0   

     points_projected  sdPts_projected  tier   player_id  
17           6.504800         0.477279     4    D_NYJ_17  
43          21.183843         1.592853     2   QB_ARI

Actual week score: 111.24
              player position team  opp  home_team  points_actual  salary  \
17              Jets        D  NYJ  DAL       True           1.00  1500.0   
44     Lamar Jackson       QB  BAL  CIN       True          33.64  6900.0   
58      Kenyan Drake       RB  MIA  WAS       True          13.00  4400.0   
62      Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
125     Mark Andrews       TE  BAL  CIN       True          14.90  4800.0   
176      Will Fuller       WR  HOU   KC      False           9.40  6000.0   
205  DeAndre Hopkins       WR  HOU   KC      False          16.50  7400.0   
213      Cooper Kupp       WR  LAR   SF       True           5.70  7100.0   
235     Willie Snead       WR  BAL  CIN       True           4.80  5500.0   

     points_projected  sdPts_projected  tier   player_id  
17           6.504800         0.477279     4    D_NYJ_17  
44          23.693690         1.568820     1   QB_BAL_44  
58          14.752067     

...

Actual week score: 91.12
                 player position team  opp  home_team  points_actual  salary  \
17                 Jets        D  NYJ  DAL       True           1.00  1500.0   
30   Patrick Mahomes II       QB   KC  HOU       True          20.82  7500.0   
62         Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
71      Phillip Lindsay       RB  DEN  TEN       True          15.50  5300.0   
132        Travis Kelce       TE   KC  HOU       True           9.80  7000.0   
178      Mecole Hardman       WR   KC  HOU       True           8.50  5300.0   
183        Robert Woods       WR  LAR   SF       True           7.60  5600.0   
194    Courtland Sutton       WR  DEN  TEN       True          11.60  5000.0   
240          Tyler Boyd       WR  CIN  BAL      False           4.00  6300.0   

     points_projected  sdPts_projected  tier   player_id  
17           6.504800         0.477279     4    D_NYJ_17  
30          22.202200         1.551496     1    QB_KC_30

Actual week score: 193.34
             player position team  opp  home_team  points_actual  salary  \
11           Chiefs        D   KC  HOU       True           5.00  2500.0   
22        Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
61       Nick Chubb       RB  CLE  SEA       True          32.90  7300.0   
64     Chris Carson       RB  SEA  CLE      False          28.90  6000.0   
123   Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
179  Dede Westbrook       WR  JAX   NO       True           8.30  5100.0   
185      D.J. Chark       WR  JAX   NO       True           7.30  5500.0   
197  Robby Anderson       WR  NYJ  DAL       True          26.50  4000.0   
200     Julio Jones       WR  ATL  ARI      False          21.80  8000.0   

     points_projected  sdPts_projected  tier   player_id  
11           7.676000         0.600442     4     D_KC_11  
22          21.868021         1.083732     2   QB_ATL_22  
61          18.649625         0.9123

Actual week score: 91.28
               player position team  opp  home_team  points_actual  salary  \
14             Browns        D  CLE  SEA       True           4.00  2800.0   
31       Dak Prescott       QB  DAL  NYJ      False          18.18  6200.0   
60        Dalvin Cook       RB  MIN  PHI       True          13.40  8400.0   
62       Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
130      Jason Witten       TE  DAL  NYJ      False          10.70  3900.0   
194  Courtland Sutton       WR  DEN  TEN       True          11.60  5000.0   
206   Jamison Crowder       WR  NYJ  DAL       True          15.80  4000.0   
216      Amari Cooper       WR  DAL  NYJ      False           1.30  7000.0   
240        Tyler Boyd       WR  CIN  BAL      False           4.00  6300.0   

     points_projected  sdPts_projected  tier   player_id  
14           6.444667         0.874345     4    D_CLE_14  
31          20.460943         0.933020     3   QB_DAL_31  
60          21.29

Actual week score: 123.0
                player position team  opp  home_team  points_actual  salary  \
19           Cardinals        D  ARI  ATL       True            1.0  1900.0   
35   Teddy Bridgewater       QB   NO  JAX      False           13.6  5300.0   
62        Le'Veon Bell       RB  NYJ  DAL       True           12.3  6400.0   
70   Leonard Fournette       RB  JAX   NO       True           17.8  6700.0   
128         Jared Cook       TE   NO  JAX      False           12.7  3400.0   
197     Robby Anderson       WR  NYJ  DAL       True           26.5  4000.0   
204     Michael Thomas       WR   NO  JAX      False           16.9  7800.0   
205    DeAndre Hopkins       WR  HOU   KC      False           16.5  7400.0   
213        Cooper Kupp       WR  LAR   SF       True            5.7  7100.0   

     points_projected  sdPts_projected  tier   player_id  
19           5.030000         1.515305     5    D_ARI_19  
35          14.453233         1.160707     8    QB_NO_35  
62     

KeyboardInterrupt: 

In [156]:
pos_max = {
    "QB": 1,
    "RB": 2,
    "WR": 4,
    "TE": 1,
    "D": 1
}

pos_min = {
    "QB": 1,
    "RB": 2,
    "WR": 4,
    "TE": 1,
    "D": 1
}

no_d_vs_off =[["QB", "D"], ["WR", "D"], ["RB", "D"], ["TE", "D"]]
prob, player_vars = get_basic_dfs_solver(df, pos_max, pos_min, proj_type='avg',
                                         opposing_player_exclusions=no_d_vs_off,
                                         stacks=[["QB", "WR", "TE"], ["RB", "WR", "-WR"]],
                                         use_actual_points=False,
                                         point_diff_for_identical=10,
                                         min_home_players=5, 
                                         max_offensive_teams=4,
                                         min_offensive_teams=4,
                                         max_per_team=4)

df = df[~df.player.isin(["Pharoh Cooper", "Luke Willson"])].reset_index(drop=True)
num_lineups = 200
max_qb_exposure = 1.0
max_lineups_for_one_qb = int(math.ceil(num_lineups*max_qb_exposure))
qb_exposure = {}

max_points = -1
max_overlap = 4
for i in range(num_lineups):
    print("Lineup {0}".format(i))
    prob.solve()
    score_df = output_performance(prob, df, print_points_actual=True)
    print(score_df)
    lineup = score_df.player_id.tolist()
    if score_df.points_actual.sum() > max_points:
        max_points = score_df.points_actual.sum()
    
    # See if we need to remove QB from consideration
    qb = score_df[score_df.position == "QB"].player_id.tolist()[0]
    if qb in qb_exposure:
        qb_exposure[qb] += 1
    else:
        qb_exposure[qb] = 1
    
    # If QB reaches max exposure remove from future lineups
    if qb_exposure[qb] >= max_lineups_for_one_qb:
        print("Reached lineup exposure max for QB: {0}".format(qb))
        prob += player_vars[qb] == 0
    
    print("Best lineup to point: {0}".format(max_points))
    prob += lpSum([player_vars[player] for player in lineup]) <= max_overlap

print("Max points: {0}".format(max_points))

Stack: QB_WR_TE_0. Pos: QB, WR, TE. Opp Pos: 
Stack: RB_WR_-WR_1. Pos: RB, WR. Opp Pos: WR
Lineup 0
Actual week score: 163.14000000000001
                player position team  opp  home_team  points_actual  salary  \
11              Chiefs        D   KC  HOU       True           5.00  2500.0   
22           Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
62        Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
70   Leonard Fournette       RB  JAX   NO       True          17.80  6700.0   
123      Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
197     Robby Anderson       WR  NYJ  DAL       True          26.50  4000.0   
200        Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
206    Jamison Crowder       WR  NYJ  DAL       True          15.80  4000.0   
216       Amari Cooper       WR  DAL  NYJ      False           1.30  7000.0   

     points_projected  sdPts_projected  tier   player_id  
11          

Actual week score: 126.83999999999999
              player position team  opp  home_team  points_actual  salary  \
0            Falcons        D  ATL  ARI      False          -1.00  2300.0   
44     Lamar Jackson       QB  BAL  CIN       True          33.64  6900.0   
62      Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
63   Ezekiel Elliott       RB  DAL  NYJ      False          29.20  8500.0   
125     Mark Andrews       TE  BAL  CIN       True          14.90  4800.0   
197   Robby Anderson       WR  NYJ  DAL       True          26.50  4000.0   
213      Cooper Kupp       WR  LAR   SF       True           5.70  7100.0   
216     Amari Cooper       WR  DAL  NYJ      False           1.30  7000.0   
238     Seth Roberts       WR  BAL  CIN       True           4.30  3000.0   

     points_projected  sdPts_projected  tier   player_id  
0            6.911600         1.018358     4     D_ATL_0  
44          23.693690         1.568820     1   QB_BAL_44  
62          20

Actual week score: 126.5
               player position team  opp  home_team  points_actual  salary  \
11             Chiefs        D   KC  HOU       True            5.0  2500.0   
43       Kyler Murray       QB  ARI  ATL       True           31.8  6500.0   
62       Le'Veon Bell       RB  NYJ  DAL       True           12.3  6400.0   
65      David Johnson       RB  ARI  ATL       True           28.2  7600.0   
148      Charles Clay       TE  ARI  ATL       True            2.8  2700.0   
197    Robby Anderson       WR  NYJ  DAL       True           26.5  4000.0   
209  Larry Fitzgerald       WR  ARI  ATL       True           12.9  6100.0   
213       Cooper Kupp       WR  LAR   SF       True            5.7  7100.0   
216      Amari Cooper       WR  DAL  NYJ      False            1.3  7000.0   

     points_projected  sdPts_projected  tier   player_id  
11           7.676000         0.600442     4     D_KC_11  
43          21.183843         1.592853     2   QB_ARI_43  
62          20.25

Actual week score: 69.52000000000001
                player position team  opp  home_team  points_actual  salary  \
11              Chiefs        D   KC  HOU       True           5.00  2500.0   
40          Jared Goff       QB  LAR   SF       True           2.12  6100.0   
70   Leonard Fournette       RB  JAX   NO       True          17.80  6700.0   
85           Joe Mixon       RB  CIN  BAL      False           5.90  5500.0   
135     Gerald Everett       TE  LAR   SF       True           2.90  3600.0   
183       Robert Woods       WR  LAR   SF       True           7.60  5600.0   
185         D.J. Chark       WR  JAX   NO       True           7.30  5500.0   
204     Michael Thomas       WR   NO  JAX      False          16.90  7800.0   
240         Tyler Boyd       WR  CIN  BAL      False           4.00  6300.0   

     points_projected  sdPts_projected  tier   player_id  
11           7.676000         0.600442     4     D_KC_11  
40          19.365736         1.232886     4   QB_LAR_

Actual week score: 143.84
               player position team  opp  home_team  points_actual  salary  \
17               Jets        D  NYJ  DAL       True           1.00  1500.0   
27       Carson Wentz       QB  PHI  MIN      False          24.54  6000.0   
62       Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
65      David Johnson       RB  ARI  ATL       True          28.20  7600.0   
133         Zach Ertz       TE  PHI  MIN      False           8.40  5400.0   
180    Nelson Agholor       WR  PHI  MIN      False           8.20  4600.0   
197    Robby Anderson       WR  NYJ  DAL       True          26.50  4000.0   
200       Julio Jones       WR  ATL  ARI      False          21.80  8000.0   
209  Larry Fitzgerald       WR  ARI  ATL       True          12.90  6100.0   

     points_projected  sdPts_projected  tier   player_id  
17           6.504800         0.477279     4    D_NYJ_17  
27          17.933148         1.576590     5   QB_PHI_27  
62          20.2

...

Actual week score: 110.12
                 player position team  opp  home_team  points_actual  salary  \
5               Bengals        D  CIN  BAL      False           9.00  1700.0   
30   Patrick Mahomes II       QB   KC  HOU       True          20.82  7500.0   
62         Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
70    Leonard Fournette       RB  JAX   NO       True          17.80  6700.0   
132        Travis Kelce       TE   KC  HOU       True           9.80  7000.0   
177      Michael Gallup       WR  DAL  NYJ      False           8.80  5600.0   
178      Mecole Hardman       WR   KC  HOU       True           8.50  5300.0   
185          D.J. Chark       WR  JAX   NO       True           7.30  5500.0   
206     Jamison Crowder       WR  NYJ  DAL       True          15.80  4000.0   

     points_projected  sdPts_projected  tier   player_id  
5            4.689000         1.476738     6     D_CIN_5  
30          22.202200         1.551496     1    QB_KC_3

Actual week score: 138.34
               player position team  opp  home_team  points_actual  salary  \
12             Ravens        D  BAL  CIN       True           5.00  4100.0   
22          Matt Ryan       QB  ATL  ARI      False          33.94  6400.0   
60        Dalvin Cook       RB  MIN  PHI       True          13.40  8400.0   
71    Phillip Lindsay       RB  DEN  TEN       True          15.50  5300.0   
123     Austin Hooper       TE  ATL  ARI      False          28.70  5000.0   
189       Corey Davis       WR  TEN  DEN      False           6.60  4000.0   
193      Mohamed Sanu       WR  ATL  ARI      False           5.90  4500.0   
194  Courtland Sutton       WR  DEN  TEN       True          11.60  5000.0   
203      Adam Thielen       WR  MIN  PHI       True          17.70  6700.0   

     points_projected  sdPts_projected  tier   player_id  
12           8.298571         0.824638     3    D_BAL_12  
22          21.868021         1.083732     2   QB_ATL_22  
60          21.2

Actual week score: 115.84
              player position team  opp  home_team  points_actual  salary  \
15            Titans        D  TEN  DEN      False           4.00  2900.0   
44     Lamar Jackson       QB  BAL  CIN       True          33.64  6900.0   
62      Le'Veon Bell       RB  NYJ  DAL       True          12.30  6400.0   
72       Mark Ingram       RB  BAL  CIN       True          15.40  6600.0   
136     Hayden Hurst       TE  BAL  CIN       True           1.40  3200.0   
197   Robby Anderson       WR  NYJ  DAL       True          26.50  4000.0   
205  DeAndre Hopkins       WR  HOU   KC      False          16.50  7400.0   
216     Amari Cooper       WR  DAL  NYJ      False           1.30  7000.0   
235     Willie Snead       WR  BAL  CIN       True           4.80  5500.0   

     points_projected  sdPts_projected  tier   player_id  
15           7.489429         1.032126     4    D_TEN_15  
44          23.693690         1.568820     1   QB_BAL_44  
62          20.259054     

Actual week score: 79.02
                player position team  opp  home_team  points_actual  salary  \
17                Jets        D  NYJ  DAL       True           1.00  1500.0   
40          Jared Goff       QB  LAR   SF       True           2.12  6100.0   
60         Dalvin Cook       RB  MIN  PHI       True          13.40  8400.0   
70   Leonard Fournette       RB  JAX   NO       True          17.80  6700.0   
111       Tyler Higbee       TE  LAR   SF       True           5.50  3000.0   
180     Nelson Agholor       WR  PHI  MIN      False           8.20  4600.0   
183       Robert Woods       WR  LAR   SF       True           7.60  5600.0   
203       Adam Thielen       WR  MIN  PHI       True          17.70  6700.0   
213        Cooper Kupp       WR  LAR   SF       True           5.70  7100.0   

     points_projected  sdPts_projected  tier   player_id  
17           6.504800         0.477279     4    D_NYJ_17  
40          19.365736         1.232886     4   QB_LAR_40  
60     

KeyboardInterrupt: 

In [160]:
model_input = "/Users/awaldrop/PycharmProjects/dfs_optimization_tools/data/harmonized_datasets/2019/dfk_harm_wk5_2019.csv"
non_ms_teams = ["LAR", "SEA", "SF", "CLE", "IND", "KC"]
df = pd.read_csv(model_input)
df = df.sort_values(by="position").copy()
df = df[~df.team.isin(non_ms_teams)].reset_index(drop=True)
df.head()

player position team  opp  home_team  points_actual  salary  \
0    Falcons        D  ATL  HOU      False           -2.0  2500.0   
1  Cardinals        D  ARI  CIN      False            1.0  2900.0   
2     Eagles        D  PHI  NYJ       True           35.0  3700.0   
3   Panthers        D  CAR  JAX       True           14.0  2600.0   
4   Patriots        D   NE  WAS      False           14.0  4300.0   

   points_projected  sdPts_projected  tier  
0          6.682000         0.943303     4  
1          7.020600         0.949946     4  
2          7.975429         1.567577     3  
3          8.296286         0.735724     3  
4          9.998000         2.569489     2

In [163]:
pos_max = {
    "QB": 1,
    "RB": 2,
    "WR": 4,
    "TE": 1,
    "D": 1
}

pos_min = {
    "QB": 1,
    "RB": 2,
    "WR": 4,
    "TE": 1,
    "D": 1
}

no_d_vs_off =[["QB", "D"], ["WR", "D"], ["RB", "D"], ["TE", "D"]]
prob, player_vars = get_basic_dfs_solver(df, pos_max, pos_min, proj_type='avg',
                                         opposing_player_exclusions=no_d_vs_off,
                                         stacks=[["QB", "WR", "TE"], ["RB", "WR", "-WR"]],
                                         use_actual_points=True,
                                         point_diff_for_identical=10, 
                                         max_offensive_teams=4,
                                         min_offensive_teams=4,
                                         max_per_team=4)

df = df[~df.player.isin(["Pharoh Cooper", "Luke Willson"])].reset_index(drop=True)
num_lineups = 5
max_qb_exposure = 1.0
max_lineups_for_one_qb = int(math.ceil(num_lineups*max_qb_exposure))
qb_exposure = {}

max_points = -1
max_overlap = 4
for i in range(num_lineups):
    print("Lineup {0}".format(i))
    prob.solve()
    score_df = output_performance(prob, df, print_points_actual=True)
    print(score_df)
    lineup = score_df.player_id.tolist()
    if score_df.points_actual.sum() > max_points:
        max_points = score_df.points_actual.sum()
    
    # See if we need to remove QB from consideration
    qb = score_df[score_df.position == "QB"].player_id.tolist()[0]
    if qb in qb_exposure:
        qb_exposure[qb] += 1
    else:
        qb_exposure[qb] = 1
    
    # If QB reaches max exposure remove from future lineups
    if qb_exposure[qb] >= max_lineups_for_one_qb:
        print("Reached lineup exposure max for QB: {0}".format(qb))
        prob += player_vars[qb] == 0
    
    print("Best lineup to point: {0}".format(max_points))
    prob += lpSum([player_vars[player] for player in lineup]) <= max_overlap

print("Max points: {0}".format(max_points))

Stack: QB_WR_TE_0. Pos: QB, WR, TE. Opp Pos: 
Stack: RB_WR_-WR_1. Pos: RB, WR. Opp Pos: WR
Lineup 0
Actual week score: 330.04
                  player position team  opp  home_team  points_actual  salary  \
2                 Eagles        D  PHI  NYJ       True          35.00  3700.0   
26        Deshaun Watson       QB  HOU  ATL       True          44.74  6700.0   
73           Aaron Jones       RB   GB  DAL      False          52.20  5900.0   
74   Christian McCaffrey       RB  CAR  JAX       True          50.70  8700.0   
147         Darren Fells       TE  HOU  ATL       True          16.00  2900.0   
226          Will Fuller       WR  HOU  ATL       True          56.70  4500.0   
228         Amari Cooper       WR  DAL   GB       True          42.60  6800.0   
235       Michael Gallup       WR  DAL   GB       True          27.30  5000.0   
248     Geronimo Allison       WR   GB  DAL      False           4.80  5000.0   

     points_projected  sdPts_projected  tier   player_id  
2   

In [164]:
pos_max = {
    "QB": 1,
    "RB": 2,
    "WR": 4,
    "TE": 1,
    "D": 1
}

pos_min = {
    "QB": 1,
    "RB": 2,
    "WR": 4,
    "TE": 1,
    "D": 1
}

no_d_vs_off =[["QB", "D"], ["WR", "D"], ["RB", "D"], ["TE", "D"]]
prob, player_vars = get_basic_dfs_solver(df, pos_max, pos_min, proj_type='avg',
                                         opposing_player_exclusions=no_d_vs_off,
                                         stacks=[["QB", "WR", "TE"], ["RB", "WR", "-WR"]],
                                         use_actual_points=False,
                                         point_diff_for_identical=10, 
                                         max_offensive_teams=4,
                                         min_offensive_teams=4,
                                         max_per_team=4)

df = df[~df.player.isin(["Pharoh Cooper", "Luke Willson"])].reset_index(drop=True)
num_lineups = 150
max_qb_exposure = 1.0
max_lineups_for_one_qb = int(math.ceil(num_lineups*max_qb_exposure))
qb_exposure = {}

max_points = -1
max_overlap = 4
for i in range(num_lineups):
    print("Lineup {0}".format(i))
    prob.solve()
    score_df = output_performance(prob, df, print_points_actual=True)
    print(score_df)
    lineup = score_df.player_id.tolist()
    if score_df.points_actual.sum() > max_points:
        max_points = score_df.points_actual.sum()
    
    # See if we need to remove QB from consideration
    qb = score_df[score_df.position == "QB"].player_id.tolist()[0]
    if qb in qb_exposure:
        qb_exposure[qb] += 1
    else:
        qb_exposure[qb] = 1
    
    # If QB reaches max exposure remove from future lineups
    if qb_exposure[qb] >= max_lineups_for_one_qb:
        print("Reached lineup exposure max for QB: {0}".format(qb))
        prob += player_vars[qb] == 0
    
    print("Best lineup to point: {0}".format(max_points))
    prob += lpSum([player_vars[player] for player in lineup]) <= max_overlap

print("Max points: {0}".format(max_points))

Stack: QB_WR_TE_0. Pos: QB, WR, TE. Opp Pos: 
Stack: RB_WR_-WR_1. Pos: RB, WR. Opp Pos: WR
Lineup 0
Actual week score: 179.70000000000002
                  player position team  opp  home_team  points_actual  salary  \
3               Panthers        D  CAR  JAX       True           14.0  2600.0   
51             Matt Ryan       QB  ATL  HOU      False           35.9  5900.0   
74   Christian McCaffrey       RB  CAR  JAX       True           50.7  8700.0   
79         Austin Ekeler       RB  LAC  DEN       True           23.3  6700.0   
149        Austin Hooper       TE  ATL  HOU      False           13.6  4500.0   
221         Keenan Allen       WR  LAC  DEN       True            5.8  7300.0   
238     Courtland Sutton       WR  DEN  LAC      False           19.2  4900.0   
241         Mohamed Sanu       WR  ATL  HOU      False           15.3  4200.0   
288     Emmanuel Sanders       WR  DEN  LAC      False            1.9  5100.0   

     points_projected  sdPts_projected  tier   play

Actual week score: 163.1
               player position team  opp  home_team  points_actual  salary  \
13             Titans        D  TEN  BUF       True            7.0  3000.0   
51          Matt Ryan       QB  ATL  HOU      False           35.9  5900.0   
79      Austin Ekeler       RB  LAC  DEN       True           23.3  6700.0   
92    Phillip Lindsay       RB  DEN  LAC      False           27.7  4900.0   
149     Austin Hooper       TE  ATL  HOU      False           13.6  4500.0   
218       Julio Jones       WR  ATL  HOU      False            7.2  7700.0   
238  Courtland Sutton       WR  DEN  LAC      False           19.2  4900.0   
240   DeAndre Hopkins       WR  HOU  ATL       True           15.8  7800.0   
244     Mike Williams       WR  LAC  DEN       True           13.4  4500.0   

     points_projected  sdPts_projected  tier   player_id  
13           8.390857         0.692414     3    D_TEN_13  
51          20.040986         0.870382     3   QB_ATL_51  
79          18.95

Actual week score: 122.34
               player position team  opp  home_team  points_actual  salary  \
3            Panthers        D  CAR  JAX       True          14.00  2600.0   
37      Lamar Jackson       QB  BAL  PIT      False          14.44  7100.0   
82      David Johnson       RB  ARI  CIN      False          18.60  7500.0   
92    Phillip Lindsay       RB  DEN  LAC      False          27.70  4900.0   
144      Mark Andrews       TE  BAL  PIT      False           9.50  4800.0   
205    Marquise Brown       WR  BAL  PIT      False          11.20  5700.0   
221      Keenan Allen       WR  LAC  DEN       True           5.80  7300.0   
238  Courtland Sutton       WR  DEN  LAC      False          19.20  4900.0   
288  Emmanuel Sanders       WR  DEN  LAC      False           1.90  5100.0   

     points_projected  sdPts_projected  tier   player_id  
3            8.296286         0.735724     3     D_CAR_3  
37          21.352324         1.156883     2   QB_BAL_37  
82          20.5

Actual week score: 134.6
               player position team  opp  home_team  points_actual  salary  \
22            Bengals        D  CIN  ARI       True            1.0  2500.0   
51          Matt Ryan       QB  ATL  HOU      False           35.9  5900.0   
53          Joe Mixon       RB  CIN  ARI       True           11.9  6100.0   
108     Royce Freeman       RB  DEN  LAC      False            8.7  4600.0   
149     Austin Hooper       TE  ATL  HOU      False           13.6  4500.0   
218       Julio Jones       WR  ATL  HOU      False            7.2  7700.0   
221      Keenan Allen       WR  LAC  DEN       True            5.8  7300.0   
232        Tyler Boyd       WR  CIN  ARI       True           31.3  6500.0   
238  Courtland Sutton       WR  DEN  LAC      False           19.2  4900.0   

     points_projected  sdPts_projected  tier   player_id  
22           7.323000         0.662564     4    D_CIN_22  
51          20.040986         0.870382     3   QB_ATL_51  
53          16.17

Actual week score: 159.82
               player position team  opp  home_team  points_actual  salary  \
9            Steelers        D  PIT  BAL       True          11.00  2100.0   
28       Dak Prescott       QB  DAL   GB       True          29.22  6000.0   
79      Austin Ekeler       RB  LAC  DEN       True          23.30  6700.0   
82      David Johnson       RB  ARI  CIN      False          18.60  7500.0   
141      Jason Witten       TE  DAL   GB       True           5.90  3800.0   
221      Keenan Allen       WR  LAC  DEN       True           5.80  7300.0   
224        Auden Tate       WR  CIN  ARI       True          11.60  3500.0   
225  Larry Fitzgerald       WR  ARI  CIN      False          11.80  6000.0   
228      Amari Cooper       WR  DAL   GB       True          42.60  6800.0   

     points_projected  sdPts_projected  tier   player_id  
9            6.677600         0.946350     4     D_PIT_9  
28          19.504836         1.278487     3   QB_DAL_28  
79          18.9

Actual week score: 171.06000000000003
                player position team  opp  home_team  points_actual  salary  \
13              Titans        D  TEN  BUF       True           7.00  3000.0   
50   Teddy Bridgewater       QB   NO   TB       True          31.26  5200.0   
79       Austin Ekeler       RB  LAC  DEN       True          23.30  6700.0   
92     Phillip Lindsay       RB  DEN  LAC      False          27.70  4900.0   
148         Jared Cook       TE   NO   TB       True          14.10  3400.0   
221       Keenan Allen       WR  LAC  DEN       True           5.80  7300.0   
227     Michael Thomas       WR   NO   TB       True          44.20  6600.0   
240    DeAndre Hopkins       WR  HOU  ATL       True          15.80  7800.0   
288   Emmanuel Sanders       WR  DEN  LAC      False           1.90  5100.0   

     points_projected  sdPts_projected  tier   player_id  
13           8.390857         0.692414     3    D_TEN_13  
50          14.750900         1.576731     6    QB_NO

Actual week score: 89.36000000000001
               player position team  opp  home_team  points_actual  salary  \
21         Buccaneers        D   TB   NO      False           1.00  2200.0   
35     Jameis Winston       QB   TB   NO      False          17.46  6200.0   
79      Austin Ekeler       RB  LAC  DEN       True          23.30  6700.0   
82      David Johnson       RB  ARI  CIN      False          18.60  7500.0   
164     Cameron Brate       TE   TB   NO      False           2.10  3000.0   
221      Keenan Allen       WR  LAC  DEN       True           5.80  7300.0   
238  Courtland Sutton       WR  DEN  LAC      False          19.20  4900.0   
262        Mike Evans       WR   TB   NO      False           0.00  7100.0   
288  Emmanuel Sanders       WR  DEN  LAC      False           1.90  5100.0   

     points_projected  sdPts_projected  tier   player_id  
21           6.330600         0.371351     5     D_TB_21  
35          19.687121         1.045910     3    QB_TB_35  
79   

Actual week score: 174.6
               player position team  opp  home_team  points_actual  salary  \
4            Patriots        D   NE  WAS      False           14.0  4300.0   
51          Matt Ryan       QB  ATL  HOU      False           35.9  5900.0   
82      David Johnson       RB  ARI  CIN      False           18.6  7500.0   
92    Phillip Lindsay       RB  DEN  LAC      False           27.7  4900.0   
149     Austin Hooper       TE  ATL  HOU      False           13.6  4500.0   
225  Larry Fitzgerald       WR  ARI  CIN      False           11.8  6000.0   
232        Tyler Boyd       WR  CIN  ARI       True           31.3  6500.0   
246     Calvin Ridley       WR  ATL  HOU      False           19.8  4900.0   
288  Emmanuel Sanders       WR  DEN  LAC      False            1.9  5100.0   

     points_projected  sdPts_projected  tier   player_id  
4            9.998000         2.569489     2      D_NE_4  
51          20.040986         0.870382     3   QB_ATL_51  
82          20.56

KeyboardInterrupt: 

In [168]:
pos_max = {
    "QB": 1,
    "RB": 2,
    "WR": 4,
    "TE": 1,
    "D": 1
}

pos_min = {
    "QB": 1,
    "RB": 2,
    "WR": 4,
    "TE": 1,
    "D": 1
}

no_d_vs_off =[["QB", "D"], ["WR", "D"], ["RB", "D"], ["TE", "D"]]
prob, player_vars = get_basic_dfs_solver(df, pos_max, pos_min, proj_type='avg',
                                         opposing_player_exclusions=no_d_vs_off,
                                         stacks=[["QB", "WR", "TE"], ["RB", "WR", "-WR"]],
                                         use_actual_points=False,
                                         point_diff_for_identical=10, 
                                         max_offensive_teams=4,
                                         min_offensive_teams=4,
                                         max_per_team=4)

df = df[~df.player.isin(["Pharoh Cooper", "Luke Willson"])].reset_index(drop=True)
num_lineups = 150
max_qb_exposure = 1.0
max_lineups_for_one_qb = int(math.ceil(num_lineups*max_qb_exposure))
qb_exposure = {}

max_points = -1
max_overlap = 3
for i in range(num_lineups):
    print("Lineup {0}".format(i))
    prob.solve()
    score_df = output_performance(prob, df, print_points_actual=True)
    print(score_df)
    lineup = score_df.player_id.tolist()
    if score_df.points_actual.sum() > max_points:
        max_points = score_df.points_actual.sum()
    
    # See if we need to remove QB from consideration
    qb = score_df[score_df.position == "QB"].player_id.tolist()[0]
    if qb in qb_exposure:
        qb_exposure[qb] += 1
    else:
        qb_exposure[qb] = 1
    
    # If QB reaches max exposure remove from future lineups
    if qb_exposure[qb] >= max_lineups_for_one_qb:
        print("Reached lineup exposure max for QB: {0}".format(qb))
        prob += player_vars[qb] == 0
    
    print("Best lineup to point: {0}".format(max_points))
    prob += lpSum([player_vars[player] for player in lineup]) <= max_overlap

print("Max points: {0}".format(max_points))

Stack: QB_WR_TE_0. Pos: QB, WR, TE. Opp Pos: 
Stack: RB_WR_-WR_1. Pos: RB, WR. Opp Pos: WR
Lineup 0
Actual week score: 179.70000000000002
                  player position team  opp  home_team  points_actual  salary  \
3               Panthers        D  CAR  JAX       True           14.0  2600.0   
51             Matt Ryan       QB  ATL  HOU      False           35.9  5900.0   
74   Christian McCaffrey       RB  CAR  JAX       True           50.7  8700.0   
79         Austin Ekeler       RB  LAC  DEN       True           23.3  6700.0   
149        Austin Hooper       TE  ATL  HOU      False           13.6  4500.0   
221         Keenan Allen       WR  LAC  DEN       True            5.8  7300.0   
238     Courtland Sutton       WR  DEN  LAC      False           19.2  4900.0   
241         Mohamed Sanu       WR  ATL  HOU      False           15.3  4200.0   
288     Emmanuel Sanders       WR  DEN  LAC      False            1.9  5100.0   

     points_projected  sdPts_projected  tier   play

Actual week score: 138.34
                  player position team  opp  home_team  points_actual  salary  \
21            Buccaneers        D   TB   NO      False           1.00  2200.0   
39            Kyle Allen       QB  CAR  JAX       True          11.64  5100.0   
74   Christian McCaffrey       RB  CAR  JAX       True          50.70  8700.0   
92       Phillip Lindsay       RB  DEN  LAC      False          27.70  4900.0   
178           Greg Olsen       TE  CAR  JAX       True           0.00  4000.0   
218          Julio Jones       WR  ATL  HOU      False           7.20  7700.0   
221         Keenan Allen       WR  LAC  DEN       True           5.80  7300.0   
238     Courtland Sutton       WR  DEN  LAC      False          19.20  4900.0   
243           D.J. Moore       WR  CAR  JAX       True          15.10  5200.0   

     points_projected  sdPts_projected  tier   player_id  
21           6.330600         0.371351     5     D_TB_21  
39          14.133900         1.285893     7 

Actual week score: 153.76
               player position team  opp  home_team  points_actual  salary  \
7             Vikings        D  MIN  NYG      False          12.00  3200.0   
35     Jameis Winston       QB   TB   NO      False          17.46  6200.0   
79      Austin Ekeler       RB  LAC  DEN       True          23.30  6700.0   
92    Phillip Lindsay       RB  DEN  LAC      False          27.70  4900.0   
177       O.J. Howard       TE   TB   NO      False           2.00  3900.0   
221      Keenan Allen       WR  LAC  DEN       True           5.80  7300.0   
225  Larry Fitzgerald       WR  ARI  CIN      False          11.80  6000.0   
231      Chris Godwin       WR   TB   NO      False          34.50  6900.0   
238  Courtland Sutton       WR  DEN  LAC      False          19.20  4900.0   

     points_projected  sdPts_projected  tier   player_id  
7            8.266571         1.261948     3     D_MIN_7  
35          19.687121         1.045910     3    QB_TB_35  
79          18.9

Actual week score: 165.46
                  player position team  opp  home_team  points_actual  salary  \
7                Vikings        D  MIN  NYG      False          12.00  3200.0   
38          Carson Wentz       QB  PHI  NYJ       True          12.06  6100.0   
74   Christian McCaffrey       RB  CAR  JAX       True          50.70  8700.0   
79         Austin Ekeler       RB  LAC  DEN       True          23.30  6700.0   
146            Zach Ertz       TE  PHI  NYJ       True          16.70  6000.0   
238     Courtland Sutton       WR  DEN  LAC      False          19.20  4900.0   
243           D.J. Moore       WR  CAR  JAX       True          15.10  5200.0   
244        Mike Williams       WR  LAC  DEN       True          13.40  4500.0   
279       Nelson Agholor       WR  PHI  NYJ       True           3.00  4700.0   

     points_projected  sdPts_projected  tier   player_id  
7            8.266571         1.261948     3     D_MIN_7  
38          20.893943         1.091786     2 

Actual week score: 190.94
                  player position team  opp  home_team  points_actual  salary  \
5               Chargers        D  LAC  DEN       True          14.00  2700.0   
46         Philip Rivers       QB  LAC  DEN       True           6.14  5800.0   
74   Christian McCaffrey       RB  CAR  JAX       True          50.70  8700.0   
79         Austin Ekeler       RB  LAC  DEN       True          23.30  6700.0   
162      Lance Kendricks       TE  LAC  DEN       True           0.00  2700.0   
217        Curtis Samuel       WR  CAR  JAX       True           7.40  4500.0   
221         Keenan Allen       WR  LAC  DEN       True           5.80  7300.0   
227       Michael Thomas       WR   NO   TB       True          44.20  6600.0   
229           D.J. Chark       WR  JAX  CAR      False          39.40  5000.0   

     points_projected  sdPts_projected  tier   player_id  
5            7.144857         0.651979     4     D_LAC_5  
46          18.637350         1.038435     4 

KeyboardInterrupt: 

In [169]:
pos_max = {
    "QB": 1,
    "RB": 3,
    "WR": 4,
    "TE": 1,
    "D": 1
}

pos_min = {
    "QB": 1,
    "RB": 2,
    "WR": 3,
    "TE": 1,
    "D": 1
}

no_d_vs_off =[["QB", "D"], ["WR", "D"], ["RB", "D"], ["TE", "D"]]
prob, player_vars = get_basic_dfs_solver(df, pos_max, pos_min, proj_type='avg',
                                         opposing_player_exclusions=no_d_vs_off,
                                         stacks=[["QB", "WR", "TE"], ["RB", "WR", "-WR"]],
                                         use_actual_points=False,
                                         point_diff_for_identical=10, 
                                         max_per_team=4)

df = df[~df.player.isin(["Pharoh Cooper", "Luke Willson"])].reset_index(drop=True)
num_lineups = 150
max_qb_exposure = 1.0
max_lineups_for_one_qb = int(math.ceil(num_lineups*max_qb_exposure))
qb_exposure = {}

max_points = -1
max_overlap = 3
for i in range(num_lineups):
    print("Lineup {0}".format(i))
    prob.solve()
    score_df = output_performance(prob, df, print_points_actual=True)
    print(score_df)
    lineup = score_df.player_id.tolist()
    if score_df.points_actual.sum() > max_points:
        max_points = score_df.points_actual.sum()
    
    # See if we need to remove QB from consideration
    qb = score_df[score_df.position == "QB"].player_id.tolist()[0]
    if qb in qb_exposure:
        qb_exposure[qb] += 1
    else:
        qb_exposure[qb] = 1
    
    # If QB reaches max exposure remove from future lineups
    if qb_exposure[qb] >= max_lineups_for_one_qb:
        print("Reached lineup exposure max for QB: {0}".format(qb))
        prob += player_vars[qb] == 0
    
    print("Best lineup to point: {0}".format(max_points))
    prob += lpSum([player_vars[player] for player in lineup]) <= max_overlap

print("Max points: {0}".format(max_points))

Stack: QB_WR_TE_0. Pos: QB, WR, TE. Opp Pos: 
Stack: RB_WR_-WR_1. Pos: RB, WR. Opp Pos: WR
Lineup 0
Actual week score: 185.7
                  player position team  opp  home_team  points_actual  salary  \
3               Panthers        D  CAR  JAX       True           14.0  2600.0   
51             Matt Ryan       QB  ATL  HOU      False           35.9  5900.0   
74   Christian McCaffrey       RB  CAR  JAX       True           50.7  8700.0   
92       Phillip Lindsay       RB  DEN  LAC      False           27.7  4900.0   
149        Austin Hooper       TE  ATL  HOU      False           13.6  4500.0   
218          Julio Jones       WR  ATL  HOU      False            7.2  7700.0   
221         Keenan Allen       WR  LAC  DEN       True            5.8  7300.0   
224           Auden Tate       WR  CIN  ARI       True           11.6  3500.0   
238     Courtland Sutton       WR  DEN  LAC      False           19.2  4900.0   

     points_projected  sdPts_projected  tier   player_id  
3    

Actual week score: 162.74
                player position team  opp  home_team  points_actual  salary  \
19                Jets        D  NYJ  PHI      False           4.00  2300.0   
37       Lamar Jackson       QB  BAL  PIT      False          14.44  7100.0   
78   Leonard Fournette       RB  JAX  CAR      False          26.70  6400.0   
92     Phillip Lindsay       RB  DEN  LAC      False          27.70  4900.0   
144       Mark Andrews       TE  BAL  PIT      False           9.50  4800.0   
205     Marquise Brown       WR  BAL  PIT      False          11.20  5700.0   
221       Keenan Allen       WR  LAC  DEN       True           5.80  7300.0   
227     Michael Thomas       WR   NO   TB       True          44.20  6600.0   
238   Courtland Sutton       WR  DEN  LAC      False          19.20  4900.0   

     points_projected  sdPts_projected  tier   player_id  
19           5.240800         0.769853     6    D_NYJ_19  
37          21.352324         1.156883     2   QB_BAL_37  
78    

Actual week score: 112.26
               player position team  opp  home_team  points_actual  salary  \
21         Buccaneers        D   TB   NO      False           1.00  2200.0   
35     Jameis Winston       QB   TB   NO      False          17.46  6200.0   
79      Austin Ekeler       RB  LAC  DEN       True          23.30  6700.0   
87       Le'Veon Bell       RB  NYJ  PHI      False          15.80  6800.0   
92    Phillip Lindsay       RB  DEN  LAC      False          27.70  4900.0   
177       O.J. Howard       TE   TB   NO      False           2.00  3900.0   
221      Keenan Allen       WR  LAC  DEN       True           5.80  7300.0   
238  Courtland Sutton       WR  DEN  LAC      False          19.20  4900.0   
262        Mike Evans       WR   TB   NO      False           0.00  7100.0   

     points_projected  sdPts_projected  tier   player_id  
21           6.330600         0.371351     5     D_TB_21  
35          19.687121         1.045910     3    QB_TB_35  
79          18.9

Actual week score: 238.74000000000004
                  player position team  opp  home_team  points_actual  salary  \
13                Titans        D  TEN  BUF       True           7.00  3000.0   
26        Deshaun Watson       QB  HOU  ATL       True          44.74  6700.0   
74   Christian McCaffrey       RB  CAR  JAX       True          50.70  8700.0   
92       Phillip Lindsay       RB  DEN  LAC      False          27.70  4900.0   
147         Darren Fells       TE  HOU  ATL       True          16.00  2900.0   
227       Michael Thomas       WR   NO   TB       True          44.20  6600.0   
238     Courtland Sutton       WR  DEN  LAC      False          19.20  4900.0   
240      DeAndre Hopkins       WR  HOU  ATL       True          15.80  7800.0   
244        Mike Williams       WR  LAC  DEN       True          13.40  4500.0   

     points_projected  sdPts_projected  tier   player_id  
13           8.390857         0.692414     3    D_TEN_13  
26          21.742100         0.6

Actual week score: 192.9
              player position team  opp  home_team  points_actual  salary  \
7            Vikings        D  MIN  NYG      False           12.0  3200.0   
51         Matt Ryan       QB  ATL  HOU      False           35.9  5900.0   
53         Joe Mixon       RB  CIN  ARI       True           11.9  6100.0   
73       Aaron Jones       RB   GB  DAL      False           52.2  5900.0   
79     Austin Ekeler       RB  LAC  DEN       True           23.3  6700.0   
149    Austin Hooper       TE  ATL  HOU      False           13.6  4500.0   
218      Julio Jones       WR  ATL  HOU      False            7.2  7700.0   
223  KeeSean Johnson       WR  ARI  CIN      False            5.5  3500.0   
232       Tyler Boyd       WR  CIN  ARI       True           31.3  6500.0   

     points_projected  sdPts_projected  tier   player_id  
7            8.266571         1.261948     3     D_MIN_7  
51          20.040986         0.870382     3   QB_ATL_51  
53          16.179363      

Actual week score: 97.58000000000001
               player position team  opp  home_team  points_actual  salary  \
3            Panthers        D  CAR  JAX       True          14.00  2600.0   
41         Joe Flacco       QB  DEN  LAC      False           9.98  4700.0   
79      Austin Ekeler       RB  LAC  DEN       True          23.30  6700.0   
83    Devonta Freeman       RB  ATL  HOU      False          18.00  5300.0   
180         Noah Fant       TE  DEN  LAC      False           1.60  2800.0   
218       Julio Jones       WR  ATL  HOU      False           7.20  7700.0   
221      Keenan Allen       WR  LAC  DEN       True           5.80  7300.0   
240   DeAndre Hopkins       WR  HOU  ATL       True          15.80  7800.0   
288  Emmanuel Sanders       WR  DEN  LAC      False           1.90  5100.0   

     points_projected  sdPts_projected  tier   player_id  
3            8.296286         0.735724     3     D_CAR_3  
41          14.472910         0.808361     7   QB_DEN_41  
79   

Actual week score: 187.96
                  player position team  opp  home_team  points_actual  salary  \
9               Steelers        D  PIT  BAL       True          11.00  2100.0   
39            Kyle Allen       QB  CAR  JAX       True          11.64  5100.0   
74   Christian McCaffrey       RB  CAR  JAX       True          50.70  8700.0   
86          Alvin Kamara       RB   NO   TB       True          16.92  8600.0   
178           Greg Olsen       TE  CAR  JAX       True           0.00  4000.0   
217        Curtis Samuel       WR  CAR  JAX       True           7.40  4500.0   
224           Auden Tate       WR  CIN  ARI       True          11.60  3500.0   
227       Michael Thomas       WR   NO   TB       True          44.20  6600.0   
231         Chris Godwin       WR   TB   NO      False          34.50  6900.0   

     points_projected  sdPts_projected  tier   player_id  
9            6.677600         0.946350     4     D_PIT_9  
39          14.133900         1.285893     7 

Actual week score: 162.4
                player position team  opp  home_team  points_actual  salary  \
21          Buccaneers        D   TB   NO      False            1.0  2200.0   
51           Matt Ryan       QB  ATL  HOU      False           35.9  5900.0   
76         Dalvin Cook       RB  MIN  NYG      False           29.8  8400.0   
78   Leonard Fournette       RB  JAX  CAR      False           26.7  6400.0   
122      Wayne Gallman       RB  NYG  MIN       True            1.4  5400.0   
149      Austin Hooper       TE  ATL  HOU      False           13.6  4500.0   
217      Curtis Samuel       WR  CAR  JAX       True            7.4  4500.0   
218        Julio Jones       WR  ATL  HOU      False            7.2  7700.0   
229         D.J. Chark       WR  JAX  CAR      False           39.4  5000.0   

     points_projected  sdPts_projected  tier   player_id  
21           6.330600         0.371351     5     D_TB_21  
51          20.040986         0.870382     3   QB_ATL_51  
76     

KeyboardInterrupt: 

In [171]:
pos_max = {
    "QB": 1,
    "RB": 2,
    "WR": 4,
    "TE": 1,
    "D": 1
}

pos_min = {
    "QB": 1,
    "RB": 2,
    "WR": 4,
    "TE": 1,
    "D": 1
}

no_d_vs_off =[["QB", "D"], ["WR", "D"], ["RB", "D"], ["TE", "D"]]
prob, player_vars = get_basic_dfs_solver(df, pos_max, pos_min, proj_type='avg',
                                         opposing_player_exclusions=no_d_vs_off,
                                         stacks=[["QB", "WR", "TE"], ["RB", "WR", "-WR"]],
                                         use_actual_points=False,
                                         point_diff_for_identical=10, 
                                         max_per_team=4)

df = df[~df.player.isin(["Pharoh Cooper", "Luke Willson"])].reset_index(drop=True)
num_lineups = 150
max_qb_exposure = 1.0
max_lineups_for_one_qb = int(math.ceil(num_lineups*max_qb_exposure))
qb_exposure = {}

max_points = -1
max_overlap = 4
for i in range(num_lineups):
    print("Lineup {0}".format(i))
    prob.solve()
    score_df = output_performance(prob, df, print_points_actual=True)
    print(score_df)
    lineup = score_df.player_id.tolist()
    if score_df.points_actual.sum() > max_points:
        max_points = score_df.points_actual.sum()
    
    # See if we need to remove QB from consideration
    qb = score_df[score_df.position == "QB"].player_id.tolist()[0]
    if qb in qb_exposure:
        qb_exposure[qb] += 1
    else:
        qb_exposure[qb] = 1
    
    # If QB reaches max exposure remove from future lineups
    if qb_exposure[qb] >= max_lineups_for_one_qb:
        print("Reached lineup exposure max for QB: {0}".format(qb))
        prob += player_vars[qb] == 0
    
    print("Best lineup to point: {0}".format(max_points))
    prob += lpSum([player_vars[player] for player in lineup]) <= max_overlap

print("Max points: {0}".format(max_points))

Stack: QB_WR_TE_0. Pos: QB, WR, TE. Opp Pos: 
Stack: RB_WR_-WR_1. Pos: RB, WR. Opp Pos: WR
Lineup 0
Actual week score: 185.7
                  player position team  opp  home_team  points_actual  salary  \
3               Panthers        D  CAR  JAX       True           14.0  2600.0   
51             Matt Ryan       QB  ATL  HOU      False           35.9  5900.0   
74   Christian McCaffrey       RB  CAR  JAX       True           50.7  8700.0   
92       Phillip Lindsay       RB  DEN  LAC      False           27.7  4900.0   
149        Austin Hooper       TE  ATL  HOU      False           13.6  4500.0   
218          Julio Jones       WR  ATL  HOU      False            7.2  7700.0   
221         Keenan Allen       WR  LAC  DEN       True            5.8  7300.0   
224           Auden Tate       WR  CIN  ARI       True           11.6  3500.0   
238     Courtland Sutton       WR  DEN  LAC      False           19.2  4900.0   

     points_projected  sdPts_projected  tier   player_id  
3    

Actual week score: 182.66
                player position team  opp  home_team  points_actual  salary  \
9             Steelers        D  PIT  BAL       True          11.00  2100.0   
38        Carson Wentz       QB  PHI  NYJ       True          12.06  6100.0   
78   Leonard Fournette       RB  JAX  CAR      False          26.70  6400.0   
79       Austin Ekeler       RB  LAC  DEN       True          23.30  6700.0   
146          Zach Ertz       TE  PHI  NYJ       True          16.70  6000.0   
204     Alshon Jeffery       WR  PHI  NYJ       True          11.20  5900.0   
221       Keenan Allen       WR  LAC  DEN       True           5.80  7300.0   
226        Will Fuller       WR  HOU  ATL       True          56.70  4500.0   
238   Courtland Sutton       WR  DEN  LAC      False          19.20  4900.0   

     points_projected  sdPts_projected  tier   player_id  
9            6.677600         0.946350     4     D_PIT_9  
38          20.893943         1.091786     2   QB_PHI_38  
78    

Actual week score: 164.99999999999997
                player position team  opp  home_team  points_actual  salary  \
13              Titans        D  TEN  BUF       True            7.0  3000.0   
51           Matt Ryan       QB  ATL  HOU      False           35.9  5900.0   
78   Leonard Fournette       RB  JAX  CAR      False           26.7  6400.0   
82       David Johnson       RB  ARI  CIN      False           18.6  7500.0   
149      Austin Hooper       TE  ATL  HOU      False           13.6  4500.0   
218        Julio Jones       WR  ATL  HOU      False            7.2  7700.0   
223    KeeSean Johnson       WR  ARI  CIN      False            5.5  3500.0   
232         Tyler Boyd       WR  CIN  ARI       True           31.3  6500.0   
238   Courtland Sutton       WR  DEN  LAC      False           19.2  4900.0   

     points_projected  sdPts_projected  tier   player_id  
13           8.390857         0.692414     3    D_TEN_13  
51          20.040986         0.870382     3   QB_ATL

Actual week score: 150.84
               player position team  opp  home_team  points_actual  salary  \
3            Panthers        D  CAR  JAX       True          14.00  2600.0   
26     Deshaun Watson       QB  HOU  ATL       True          44.74  6700.0   
82      David Johnson       RB  ARI  CIN      False          18.60  7500.0   
92    Phillip Lindsay       RB  DEN  LAC      False          27.70  4900.0   
131      Jordan Akins       TE  HOU  ATL       True           3.10  3200.0   
221      Keenan Allen       WR  LAC  DEN       True           5.80  7300.0   
238  Courtland Sutton       WR  DEN  LAC      False          19.20  4900.0   
240   DeAndre Hopkins       WR  HOU  ATL       True          15.80  7800.0   
288  Emmanuel Sanders       WR  DEN  LAC      False           1.90  5100.0   

     points_projected  sdPts_projected  tier   player_id  
3            8.296286         0.735724     3     D_CAR_3  
26          21.742100         0.679768     2   QB_HOU_26  
82          20.5

Actual week score: 205.2
                  player position team  opp  home_team  points_actual  salary  \
9               Steelers        D  PIT  BAL       True           11.0  2100.0   
51             Matt Ryan       QB  ATL  HOU      False           35.9  5900.0   
74   Christian McCaffrey       RB  CAR  JAX       True           50.7  8700.0   
87          Le'Veon Bell       RB  NYJ  PHI      False           15.8  6800.0   
149        Austin Hooper       TE  ATL  HOU      False           13.6  4500.0   
204       Alshon Jeffery       WR  PHI  NYJ       True           11.2  5900.0   
227       Michael Thomas       WR   NO   TB       True           44.2  6600.0   
246        Calvin Ridley       WR  ATL  HOU      False           19.8  4900.0   
281      Jamison Crowder       WR  NYJ  PHI      False            3.0  4300.0   

     points_projected  sdPts_projected  tier   player_id  
9            6.677600         0.946350     4     D_PIT_9  
51          20.040986         0.870382     3  

KeyboardInterrupt: 

In [186]:
def jitter_player_point_model(prob, df, player_vars):
    def jitter_pts(row):
        points = row["points_projected"]
        sd = row["sdPts_projected"]
        return np.random.normal(points, sd, 1)[0]

    df["points_jitter"] = df.apply(jitter_pts, axis=1)
    player_dict = get_player_attribute_dict(df, "points_jitter")
    prob += lpSum([player_vars[player]*player_dict[player] for player in player_vars])
    return prob

In [189]:
pos_max = {
    "QB": 1,
    "RB": 2,
    "WR": 4,
    "TE": 1,
    "D": 1
}

pos_min = {
    "QB": 1,
    "RB": 2,
    "WR": 4,
    "TE": 1,
    "D": 1
}

no_d_vs_off =[["QB", "D"], ["WR", "D"], ["RB", "D"], ["TE", "D"]]
prob, player_vars = get_basic_dfs_solver(df, pos_max, pos_min, proj_type='avg',
                                         opposing_player_exclusions=no_d_vs_off,
                                         stacks=[["QB", "WR", "TE"], ["WR", "RB", "-WR"]],
                                         use_actual_points=False,
                                         point_diff_for_identical=10, 
                                         max_per_team=4)

df = df[~df.player.isin(["Pharoh Cooper", "Luke Willson"])].reset_index(drop=True)
num_lineups = 100
max_qb_exposure = 1.0
max_lineups_for_one_qb = int(math.ceil(num_lineups*max_qb_exposure))
qb_exposure = {}

max_points = -1
max_overlap = 4
for i in range(num_lineups):
    print("Lineup {0}".format(i))
    prob.solve()
    score_df = output_performance(prob, df, print_points_actual=True)
    print(score_df)
    lineup = score_df.player_id.tolist()
    if score_df.points_actual.sum() > max_points:
        max_points = score_df.points_actual.sum()
    
    # See if we need to remove QB from consideration
    qb = score_df[score_df.position == "QB"].player_id.tolist()[0]
    if qb in qb_exposure:
        qb_exposure[qb] += 1
    else:
        qb_exposure[qb] = 1
    
    # If QB reaches max exposure remove from future lineups
    if qb_exposure[qb] >= max_lineups_for_one_qb:
        print("Reached lineup exposure max for QB: {0}".format(qb))
        prob += player_vars[qb] == 0
    
    print("Best lineup to point: {0}".format(max_points))
    prob += lpSum([player_vars[player] for player in lineup]) <= max_overlap
    
    if i%2 == 0:
        jitter_player_point_model(prob, df, player_vars)

print("Max points: {0}".format(max_points))

Stack: QB_WR_TE_0. Pos: QB, WR, TE. Opp Pos: 
Stack: WR_RB_-WR_1. Pos: WR, RB. Opp Pos: WR
Lineup 0
Actual week score: 185.7
                  player position team  opp  home_team  points_actual  salary  \
3               Panthers        D  CAR  JAX       True           14.0  2600.0   
51             Matt Ryan       QB  ATL  HOU      False           35.9  5900.0   
74   Christian McCaffrey       RB  CAR  JAX       True           50.7  8700.0   
92       Phillip Lindsay       RB  DEN  LAC      False           27.7  4900.0   
149        Austin Hooper       TE  ATL  HOU      False           13.6  4500.0   
218          Julio Jones       WR  ATL  HOU      False            7.2  7700.0   
221         Keenan Allen       WR  LAC  DEN       True            5.8  7300.0   
224           Auden Tate       WR  CIN  ARI       True           11.6  3500.0   
238     Courtland Sutton       WR  DEN  LAC      False           19.2  4900.0   

     points_projected  sdPts_projected  tier   player_id  points

Actual week score: 184.5
                  player position team  opp  home_team  points_actual  salary  \
22               Bengals        D  CIN  ARI       True            1.0  2500.0   
51             Matt Ryan       QB  ATL  HOU      False           35.9  5900.0   
74   Christian McCaffrey       RB  CAR  JAX       True           50.7  8700.0   
107        Miles Sanders       RB  PHI  NYJ       True           10.4  4500.0   
149        Austin Hooper       TE  ATL  HOU      False           13.6  4500.0   
205       Marquise Brown       WR  BAL  PIT      False           11.2  5700.0   
218          Julio Jones       WR  ATL  HOU      False            7.2  7700.0   
229           D.J. Chark       WR  JAX  CAR      False           39.4  5000.0   
243           D.J. Moore       WR  CAR  JAX       True           15.1  5200.0   

     points_projected  sdPts_projected  tier   player_id  points_jitter  
22           7.323000         0.662564     4    D_CIN_22       7.372418  
51          20.0

Actual week score: 141.56
               player position team  opp  home_team  points_actual  salary  \
9            Steelers        D  PIT  BAL       True          11.00  2100.0   
35     Jameis Winston       QB   TB   NO      False          17.46  6200.0   
79      Austin Ekeler       RB  LAC  DEN       True          23.30  6700.0   
87       Le'Veon Bell       RB  NYJ  PHI      False          15.80  6800.0   
177       O.J. Howard       TE   TB   NO      False           2.00  3900.0   
221      Keenan Allen       WR  LAC  DEN       True           5.80  7300.0   
231      Chris Godwin       WR   TB   NO      False          34.50  6900.0   
238  Courtland Sutton       WR  DEN  LAC      False          19.20  4900.0   
245        John Brown       WR  BUF  TEN      False          12.50  5100.0   

     points_projected  sdPts_projected  tier   player_id  points_jitter  
9            6.677600         0.946350     4     D_PIT_9       7.296756  
35          19.687121         1.045910     3 

Actual week score: 176.18
               player position team  opp  home_team  points_actual  salary  \
13             Titans        D  TEN  BUF       True           7.00  3000.0   
33        Andy Dalton       QB  CIN  ARI       True          18.98  5700.0   
82      David Johnson       RB  ARI  CIN      False          18.60  7500.0   
92    Phillip Lindsay       RB  DEN  LAC      False          27.70  4900.0   
137      Tyler Eifert       TE  CIN  ARI       True           3.40  3300.0   
221      Keenan Allen       WR  LAC  DEN       True           5.80  7300.0   
227    Michael Thomas       WR   NO   TB       True          44.20  6600.0   
232        Tyler Boyd       WR  CIN  ARI       True          31.30  6500.0   
238  Courtland Sutton       WR  DEN  LAC      False          19.20  4900.0   

     points_projected  sdPts_projected  tier   player_id  points_jitter  
13           8.390857         0.692414     3    D_TEN_13       8.073825  
33          17.611007         0.806765     5 

Actual week score: 192.44
               player position team  opp  home_team  points_actual  salary  \
3            Panthers        D  CAR  JAX       True          14.00  2600.0   
26     Deshaun Watson       QB  HOU  ATL       True          44.74  6700.0   
82      David Johnson       RB  ARI  CIN      False          18.60  7500.0   
92    Phillip Lindsay       RB  DEN  LAC      False          27.70  4900.0   
147      Darren Fells       TE  HOU  ATL       True          16.00  2900.0   
225  Larry Fitzgerald       WR  ARI  CIN      False          11.80  6000.0   
232        Tyler Boyd       WR  CIN  ARI       True          31.30  6500.0   
240   DeAndre Hopkins       WR  HOU  ATL       True          15.80  7800.0   
245        John Brown       WR  BUF  TEN      False          12.50  5100.0   

     points_projected  sdPts_projected  tier   player_id  points_jitter  
3            8.296286         0.735724     3     D_CAR_3       8.759054  
26          21.742100         0.679768     2 

...

Actual week score: 166.3
               player position team  opp  home_team  points_actual  salary  \
2              Eagles        D  PHI  NYJ       True           35.0  3700.0   
51          Matt Ryan       QB  ATL  HOU      False           35.9  5900.0   
85    Ezekiel Elliott       RB  DAL   GB       True           17.1  8300.0   
108     Royce Freeman       RB  DEN  LAC      False            8.7  4600.0   
149     Austin Hooper       TE  ATL  HOU      False           13.6  4500.0   
204    Alshon Jeffery       WR  PHI  NYJ       True           11.2  5900.0   
221      Keenan Allen       WR  LAC  DEN       True            5.8  7300.0   
238  Courtland Sutton       WR  DEN  LAC      False           19.2  4900.0   
246     Calvin Ridley       WR  ATL  HOU      False           19.8  4900.0   

     points_projected  sdPts_projected  tier   player_id  points_jitter  
2            7.975429         1.567577     3     D_PHI_2       9.438988  
51          20.040986         0.870382     3  

Actual week score: 176.12000000000003
               player position team  opp  home_team  points_actual  salary  \
3            Panthers        D  CAR  JAX       True          14.00  2600.0   
28       Dak Prescott       QB  DAL   GB       True          29.22  6000.0   
73        Aaron Jones       RB   GB  DAL      False          52.20  5900.0   
108     Royce Freeman       RB  DEN  LAC      False           8.70  4600.0   
141      Jason Witten       TE  DAL   GB       True           5.90  3800.0   
221      Keenan Allen       WR  LAC  DEN       True           5.80  7300.0   
228      Amari Cooper       WR  DAL   GB       True          42.60  6800.0   
240   DeAndre Hopkins       WR  HOU  ATL       True          15.80  7800.0   
288  Emmanuel Sanders       WR  DEN  LAC      False           1.90  5100.0   

     points_projected  sdPts_projected  tier   player_id  points_jitter  
3            8.296286         0.735724     3     D_CAR_3       8.597144  
28          19.504836         1.2

Actual week score: 179.74
                  player position team  opp  home_team  points_actual  salary  \
3               Panthers        D  CAR  JAX       True          14.00  2600.0   
37         Lamar Jackson       QB  BAL  PIT      False          14.44  7100.0   
74   Christian McCaffrey       RB  CAR  JAX       True          50.70  8700.0   
82         David Johnson       RB  ARI  CIN      False          18.60  7500.0   
144         Mark Andrews       TE  BAL  PIT      False           9.50  4800.0   
205       Marquise Brown       WR  BAL  PIT      False          11.20  5700.0   
223      KeeSean Johnson       WR  ARI  CIN      False           5.50  3500.0   
224           Auden Tate       WR  CIN  ARI       True          11.60  3500.0   
227       Michael Thomas       WR   NO   TB       True          44.20  6600.0   

     points_projected  sdPts_projected  tier   player_id  points_jitter  
3            8.296286         0.735724     3     D_CAR_3       8.445251  
37          21.

Actual week score: 139.73999999999998
                player position team  opp  home_team  points_actual  salary  \
13              Titans        D  TEN  BUF       True           7.00  3000.0   
37       Lamar Jackson       QB  BAL  PIT      False          14.44  7100.0   
52    David Montgomery       RB  CHI  OAK      False          10.60  5200.0   
78   Leonard Fournette       RB  JAX  CAR      False          26.70  6400.0   
144       Mark Andrews       TE  BAL  PIT      False           9.50  4800.0   
205     Marquise Brown       WR  BAL  PIT      False          11.20  5700.0   
221       Keenan Allen       WR  LAC  DEN       True           5.80  7300.0   
229         D.J. Chark       WR  JAX  CAR      False          39.40  5000.0   
243         D.J. Moore       WR  CAR  JAX       True          15.10  5200.0   

     points_projected  sdPts_projected  tier   player_id  points_jitter  
13           8.390857         0.692414     3    D_TEN_13       8.921685  
37          21.352324  

KeyboardInterrupt: 

In [192]:
pos_max = {
    "QB": 1,
    "RB": 2,
    "WR": 4,
    "TE": 1,
    "D": 1
}

pos_min = {
    "QB": 1,
    "RB": 2,
    "WR": 4,
    "TE": 1,
    "D": 1
}

no_d_vs_off =[["QB", "D"], ["WR", "D"], ["RB", "D"], ["TE", "D"]]
prob, player_vars = get_basic_dfs_solver(df, pos_max, pos_min, proj_type='avg',
                                         opposing_player_exclusions=no_d_vs_off,
                                         stacks=[["QB", "WR", "TE"], ["WR", "-WR", "RB"]],
                                         use_actual_points=False,
                                         point_diff_for_identical=0, 
                                         max_per_team=4)

df = df[~df.player.isin(["Pharoh Cooper", "Luke Willson"])].reset_index(drop=True)
num_lineups = 200
max_qb_exposure = 1.0
max_lineups_for_one_qb = int(math.ceil(num_lineups*max_qb_exposure))
qb_exposure = {}

max_points = -1
max_overlap = 4
for i in range(num_lineups):
    print("Lineup {0}".format(i))
    prob.solve()
    score_df = output_performance(prob, df, print_points_actual=True)
    print(score_df)
    lineup = score_df.player_id.tolist()
    if score_df.points_actual.sum() > max_points:
        max_points = score_df.points_actual.sum()
    
    # See if we need to remove QB from consideration
    qb = score_df[score_df.position == "QB"].player_id.tolist()[0]
    if qb in qb_exposure:
        qb_exposure[qb] += 1
    else:
        qb_exposure[qb] = 1
    
    # If QB reaches max exposure remove from future lineups
    if qb_exposure[qb] >= max_lineups_for_one_qb:
        print("Reached lineup exposure max for QB: {0}".format(qb))
        prob += player_vars[qb] == 0
    
    print("Best lineup to point: {0}".format(max_points))
    prob += lpSum([player_vars[player] for player in lineup]) <= max_overlap
    
    if i%2 == 0:
        jitter_player_point_model(prob, df, player_vars)

print("Max points: {0}".format(max_points))

Stack: QB_WR_TE_0. Pos: QB, WR, TE. Opp Pos: 
Stack: WR_-WR_RB_1. Pos: WR, RB. Opp Pos: WR
Lineup 0
Actual week score: 185.7
                  player position team  opp  home_team  points_actual  salary  \
3               Panthers        D  CAR  JAX       True           14.0  2600.0   
51             Matt Ryan       QB  ATL  HOU      False           35.9  5900.0   
74   Christian McCaffrey       RB  CAR  JAX       True           50.7  8700.0   
92       Phillip Lindsay       RB  DEN  LAC      False           27.7  4900.0   
149        Austin Hooper       TE  ATL  HOU      False           13.6  4500.0   
218          Julio Jones       WR  ATL  HOU      False            7.2  7700.0   
221         Keenan Allen       WR  LAC  DEN       True            5.8  7300.0   
224           Auden Tate       WR  CIN  ARI       True           11.6  3500.0   
238     Courtland Sutton       WR  DEN  LAC      False           19.2  4900.0   

     points_projected  sdPts_projected  tier   player_id  points

Actual week score: 140.54
               player position team  opp  home_team  points_actual  salary  \
13             Titans        D  TEN  BUF       True           7.00  3000.0   
26     Deshaun Watson       QB  HOU  ATL       True          44.74  6700.0   
79      Austin Ekeler       RB  LAC  DEN       True          23.30  6700.0   
107     Miles Sanders       RB  PHI  NYJ       True          10.40  4500.0   
131      Jordan Akins       TE  HOU  ATL       True           3.10  3200.0   
204    Alshon Jeffery       WR  PHI  NYJ       True          11.20  5900.0   
221      Keenan Allen       WR  LAC  DEN       True           5.80  7300.0   
238  Courtland Sutton       WR  DEN  LAC      False          19.20  4900.0   
240   DeAndre Hopkins       WR  HOU  ATL       True          15.80  7800.0   

     points_projected  sdPts_projected  tier   player_id  points_jitter  
13           8.390857         0.692414     3    D_TEN_13       7.919963  
26          21.742100         0.679768     2 

Actual week score: 117.22
                       player position team  opp  home_team  points_actual  \
4                    Patriots        D   NE  WAS      False          14.00   
42              Aaron Rodgers       QB   GB  DAL      False           9.42   
79              Austin Ekeler       RB  LAC  DEN       True          23.30   
104              Ronald Jones       RB   TB   NO      False           7.60   
157              Jimmy Graham       TE   GB  DAL      False           7.10   
221              Keenan Allen       WR  LAC  DEN       True           5.80   
234            Julian Edelman       WR   NE  WAS      False          28.00   
238          Courtland Sutton       WR  DEN  LAC      False          19.20   
292  Marquez Valdes-Scantling       WR   GB  DAL      False           2.80   

     salary  points_projected  sdPts_projected  tier   player_id  \
4    4300.0          9.998000         2.569489     2      D_NE_4   
42   6000.0         18.822329         0.993733     4    Q

Actual week score: 217.21999999999997
               player position team  opp  home_team  points_actual  salary  \
9            Steelers        D  PIT  BAL       True          11.00  2100.0   
28       Dak Prescott       QB  DAL   GB       True          29.22  6000.0   
73        Aaron Jones       RB   GB  DAL      False          52.20  5900.0   
79      Austin Ekeler       RB  LAC  DEN       True          23.30  6700.0   
141      Jason Witten       TE  DAL   GB       True           5.90  3800.0   
221      Keenan Allen       WR  LAC  DEN       True           5.80  7300.0   
228      Amari Cooper       WR  DAL   GB       True          42.60  6800.0   
234    Julian Edelman       WR   NE  WAS      False          28.00  6300.0   
238  Courtland Sutton       WR  DEN  LAC      False          19.20  4900.0   

     points_projected  sdPts_projected  tier   player_id  points_jitter  
9            6.677600         0.946350     4     D_PIT_9       7.555314  
28          19.504836         1.2

Actual week score: 151.96000000000004
                  player position team  opp  home_team  points_actual  salary  \
3               Panthers        D  CAR  JAX       True          14.00  2600.0   
34            Josh Allen       QB  BUF  TEN      False          18.46  5700.0   
74   Christian McCaffrey       RB  CAR  JAX       True          50.70  8700.0   
79         Austin Ekeler       RB  LAC  DEN       True          23.30  6700.0   
140          Dawson Knox       TE  BUF  TEN      False           3.20  3100.0   
221         Keenan Allen       WR  LAC  DEN       True           5.80  7300.0   
238     Courtland Sutton       WR  DEN  LAC      False          19.20  4900.0   
245           John Brown       WR  BUF  TEN      False          12.50  5100.0   
248     Geronimo Allison       WR   GB  DAL      False           4.80  5000.0   

     points_projected  sdPts_projected  tier   player_id  points_jitter  
3            8.296286         0.735724     3     D_CAR_3       9.623454  
34 

...

Actual week score: 215.32000000000005
                       player position team  opp  home_team  points_actual  \
3                    Panthers        D  CAR  JAX       True          14.00   
31               Kyler Murray       QB  ARI  CIN      False          25.42   
73                Aaron Jones       RB   GB  DAL      False          52.20   
82              David Johnson       RB  ARI  CIN      False          18.60   
142              Charles Clay       TE  ARI  CIN      False           3.70   
225          Larry Fitzgerald       WR  ARI  CIN      False          11.80   
227            Michael Thomas       WR   NO   TB       True          44.20   
228              Amari Cooper       WR  DAL   GB       True          42.60   
292  Marquez Valdes-Scantling       WR   GB  DAL      False           2.80   

     salary  points_projected  sdPts_projected  tier   player_id  \
3    2600.0          8.296286         0.735724     3     D_CAR_3   
31   6300.0         18.198507         1.31427

Actual week score: 159.84
                  player position team  opp  home_team  points_actual  salary  \
9               Steelers        D  PIT  BAL       True          11.00  2100.0   
43         Mason Rudolph       QB  PIT  BAL       True           9.24  5100.0   
76           Dalvin Cook       RB  MIN  NYG      False          29.80  8400.0   
78     Leonard Fournette       RB  JAX  CAR      False          26.70  6400.0   
143       Vance McDonald       TE  PIT  BAL       True           6.40  3800.0   
208     Sterling Shepard       WR  NYG  MIN       True           9.70  5800.0   
230         Adam Thielen       WR  MIN  NYG      False          35.00  6700.0   
237  JuJu Smith-Schuster       WR  PIT  BAL       True          19.50  6400.0   
245           John Brown       WR  BUF  TEN      False          12.50  5100.0   

     points_projected  sdPts_projected  tier   player_id  points_jitter  
9            6.677600         0.946350     4     D_PIT_9       7.067448  
43          15.

Actual week score: 177.14
               player position team  opp  home_team  points_actual  salary  \
4            Patriots        D   NE  WAS      False          14.00  4300.0   
26     Deshaun Watson       QB  HOU  ATL       True          44.74  6700.0   
52   David Montgomery       RB  CHI  OAK      False          10.60  5200.0   
73        Aaron Jones       RB   GB  DAL      False          52.20  5900.0   
131      Jordan Akins       TE  HOU  ATL       True           3.10  3200.0   
221      Keenan Allen       WR  LAC  DEN       True           5.80  7300.0   
233    Allen Robinson       WR  CHI  OAK      False          28.70  5600.0   
240   DeAndre Hopkins       WR  HOU  ATL       True          15.80  7800.0   
285    Hunter Renfrow       WR  OAK  CHI       True           2.20  4000.0   

     points_projected  sdPts_projected  tier   player_id  points_jitter  
4            9.998000         2.569489     2      D_NE_4      13.869928  
26          21.742100         0.679768     2 

Actual week score: 186.74
                  player position team  opp  home_team  points_actual  salary  \
9               Steelers        D  PIT  BAL       True          11.00  2100.0   
32          Kirk Cousins       QB  MIN  NYG      False          23.54  5300.0   
74   Christian McCaffrey       RB  CAR  JAX       True          50.70  8700.0   
89           James White       RB   NE  WAS      False          13.20  5000.0   
189         Kyle Rudolph       TE  MIN  NYG      False           1.40  3000.0   
222       Terry McLaurin       WR  WAS   NE       True           8.10  5100.0   
230         Adam Thielen       WR  MIN  NYG      False          35.00  6700.0   
234       Julian Edelman       WR   NE  WAS      False          28.00  6300.0   
240      DeAndre Hopkins       WR  HOU  ATL       True          15.80  7800.0   

     points_projected  sdPts_projected  tier   player_id  points_jitter  
9            6.677600         0.946350     4     D_PIT_9       7.631619  
32          15.

Actual week score: 134.85999999999999
                  player position team  opp  home_team  points_actual  salary  \
7                Vikings        D  MIN  NYG      False          12.00  3200.0   
35        Jameis Winston       QB   TB   NO      False          17.46  6200.0   
52      David Montgomery       RB  CHI  OAK      False          10.60  5200.0   
74   Christian McCaffrey       RB  CAR  JAX       True          50.70  8700.0   
177          O.J. Howard       TE   TB   NO      False           2.00  3900.0   
205       Marquise Brown       WR  BAL  PIT      False          11.20  5700.0   
233       Allen Robinson       WR  CHI  OAK      False          28.70  5600.0   
262           Mike Evans       WR   TB   NO      False           0.00  7100.0   
285       Hunter Renfrow       WR  OAK  CHI       True           2.20  4000.0   

     points_projected  sdPts_projected  tier   player_id  points_jitter  
7            8.266571         1.261948     3     D_MIN_7      11.123794  
35 